## Create Records

### Profile Creation  (from the records of the dataset)

Replace the name of the file.json of the dataset


In [10]:
import json
import os

# Load the JSON data
input_file = "C:/Users/sam/Documents/GitHub/dataingestion/output_dates_1.json"  # Path to your input file
output_folder = "C:/Users/sam/Documents/GitHub/dataingestion/records/"  # Folder to store the output files

# Ensure the output directory exists
os.makedirs(output_folder, exist_ok=True)

# Read the input JSON file
with open(input_file, "r", encoding="utf-8") as file:
    data = json.load(file)

# Export each profile to a separate JSON file
for record in data:
    title = record.get("title", "unknown").replace(" ", "_").lower()  # Generate a file-safe name
    output_file = os.path.join(output_folder, f"{title}.json")
    
    # Write the profile to a separate JSON file
    with open(output_file, "w", encoding="utf-8") as outfile:
        json.dump(record, outfile, indent=4, ensure_ascii=False)

print(f"Exported {len(data)} profiles to {output_folder}")


Exported 4 profiles to C:/Users/sam/Documents/GitHub/dataingestion/records/


## Check API authentification

In [2]:

import requests
import json
import urllib3

# Disable SSL warnings (only if you're working in a non-production environment)
urllib3.disable_warnings(urllib3.exceptions.InsecureRequestWarning)

# Define the API endpoint
api_url = "http://wikibase.example.com/w/api.php"  # Replace with your actual API URL

# Initialize session
session = requests.Session()

# Step 1: Retrieve the login token
params = {
    "action": "query",
    "meta": "tokens",
    "type": "login",
    "format": "json"
}

# Make the GET request to retrieve the login token
response = session.get(api_url, params=params, verify=False)

if response.status_code == 200:
    data = response.json()
    login_token = data['query']['tokens']['logintoken']
    print(f"Login Token: {login_token}")
else:
    print(f"Failed to retrieve login token. Status code: {response.status_code}")
    exit()

# Step 2: Log in using the login token
login_params = {
    "action": "clientlogin",
    "username": "admin",  # Replace with your username
    "password": "change-this-password",  # Replace with your password
    "logintoken": login_token,
    "loginreturnurl": "https://wikibase.example.com",  # Replace with your return URL
    "format": "json"
}

login_response = session.post(api_url, data=login_params, verify=False)

if login_response.status_code == 200:
    login_data = login_response.json()
    if login_data.get("clientlogin", {}).get("status") == "PASS":
        print("Logged in successfully!")
    else:
        print(f"Failed to log in: {login_data}")
        exit()
else:
    print(f"Login request failed with status code: {login_response.status_code}")
    exit()

# Step 3: Retrieve CSRF token
csrf_params = {
    "action": "query",
    "meta": "tokens",
    "type": "csrf",
    "format": "json"
}

csrf_response = session.get(api_url, params=csrf_params, verify=False)

if csrf_response.status_code == 200:
    csrf_data = csrf_response.json()
    csrf_token = csrf_data['query']['tokens']['csrftoken']
    print(f"CSRF Token: {csrf_token}")
else:
    print(f"Failed to retrieve CSRF token. Status code: {csrf_response.status_code}")
    exit()

# Optional: Save cookies to a file for later use
with open('cookies.txt', 'w') as f:
    cookies = session.cookies.get_dict()
    for key, value in cookies.items():
        f.write(f'{key}={value}\n')

# Now you can use `session` to make authenticated requests to the API



Login Token: 4663d043c30d6ec161479fa78f41fecf6751ac90+\
Logged in successfully!
CSRF Token: 939bf951707da6a65a8788c9b69d38706751ac90+\


In [3]:
import requests
import json
import urllib3

# Disable SSL warnings (only if you're working in a non-production environment)
urllib3.disable_warnings(urllib3.exceptions.InsecureRequestWarning)

# Define the API endpoint
api_url = "http://wikibase.example.com/w/api.php"  # Replace with your actual API URL

# Initialize session
session = requests.Session()

# Step 1: Retrieve the login token
params = {
    "action": "query",
    "meta": "tokens",
    "type": "login",
    "format": "json"
}

# Make the GET request to retrieve the login token
response = session.get(api_url, params=params, verify=False)

if response.status_code == 200:
    data = response.json()
    login_token = data['query']['tokens']['logintoken']
    print(f"Login Token: {login_token}")
else:
    print(f"Failed to retrieve login token. Status code: {response.status_code}")
    exit()

# Step 2: Log in using the login token
login_params = {
    "action": "clientlogin",
    "username": "admin",  # Replace with your username
    "password": "change-this-password",  # Replace with your password
    "logintoken": login_token,
    "loginreturnurl": "https://wikibase.example.com",  # Replace with your return URL
    "format": "json"
}

login_response = session.post(api_url, data=login_params, verify=False)

if login_response.status_code == 200:
    login_data = login_response.json()
    if login_data.get("clientlogin", {}).get("status") == "PASS":
        print("Logged in successfully!")
    else:
        print(f"Failed to log in: {login_data}")
        exit()
else:
    print(f"Login request failed with status code: {login_response.status_code}")
    exit()

# Step 3: Retrieve CSRF token
csrf_params = {
    "action": "query",
    "meta": "tokens",
    "type": "csrf",
    "format": "json"
}

csrf_response = session.get(api_url, params=csrf_params, verify=False)

if csrf_response.status_code == 200:
    csrf_data = csrf_response.json()
    csrf_token = csrf_data['query']['tokens']['csrftoken']
    print(f"CSRF Token: {csrf_token}")
else:
    print(f"Failed to retrieve CSRF token. Status code: {csrf_response.status_code}")
    exit()

# Step 4: Check if the entity exists
entity_id = "Q205"  # Replace with your actual entity ID
retrieve_params = {
    'action': 'wbgetentities',
    'ids': entity_id,
    'format': 'json'
}

retrieve_response = session.get(api_url, params=retrieve_params, verify=False)

if retrieve_response.status_code == 200:
    entity_data = retrieve_response.json()
    if 'entities' in entity_data and entity_id in entity_data['entities']:
        print(f"Entity {entity_id} exists. Proceeding with claim additions.")
    else:
        print(f"Entity {entity_id} does not exist. Please check the ID.")
        exit()
else:
    print(f"Failed to retrieve entity with status code: {retrieve_response.status_code}")
    exit()

# Step 5: Add a statement to the entity
property_id = "P53"  # Example property, e.g., "date of birth"
value = json.dumps({
    "entity-type": "time",
    "time": "+1980-05-10T00:00:00Z",
    "timezone": 0,
    "before": 0,
    "after": 0,
    "precision": 11,
    "calendarmodel": "http://www.wikidata.org/entity/Q1985727"
})

claim_params = {
    'action': 'wbcreateclaim',
    'entity': entity_id,
    'snaktype': 'value',
    'property': property_id,
    'value': value,
    'token': csrf_token,
    'format': 'json'
}

claim_response = session.post(api_url, data=claim_params, verify=False)

if claim_response.status_code == 200:
    claim_data = claim_response.json()
    print(f"Statement added successfully: {claim_data}")
else:
    print(f"Failed to add statement with status code: {claim_response.status_code}, Error: {claim_response.json()}")

Login Token: a249a7d1e3c5e1090586361be2ab6ab56751ac9a+\
Logged in successfully!
CSRF Token: 4332af6baf622db7b7f00b9b2b7871d66751ac9a+\
Entity Q205 exists. Proceeding with claim additions.
Statement added successfully: {'error': {'code': 'no-such-entity', 'info': '⧼no-such-entity⧽', 'messages': [{'name': 'no-such-entity', 'parameters': ['Q205'], 'html': {'*': '⧼no-such-entity⧽'}}], '*': 'See http://wikibase.example.com/w/api.php for API usage. Subscribe to the mediawiki-api-announce mailing list at &lt;https://lists.wikimedia.org/postorius/lists/mediawiki-api-announce.lists.wikimedia.org/&gt; for notice of API deprecations and breaking changes.'}}


### Create Properties


In [5]:
import requests
import json
import urllib3

# Disable SSL warnings (only if you're working in a non-production environment)
urllib3.disable_warnings(urllib3.exceptions.InsecureRequestWarning)

# Define the API endpoint
api_url = "https://wikibase.example.com/w/api.php"  # Replace with your actual API URL

# Initialize session
session = requests.Session()

# Step 1: Retrieve the login token
params = {
    "action": "query",
    "meta": "tokens",
    "type": "login",
    "format": "json"
}

# Make the GET request to retrieve the login token
response = session.get(api_url, params=params, verify=False)

if response.status_code == 200:
    data = response.json()
    login_token = data['query']['tokens']['logintoken']
    print(f"Login Token: {login_token}")
else:
    print(f"Failed to retrieve login token. Status code: {response.status_code}")
    exit()

# Step 2: Log in using the login token
login_params = {
    "action": "clientlogin",
    "username": "admin",  # Replace with your username
    "password": "change-this-password",  # Replace with your password
    "logintoken": login_token,
    "loginreturnurl": "https://wikibase.example.com",  # Replace with your return URL
    "format": "json"
}

login_response = session.post(api_url, data=login_params, verify=False)

if login_response.status_code == 200:
    login_data = login_response.json()
    if login_data.get("clientlogin", {}).get("status") == "PASS":
        print("Logged in successfully!")
    else:
        print(f"Failed to log in: {login_data}")
        exit()
else:
    print(f"Login request failed with status code: {login_response.status_code}")
    exit()

# Step 3: Retrieve CSRF token
csrf_params = {
    "action": "query",
    "meta": "tokens",
    "type": "csrf",
    "format": "json"
}

csrf_response = session.get(api_url, params=csrf_params, verify=False)

if csrf_response.status_code == 200:
    csrf_data = csrf_response.json()
    csrf_token = csrf_data['query']['tokens']['csrftoken']
    print(f"CSRF Token: {csrf_token}")
else:
    print(f"Failed to retrieve CSRF token. Status code: {csrf_response.status_code}")
    exit()

# Function to create a property with exponential backoff and retry mechanism
def create_property(label, description, datatype, max_retries=5):
    csrf_token = get_csrf_token()
    if csrf_token is None:
        print("Failed to retrieve CSRF token. Skipping property creation.")
        return

    property_data = {
        "action": "wbeditentity",
        "new": "property",
        "token": csrf_token,
        "format": "json",
        "data": json.dumps({
            "labels": {
                "en": {
                    "language": "en",
                    "value": label
                }
            },
            "descriptions": {
                "en": {
                    "language": "en",
                    "value": description
                }
            },
            "datatype": datatype
        }),
        "contentmodel": "json"
    }

    retries = 0
    while retries < max_retries:
        try:
            response = session.post(api_url, data=property_data, verify=False, timeout=15)  # Adding a 15-second timeout for the post request
            result = response.json()

            if response.status_code == 200:
                if 'entity' in result:
                    print(f"Property '{label}' created with ID: {result['entity']['id']}")
                    return
                else:
                    messages = result.get('error', {}).get('messages', [])
                    if any('wikibase-validator-label-conflict' in message.get('name', '') for message in messages):
                        print(f"Property '{label}' already exists. Skipping creation.")
                        return
                    else:
                        print(f"Failed to create property '{label}': {result}")
            else:
                print(f"Request failed with status code: {response.status_code}")

            # Handle retry on failure
            retries += 1
            sleep_time = 2 ** retries + random.uniform(0, 1)  # Exponential backoff with jitter
            print(f"Retrying in {sleep_time:.2f} seconds... (Attempt {retries}/{max_retries})")
            time.sleep(sleep_time)

        except requests.exceptions.Timeout:
            print(f"Property creation request for '{label}' timed out. Retrying...")
        except requests.exceptions.RequestException as e:
            print(f"An error occurred: {e}")
            retries += 1
            sleep_time = 2 ** retries + random.uniform(0, 1)  # Exponential backoff with jitter
            print(f"Retrying in {sleep_time:.2f} seconds... (Attempt {retries}/{max_retries})")
            time.sleep(sleep_time)
    
    print(f"Failed to create property '{label}' after {max_retries} attempts.")

# Define the properties to create based on the statements you provided
properties_to_create = {
    "P117": ("Household Organization", "A property to store the household organization as plain text", "string"),
    "P51": ("First Name", "A property to store the first name as plain text", "string"),
    "P52": ("Last Name", "A property to store the last name as plain text", "string"),
    "P142": ("Last Name Changed", "A property to store the last name after being changed (married name)", "string"),
    "P53": ("Birth Date", "A property to store the date of birth", "time"),
    "P54": ("Birth Place", "A property to store the place of birth", "string"),
    "P58": ("Death Place", "A property to store the place of death", "string"),
    "P55": ("Nationality", "A property to store nationality", "string"),
    "P166": ("Birth Country", "A property to store the country of birth", "string"),
    "P170": ("Death Date Notes", "A property to store any notes regarding the date of death", "string"),
    "P172": ("Alternative Death Place", "A property to store an alternative death place", "string"),
    "P173": ("Death Country", "A property to store the country of death", "string"),
    "P174": ("Alternative Death Country", "A property to store an alternative death country", "string"),
    "P177": ("Convoy", "A property to store the convoy information", "string"),
    "P178": ("Convoy Place", "A property to store the place related to convoy", "string"),
    "P179": ("Convoy Date", "A property to store the date of convoy", "time"),
    "P181": ("Enter Date", "A property to store the date of entry", "time"),
    "P184": ("Exit Place 1940-1941", "A property to store the exit place between 1940-1941", "string"),
    "P186": ("Exit Place 1941-1944", "A property to store the exit place between 1941-1944", "string"),
    "P189": ("Profession", "A property to store the profession", "string")
}

# Create the properties
for prop_id, (label, description, datatype) in properties_to_create.items():
    print(f"Creating property {label}...")
    create_property(label, description, datatype)
    time.sleep(5)  # Pause between requests to avoid hitting the rate limit

Login Token: 886100dfd99a31bb6ce5e537d866ee78670e6336+\
Logged in successfully!
CSRF Token: 65a56950f040582f431153416d7b82db670e6336+\
Creating property Household Organization...
Property 'Household Organization' created with ID: P1
Creating property First Name...
Property 'First Name' created with ID: P2
Creating property Last Name...
Property 'Last Name' created with ID: P3
Creating property Last Name Changed...
Property 'Last Name Changed' created with ID: P4
Creating property Birth Date...
Property 'Birth Date' created with ID: P5
Creating property Birth Place...
Property 'Birth Place' created with ID: P6
Creating property Death Place...
Property 'Death Place' created with ID: P7
Creating property Nationality...
Property 'Nationality' created with ID: P8
Creating property Birth Country...
Property 'Birth Country' created with ID: P9
Creating property Death Date Notes...
Property 'Death Date Notes' created with ID: P10
Creating property Alternative Death Place...
Property 'Alternati

In [5]:
import requests
import json
import urllib3
import time
import random

# Disable SSL warnings (only if you're working in a non-production environment)
urllib3.disable_warnings(urllib3.exceptions.InsecureRequestWarning)

# Define the API endpoint
api_url = "http://wikibase.example.com/w/api.php"  # Replace with your actual API URL

# Initialize session
session = requests.Session()

# Step 1: Retrieve the login token
params = {
    "action": "query",
    "meta": "tokens",
    "type": "login",
    "format": "json"
}

# Make the GET request to retrieve the login token
response = session.get(api_url, params=params, verify=False)

if response.status_code == 200:
    data = response.json()
    login_token = data['query']['tokens']['logintoken']
    print(f"Login Token: {login_token}")
else:
    print(f"Failed to retrieve login token. Status code: {response.status_code}")
    exit()

# Step 2: Log in using the login token
login_params = {
    "action": "clientlogin",
    "username": "admin",  # Replace with your username
    "password": "change-this-password",  # Replace with your password
    "logintoken": login_token,
    "loginreturnurl": "http://wikibase.example.com",  # Replace with your return URL
    "format": "json"
}

login_response = session.post(api_url, data=login_params, verify=False)

if login_response.status_code == 200:
    login_data = login_response.json()
    if login_data.get("clientlogin", {}).get("status") == "PASS":
        print("Logged in successfully!")
    else:
        print(f"Failed to log in: {login_data}")
        exit()
else:
    print(f"Login request failed with status code: {login_response.status_code}")
    exit()

# Step 3: Retrieve CSRF token
csrf_params = {
    "action": "query",
    "meta": "tokens",
    "type": "csrf",
    "format": "json"
}

csrf_response = session.get(api_url, params=csrf_params, verify=False)

if csrf_response.status_code == 200:
    csrf_data = csrf_response.json()
    csrf_token = csrf_data['query']['tokens']['csrftoken']
    print(f"CSRF Token: {csrf_token}")
else:
    print(f"Failed to retrieve CSRF token. Status code: {csrf_response.status_code}")
    exit()

# Function to get all properties from Wikibase (Namespace 122 is for Properties)
def get_all_properties():
    properties = []
    apcontinue = None  # For pagination

    while True:
        params = {
            "action": "query",
            "list": "allpages",
            "apnamespace": 122,  # Namespace for properties
            "aplimit": "max",    # Adjust this to a reasonable number, max can be 500
            "format": "json"
        }

        if apcontinue:
            params["apcontinue"] = apcontinue

        response = session.get(api_url, params=params, verify=False)
        data = response.json()

        # Check if the request was successful
        if "query" in data:
            # Append current batch of properties to the list
            properties.extend(data["query"].get("allpages", []))
        else:
            print(f"Error in response: {data}")
            break

        # Check if there's more data to fetch
        if "continue" in data:
            apcontinue = data["continue"]["apcontinue"]
        else:
            break

        # Adding a random delay to avoid hitting rate limits
        time.sleep(random.uniform(1, 3))

    return properties

# Main logic to retrieve all properties
def main():
    # Retrieve all properties from the Property namespace (122)
    properties = get_all_properties()

    # Check if all properties were retrieved
    print("Total properties retrieved:", len(properties))
    for prop in properties:
        print(f"ID: {prop['pageid']}, Title: {prop['title']}")

# Execute the main function
main()

Login Token: 0be17a089685fbc99d5bd83e443677806751acb4+\
Logged in successfully!
CSRF Token: 45a9f714e7c4ba192f889dbe753ca9c86751acb4+\
Total properties retrieved: 22
ID: 2, Title: Property:P1
ID: 11, Title: Property:P10
ID: 12, Title: Property:P11
ID: 13, Title: Property:P12
ID: 14, Title: Property:P13
ID: 15, Title: Property:P14
ID: 16, Title: Property:P15
ID: 17, Title: Property:P16
ID: 18, Title: Property:P17
ID: 19, Title: Property:P18
ID: 20, Title: Property:P19
ID: 3, Title: Property:P2
ID: 21, Title: Property:P20
ID: 217, Title: Property:P21
ID: 218, Title: Property:P22
ID: 4, Title: Property:P3
ID: 5, Title: Property:P4
ID: 6, Title: Property:P5
ID: 7, Title: Property:P6
ID: 8, Title: Property:P7
ID: 9, Title: Property:P8
ID: 10, Title: Property:P9


## Creating Entities

In [ ]:
import os
import requests
import json
import urllib3
import time  # Import time for the sleep function

# Disable SSL warnings (only if you're working in a non-production environment)
urllib3.disable_warnings(urllib3.exceptions.InsecureRequestWarning)

# Define the API endpoint
api_url = "https://wikibase.example.com/w/api.php"  # Replace with your actual API URL

# Your bot's credentials
USERNAME = "admin"  # Replace with your username
PASSWORD = "change-this-password"  # Replace with your password

# Directory containing the JSON profiles
input_directory = "/Users/ismail.ahouari/wikibase-release-pipeline/deploy/profiles/"  # Replace with your actual directory path

# Function to log in to Wikibase
def login_to_wikibase():
    session = requests.Session()
    
    # Step 1: Retrieve the login token
    params = {
        "action": "query",
        "meta": "tokens",
        "type": "login",
        "format": "json"
    }

    response = session.get(api_url, params=params, verify=False)

    if response.status_code == 200:
        data = response.json()
        login_token = data['query']['tokens']['logintoken']
    else:
        raise Exception(f"Failed to retrieve login token. Status code: {response.status_code}")

    # Step 2: Log in using the login token
    login_params = {
        "action": "clientlogin",
        "username": USERNAME,
        "password": PASSWORD,
        "logintoken": login_token,
        "loginreturnurl": api_url,  # Replace with your return URL
        "format": "json"
    }

    login_response = session.post(api_url, data=login_params, verify=False)

    if login_response.status_code == 200:
        login_data = login_response.json()
        if login_data.get("clientlogin", {}).get("status") == "PASS":
            print("Logged in successfully!")
        else:
            raise Exception(f"Failed to log in: {login_data}")
    else:
        raise Exception(f"Login request failed with status code: {login_response.status_code}")

    return session

# Function to retrieve CSRF token
def get_csrf_token(session):
    csrf_params = {
        "action": "query",
        "meta": "tokens",
        "type": "csrf",
        "format": "json"
    }

    csrf_response = session.get(api_url, params=csrf_params, verify=False)

    if csrf_response.status_code == 200:
        csrf_data = csrf_response.json()
        return csrf_data['query']['tokens']['csrftoken']
    else:
        raise Exception(f"Failed to retrieve CSRF token. Status code: {csrf_response.status_code}")

# Function to search for an existing entity by label and description
def find_existing_entity(session, label, description, language='en'):
    search_params = {
        'action': 'wbsearchentities',
        'search': label,
        'language': language,
        'format': 'json',
        'type': 'item'
    }

    search_response = session.get(api_url, params=search_params, verify=False)

    if search_response.status_code == 200:
        search_data = search_response.json()
        for entity in search_data.get('search', []):
            # Compare both the label and description to identify the correct entity
            if entity['label'] == label and entity.get('description', '') == description:
                print(f"Found existing entity: {entity['id']} for label: {label}")
                return entity['id']  # Return the ID of the matching entity
    return None

def create_or_update_entity(session, csrf_token, person_data):
    label = f"{person_data['first_name']} {person_data['last_name']}"
    description = f"Profile of {label}"
    
    # Check if an entity with this label and description already exists
    existing_entity_id = find_existing_entity(session, label, description)
    
    if existing_entity_id:
        print(f"Entity already exists: {existing_entity_id}. Skipping creation.")
        return existing_entity_id  # Return the existing entity ID to update it

    # Prepare data for entity creation
    entity_data = {
        'labels': {'en': {'language': 'en', 'value': label}},
        'descriptions': {'en': {'language': 'en', 'value': description}},
        'claims': []
    }

    # Attempt to create the entity
    response = session.post(api_url, data={
        'action': 'wbeditentity',
        'new': 'item',
        'token': csrf_token,
        'data': json.dumps(entity_data),
        'format': 'json'
    }, verify=False)

    if response.status_code == 200:
        response_data = response.json()
        if 'error' in response_data:
            if response_data['error']['code'] == 'modification-failed':
                # This error indicates that the entity already exists, so find it and return the ID
                existing_entity_id = find_existing_entity(session, label, description)
                if existing_entity_id:
                    print(f"Entity already exists: {existing_entity_id}. Skipping creation.")
                    return existing_entity_id
            else:
                raise Exception(f"Failed to create entity: {response_data['error']['info']}")
        else:
            print(f"Created new entity: {response_data['entity']['id']}")
            return response_data['entity']['id']
    else:
        raise Exception(f"Failed to create entity with status code: {response.status_code}")

# Function to check if a statement exists for a given property and value
def statement_exists(entity_data, property_id, value):
    claims = entity_data.get('claims', {})
    
    if property_id in claims:
        # Iterate through all claims for this property
        for claim in claims[property_id]:
            existing_value = claim['mainsnak'].get('datavalue', {}).get('value')
            if existing_value == value:
                return True  # Statement with this value already exists
    
    return False  # Statement does not exist

# Function to retrieve entity data
def get_entity_data(session, entity_id):
    retrieve_params = {
        'action': 'wbgetentities',
        'ids': entity_id,
        'format': 'json'
    }
    
    retrieve_response = session.get(api_url, params=retrieve_params, verify=False)
    
    if retrieve_response.status_code == 200:
        entity_data = retrieve_response.json().get('entities', {}).get(entity_id, {})
        return entity_data
    else:
        raise Exception(f"Failed to retrieve entity data with status code: {retrieve_response.status_code}")

from datetime import datetime

# Function to convert date from "DD/MM/YYYY" to "YYYY-MM-DDT00:00:00Z"
def convert_date(date_str):
    try:
        return datetime.strptime(date_str, "%d/%m/%Y").strftime("%Y-%m-%dT00:00:00Z")
    except ValueError:
        return "0000-00-00T00:00:00Z"

def add_statements(session, csrf_token, entity_id, person_data):
    # Retrieve existing entity data
    entity_data = get_entity_data(session, entity_id)

    # Constructing statements dynamically based on person_data with "Unknown" as default for missing data
    statements = {
        "P4": {"value": person_data.get('last_name_changed', "Unknown"), "type": "string"},  # Last Name Changed (String)
        
        "P5": {  # Birth Date (Time)
            "value": {
                "time": f"+{convert_date(person_data.get('birth_date', '0000-00-00'))}",
                "timezone": 0,
                "before": 0,
                "after": 0,
                "precision": 11,
                "calendarmodel": "http://www.wikidata.org/entity/Q1985727"
            },
            "type": "time"
        } if person_data.get('birth_date') else {
            "value": {
                "time": "+0000-00-00T00:00:00Z",
                "precision": 11,
                "calendarmodel": "http://www.wikidata.org/entity/Q1985727"
            },
            "type": "time"
        },
        
        "P16": {  # Convoy Date (Time)
            "value": {
                "time": f"+{convert_date(person_data.get('convoy_date', '0000-00-00'))}",
                "timezone": 0,
                "before": 0,
                "after": 0,
                "precision": 11,
                "calendarmodel": "http://www.wikidata.org/entity/Q1985727"
            },
            "type": "time"
        } if person_data.get('convoy_date') else {
            "value": {
                "time": "+0000-00-00T00:00:00Z",
                "precision": 11,
                "calendarmodel": "http://www.wikidata.org/entity/Q1985727"
            },
            "type": "time"
        },
        
        "P17": {  # Enter Date (Time)
            "value": {
                "time": f"+{convert_date(person_data.get('enter_date', '0000-00-00'))}",
                "timezone": 0,
                "before": 0,
                "after": 0,
                "precision": 11,
                "calendarmodel": "http://www.wikidata.org/entity/Q1985727"
            },
            "type": "time"
        } if person_data.get('enter_date') else {
            "value": {
                "time": "+0000-00-00T00:00:00Z",
                "precision": 11,
                "calendarmodel": "http://www.wikidata.org/entity/Q1985727"
            },
            "type": "time"
        },
        
        "P6": {"value": person_data.get('birth_place', "Unknown"), "type":"string"},  # Birth Place (String)
        "P9": {"value": person_data.get('birth_country', "Unknown"), "type": "string"},  # Birth Country (String)
        "P10": {"value": person_data.get('death_date_notes', "Unknown"), "type": "string"},  # Death Date Notes (String)
        "P7": {"value": person_data.get('death_place', "Unknown"), "type": "string"},  # Death Place (String)
        "P11": {"value": person_data.get('alternative_death_place', "Unknown"), "type": "string"},  # Alternative Death Place (String)
        "P12": {"value": person_data.get('death_country', "Unknown"), "type": "string"},  # Death Country (String)
        "P13": {"value": person_data.get('alternative_death_country', "Unknown"), "type": "string"},  # Alternative Death Country (String)
        "P8": {"value": person_data.get('nationality', "Unknown"), "type": "string"},  # Nationality (String)
        "P14": {"value": person_data.get('convoy', "Unknown"), "type": "string"},  # Convoy (String)
        "P15": {"value": person_data.get('convoy_place', "Unknown"), "type": "string"},  # Convoy Place (String)
        "P18": {"value": person_data.get('exit_19400510_to_19411015_place', "Unknown"), "type": "string"},  # Exit Between 1940-05-10 and 1941-10-15 Place (String)
        "P19": {"value": person_data.get('exit_19411016_to_19440910_place', "Unknown"), "type": "string"},  # Exit Between 1941-10-16 and 1944-09-10 Place (String)
        "P20": {"value": person_data.get('professions', "Unknown"), "type": "string"}  # Professions (String)
    }

    # Add statements for each property if they don't already exist
    for prop_id, value_data in statements.items():
        if not statement_exists(entity_data, prop_id, value_data['value']):
            claim_params = {
                'action': 'wbcreateclaim',
                'entity': entity_id,
                'snaktype': 'value',
                'property': prop_id,
                'value': json.dumps(value_data['value']),
                'token': csrf_token,
                'format': 'json'
            }



    # Add statements for each property if they don't already exist
    for prop_id, value_data in statements.items():
        if not statement_exists(entity_data, prop_id, value_data['value']):
            claim_params = {
                'action': 'wbcreateclaim',
                'entity': entity_id,
                'snaktype': 'value',
                'property': prop_id,
                'value': json.dumps(value_data['value']),
                'token': csrf_token,
                'format': 'json'
            }

            claim_response = session.post(api_url, data=claim_params, verify=False)

            if claim_response.status_code == 200:
                claim_data = claim_response.json()
                if 'error' in claim_data:
                    print(f"Failed to add statement for property {prop_id}: {claim_data['error']['info']}")
                else:
                    print(f"Statement added successfully for property {prop_id}")
            else:
                print(f"Failed to add statement for property {prop_id} with status code: {claim_response.status_code}, Error: {claim_response.json()}")
        else:
            print(f"Statement for property {prop_id} already exists. Skipping.")

# Function to process all profiles with a 3-second delay between each entity creation
def process_profiles():
    session = login_to_wikibase()
    csrf_token = get_csrf_token(session)
    
    for filename in os.listdir(input_directory):
        if filename.endswith(".json"):
            file_path = os.path.join(input_directory, filename)
            with open(file_path, "r", encoding="utf-8") as file:
                person_data = json.load(file)
                entity_id = create_or_update_entity(session, csrf_token, person_data)
                if entity_id is None:
                    print(f"Skipping profile {filename} because entity creation or identification failed.")
                    continue  # Skip this profile if no entity was found or created
                print(f"Processing entity {entity_id} for {filename}")
                add_statements(session, csrf_token, entity_id, person_data)
                
                # Pause for 3 seconds to comply with API rate limits
                time.sleep(3)

# Run the process
process_profiles()

### ADDING EXTRA STATEMENTS TO AN EXISTING ENITTY

In [ ]:
import requests
import json
import urllib3

# Disable SSL warnings (only if you're working in a non-production environment)
urllib3.disable_warnings(urllib3.exceptions.InsecureRequestWarning)

# Define the API endpoint
api_url = "https://wikibase.example.com/w/api.php"  # Replace with your actual API URL

# Initialize session
session = requests.Session()

# Step 1: Retrieve the login token
params = {
    "action": "query",
    "meta": "tokens",
    "type": "login",
    "format": "json"
}

# Make the GET request to retrieve the login token
response = session.get(api_url, params=params, verify=False)

if response.status_code == 200:
    data = response.json()
    login_token = data['query']['tokens']['logintoken']
    print(f"Login Token: {login_token}")
else:
    print(f"Failed to retrieve login token. Status code: {response.status_code}")
    exit()

# Step 2: Log in using the login token
login_params = {
    "action": "clientlogin",
    "username": "admin",  # Replace with your username
    "password": "change-this-password",  # Replace with your password
    "logintoken": login_token,
    "loginreturnurl": "https://wikibase.example.com",  # Replace with your return URL
    "format": "json"
}

login_response = session.post(api_url, data=login_params, verify=False)

if login_response.status_code == 200:
    login_data = login_response.json()
    if login_data.get("clientlogin", {}).get("status") == "PASS":
        print("Logged in successfully!")
    else:
        print(f"Failed to log in: {login_data}")
        exit()
else:
    print(f"Login request failed with status code: {login_response.status_code}")
    exit()

# Step 3: Retrieve CSRF token
csrf_params = {
    "action": "query",
    "meta": "tokens",
    "type": "csrf",
    "format": "json"
}

csrf_response = session.get(api_url, params=csrf_params, verify=False)

if csrf_response.status_code == 200:
    csrf_data = csrf_response.json()
    csrf_token = csrf_data['query']['tokens']['csrftoken']
    print(f"CSRF Token: {csrf_token}")
else:
    print(f"Failed to retrieve CSRF token. Status code: {csrf_response.status_code}")
    exit()

# Step 4: Check if the entity exists
entity_id = "Q205"  # Replace with your actual entity ID
retrieve_params = {
    'action': 'wbgetentities',
    'ids': entity_id,
    'format': 'json'
}

retrieve_response = session.get(api_url, params=retrieve_params, verify=False)

if retrieve_response.status_code == 200:
    entity_data = retrieve_response.json()
    if 'entities' in entity_data and entity_id in entity_data['entities']:
        print(f"Entity {entity_id} exists. Proceeding with claim additions.")
    else:
        print(f"Entity {entity_id} does not exist. Please check the ID.")
        exit()
else:
    print(f"Failed to retrieve entity with status code: {retrieve_response.status_code}")
    exit()

# Step 5: Add multiple statements to the entity

# Correct mapping of your data to appropriate property IDs with accurate data formats
statements = {
    "P117": "0019-Bar-Gutenstein",  # Household Organization (String)
    "P51": "Bär (Baer)",  # First Name (String)
    "P52": "Hilde",  # Last Name (String)
    "P142": "Mayer (nom d'épouse)",  # Last Name Changed (String)
    "P53":{  # Example property, e.g., "date of birth"
    "entity-type": "time",
    "time": "+1980-05-10T00:00:00Z",
    "timezone": 0,
    "before": 0,
    "after": 0,
    "precision": 11,
    "calendarmodel": "http://www.wikidata.org/entity/Q1985727"
     } , # Birth Date (Time)
    "P53": {
        "entity-type": "time",
        "time": "+1914-03-04T00:00:00Z",
        "timezone": 0,
        "before": 0,
        "after": 0,
        "precision": 11,
        "calendarmodel": "http://www.wikidata.org/entity/Q1985727"
    },  # Original Birth Date (Time)
    "P54": "Höheinöd",  # Birth Place (String)####
    "P58": "Chelmno",  # Death Place (String)###
    "P55": "Allemande",  # Nationality (String)####
    "P166": "Allemagne",  # Birth Country (String)
    "P170": "00/06/1944",  # Death Date Notes (String)
    
    "P172": "Kulmhof",  # Alternative Death Place (String)
    "P173": "Pologne",  # Death Country (String)
    "P174": "Deutsches Reich",  # Alternative Death Country (String)
    "P55": "Allemande",  # Nationality (String)####
    "P177": "L-01",  # Convoy (String)
    "P178": "Luxembourg",  # Convoy Place (String)
    "P179": {
        "entity-type": "time",
        "time": "+1941-10-16T00:00:00Z",
        "timezone": 0,
        "before": 0,
        "after": 0,
        "precision": 11,
        "calendarmodel": "http://www.wikidata.org/entity/Q1985727"
    },  # Convoy Date (Time)
    "P181": {
        "entity-type": "time",
        "time": "+1936-05-01T00:00:00Z",
        "timezone": 0,
        "before": 0,
        "after": 0,
        "precision": 11,
        "calendarmodel": "http://www.wikidata.org/entity/Q1985727"
    },  # Enter Date (Time)
    "P184": "Luxembourg",  # Exit Between 1940-05-10 and 1941-10-15 Place (String)
    "P186": "Luxembourg",  # Exit Between 1941-10-16 and 1944-09-10 Place (String)
    "P189": "Fußpflegerin"  # Professions (String)
}


# Function to add a statement
def add_statement(entity_id, property_id, value):
    claim_params = {
        'action': 'wbcreateclaim',
        'entity': entity_id,
        'snaktype': 'value',
        'property': property_id,
        'value': json.dumps(value) if isinstance(value, dict) else json.dumps(value),
        'token': csrf_token,
        'format': 'json'
    }

    claim_response = session.post(api_url, data=claim_params, verify=False)

    if claim_response.status_code == 200:
        claim_data = claim_response.json()
        if 'error' in claim_data:
            print(f"Failed to add statement for property {property_id}: {claim_data['error']['info']}")
        else:
            print(f"Statement added successfully for property {property_id}")
    else:
        print(f"Failed to add statement for property {property_id} with status code: {claim_response.status_code}, Error: {claim_response.json()}")

# Adding all statements
for prop_id, value in statements.items():
    add_statement(entity_id, prop_id, value)

Login Token: 53bd5d9e4d6ed4587dc242deac6e3ab066d09cba+\
Logged in successfully!
CSRF Token: 34abce11a5745650008e59a16cf002c266d09cba+\
Entity Q205 exists. Proceeding with claim additions.
Statement added successfully for property P117
Statement added successfully for property P51
Statement added successfully for property P52
Statement added successfully for property P142
Statement added successfully for property P53
Failed to add statement for property P54: Invalid snak data.
Failed to add statement for property P58: Invalid snak data.
Failed to add statement for property P55: Invalid snak data.
Statement added successfully for property P166
Statement added successfully for property P170
Statement added successfully for property P172
Statement added successfully for property P173
Statement added successfully for property P174
Statement added successfully for property P177
Statement added successfully for property P178
Statement added successfully for property P179
Statement added succe

In [ ]:
### "P39": {"value": person_data.get('type', "Unknown"), "type": "string"},  # Last Name Changed (String)

In [ ]:
import os
import requests
import json
import urllib3
import time
import re
from unidecode import unidecode

# Disable SSL warnings (only if you're working in a non-production environment)
urllib3.disable_warnings(urllib3.exceptions.InsecureRequestWarning)

# Define the API endpoint
api_url = "https://wikibase.example.com/w/api.php"  # Replace with your actual API URL

# Your bot's credentials
USERNAME = "admin"  # Replace with your username
PASSWORD = "change-this-password"  # Replace with your password

# Directory containing the JSON profiles
input_directory = "/Users/ismail.ahouari/wikibase-release-pipeline/deploy/profiles/"  # Replace with your actual directory path

# Function to log in to Wikibase
def login_to_wikibase():
    session = requests.Session()
    
    # Step 1: Retrieve the login token
    params = {
        "action": "query",
        "meta": "tokens",
        "type": "login",
        "format": "json"
    }

    response = session.get(api_url, params=params, verify=False)

    if response.status_code == 200:
        data = response.json()
        login_token = data['query']['tokens']['logintoken']
    else:
        raise Exception(f"Failed to retrieve login token. Status code: {response.status_code}")

    # Step 2: Log in using the login token
    login_params = {
        "action": "clientlogin",
        "username": USERNAME,
        "password": PASSWORD,
        "logintoken": login_token,
        "loginreturnurl": api_url,  # Replace with your return URL
        "format": "json"
    }

    login_response = session.post(api_url, data=login_params, verify=False)

    if login_response.status_code == 200:
        login_data = login_response.json()
        if login_data.get("clientlogin", {}).get("status") == "PASS":
            print("Logged in successfully!")
        else:
            raise Exception(f"Failed to log in: {login_data}")
    else:
        raise Exception(f"Login request failed with status code: {login_response.status_code}")

    return session

# Function to retrieve CSRF token
def get_csrf_token(session):
    csrf_params = {
        "action": "query",
        "meta": "tokens",
        "type": "csrf",
        "format": "json"
    }

    csrf_response = session.get(api_url, params=csrf_params, verify=False)

    if csrf_response.status_code == 200:
        csrf_data = csrf_response.json()
        return csrf_data['query']['tokens']['csrftoken']
    else:
        raise Exception(f"Failed to retrieve CSRF token. Status code: {csrf_response.status_code}")

# Normalize the label to remove special characters and convert to lowercase
def normalize_label(label):
    label = unidecode(label)
    label = re.sub(r'[\W_]+', ' ', label).strip().lower()
    return label

# Function to retrieve all entities and their labels
def retrieve_all_entities(session, limit=50):
    entities = {}
    continue_token = None

    while True:
        params = {
            'action': 'query',
            'list': 'allpages',
            'apnamespace': 0,  # Namespace 0 for items (Q items)
            'aplimit': limit,
            'format': 'json',
        }

        if continue_token:
            params['apcontinue'] = continue_token

        response = session.get(api_url, params=params, verify=False)

        if response.status_code == 200:
            data = response.json()
            pages = data.get('query', {}).get('allpages', [])
            for page in pages:
                entity_id = page['title']
                entity_label = get_entity_label(session, entity_id)
                if entity_label:
                    normalized_label = normalize_label(entity_label)
                    entities[normalized_label] = entity_id

            continue_token = data.get('continue', {}).get('apcontinue', None)
            if not continue_token:
                break
        else:
            raise Exception(f"Failed to retrieve entities. Status code: {response.status_code}")

    return entities

# Function to retrieve the label of a specific entity
def get_entity_label(session, entity_id, language='en'):
    params = {
        'action': 'wbgetentities',
        'ids': entity_id,
        'props': 'labels',
        'languages': language,
        'format': 'json'
    }
    
    response = session.get(api_url, params=params, verify=False)
    
    if response.status_code == 200:
        data = response.json()
        entities = data.get('entities', {})
        if entity_id in entities:
            labels = entities[entity_id].get('labels', {})
            return labels.get(language, {}).get('value', None)
    return None

# Function to update statements in an entity
def update_statements(session, csrf_token, entity_id, person_data):
    statements = {
        "P39": {"value": person_data.get('type', "Unknown"), "type": "string"},  # Example property
    }

    for prop_id, value_data in statements.items():
        claim_params = {
            'action': 'wbsetclaimvalue',
            'claim': entity_id,
            'snaktype': 'value',
            'property': prop_id,
            'value': json.dumps(value_data['value']),
            'token': csrf_token,
            'format': 'json'
        }

        claim_response = session.post(api_url, data=claim_params, verify=False)

        if claim_response.status_code == 200:
            claim_data = claim_response.json()
            if 'error' in claim_data:
                print(f"Failed to update statement for property {prop_id}: {claim_data['error']['info']}")
            else:
                print(f"Statement updated successfully for property {prop_id}")
        else:
            print(f"Failed to update statement for property {prop_id} with status code: {claim_response.status_code}, Error: {claim_response.json()}")

# Function to process all profiles and update statements
def process_profiles_for_update():
    session = login_to_wikibase()
    csrf_token = get_csrf_token(session)
    
    # Retrieve all entities and their labels
    entities = retrieve_all_entities(session)
    
    for filename in os.listdir(input_directory):
        if filename.endswith(".json"):
            file_path = os.path.join(input_directory, filename)
            with open(file_path, "r", encoding="utf-8") as file:
                person_data = json.load(file)

                # Extract and normalize the label from the filename
                base_filename = os.path.splitext(filename)[0]
                normalized_label = normalize_label(base_filename.replace("-", " "))

                # Find the entity by normalized label in the retrieved entities
                entity_id = entities.get(normalized_label)
                
                if entity_id is None:
                    print(f"Entity not found for {filename}. Skipping update.")
                    continue  # Skip this profile if the entity does not exist
                
                print(f"Updating entity {entity_id} for {filename}")
                update_statements(session, csrf_token, entity_id, person_data)
                
                # Pause for 3 seconds to comply with API rate limits
                time.sleep(3)

# Run the update process
process_profiles_for_update()

Logged in successfully!
Entity not found for Rosenthal-Ester(a).json. Skipping update.
Entity not found for Dura-Margarete.json. Skipping update.
Entity not found for Rothschild-Elisabeth.json. Skipping update.
Entity not found for Herrmann-Robert.json. Skipping update.
Entity not found for Wonagus-Joseph.json. Skipping update.
Entity not found for Borenstein-Elsa.json. Skipping update.
Entity not found for Weinberg-Martha.json. Skipping update.
Entity not found for Steinberger-Adolf.json. Skipping update.
Entity not found for Gompel-Martha.json. Skipping update.
Entity not found for Lipka-Sara_Frajda.json. Skipping update.
Entity not found for Finkelstein-Rachel.json. Skipping update.
Entity not found for Lévy-Gudella_dit_Della.json. Skipping update.
Entity not found for Dura-Martin.json. Skipping update.
Entity not found for Borenstein-Bernard.json. Skipping update.
Entity not found for Nathan-Chaja.json. Skipping update.
Entity not found for Hirsch-Nathalie.json. Skipping update.
En

### The Entities Created

In [21]:
import requests
import time
import random

# Initialize session
session = requests.Session()
api_url = "https://wikibase.example.com/w/api.php"  # Your Wikibase API URL

# Function to get CSRF token
def get_csrf_token():
    response = session.get(api_url, params={
        "action": "query",
        "meta": "tokens",
        "type": "csrf",
        "format": "json"
    }, verify=False)
    data = response.json()
    return data["query"]["tokens"]["csrftoken"]

# Function to get all properties from Wikibase
def get_all_properties():
    properties = []
    apcontinue = None  # For pagination

    while True:
        params = {
            "action": "query",
            "list": "allpages",
            "apnamespace": 120,  # Namespace for properties
            "aplimit": "max",    # Adjust this to a reasonable number, max can be 500
            "format": "json"
        }

        if apcontinue:
            params["apcontinue"] = apcontinue

        response = session.get(api_url, params=params, verify=False)
        data = response.json()

        # Check if the request was successful
        if "query" in data:
            # Append current batch of properties to the list
            properties.extend(data["query"].get("allpages", []))
        else:
            print(f"Error in response: {data}")
            break

        # Check if there's more data to fetch
        if "continue" in data:
            apcontinue = data["continue"]["apcontinue"]
        else:
            break

        # Adding a random delay to avoid hitting rate limits
        time.sleep(random.uniform(1, 3))

    return properties

def get_info_for_entity(qid):
    params = {
        "action": "wbgetentities",
        "ids": qid,
        "props": "labels|claims",
        "languages": "en",
        "format": "json"
    }

    response = session.get(api_url, params=params, verify=False)
    data = response.json()

    label = "No label found"
    claims = {}

    if "entities" in data and qid in data["entities"]:
        entity = data["entities"][qid]

        # Extract label
        if "labels" in entity and "en" in entity["labels"]:
            label = entity["labels"]["en"]["value"]

        # Extract all claims
        if "claims" in entity:
            for prop_id, prop_claims in entity["claims"].items():
                claims[prop_id] = []
                for claim in prop_claims:
                    value = claim["mainsnak"].get("datavalue", {}).get("value")
                    claims[prop_id].append(value)

    return label, claims

# Main logic
def main():
    # Get the CSRF token (not needed for reading, but included for completeness)
    csrf_token = get_csrf_token()

    # Retrieve all properties
    properties = get_all_properties()

    # Extract QIDs from the titles
    qids = [prop['title'].replace("Item:", "") for prop in properties]

    # Print total number of entities
    print(f"Total Entities: {len(qids)}")

    # Iterate through each QID and retrieve the label
    for qid in qids:
        label, _ = get_info_for_entity(qid)
        print(f"QID: {qid}, Label: {label}")

if __name__ == "__main__":
    main()

Total Entities: 192
QID: Q1, Label: Rosenthal Ester(a)
QID: Q10, Label: Lipka Sara Frajda
QID: Q100, Label: Rudow, Rudovs Erich
QID: Q101, Label: Rosenthal Maria / Macha
QID: Q102, Label: Borenstein Hanna (Helene)
QID: Q103, Label: Wonagus Ida
QID: Q104, Label: Gerson Elisabeth (Elise)
QID: Q105, Label: Springut Gisela
QID: Q106, Label: Michel Carlo
QID: Q107, Label: Seckler Blanche
QID: Q108, Label: Schmitz Johanna
QID: Q109, Label: Menzel Theodor
QID: Q11, Label: Finkelstein Rachel
QID: Q110, Label: David Irma
QID: Q111, Label: David Edmund
QID: Q112, Label: Wolf Paula
QID: Q113, Label: Weinberg Hermann
QID: Q114, Label: Wolff Therese (Theresia)
QID: Q115, Label: Glaser Anne
QID: Q116, Label: Faktorowitsch Salomon dit Sally
QID: Q117, Label: Cerf Salomon, genannt Schlauber
QID: Q118, Label: Schutzmann Esther Rosa
QID: Q119, Label: Borenstein Marcel
QID: Q12, Label: Lévy Gudella dit Della
QID: Q120, Label: Hanau Erich
QID: Q121, Label: Wolf Chaim
QID: Q122, Label: Ehrlich Frida
QID: Q

# Update a specific Entity 

## Check the entites Attributes

In [2]:
import requests
import time
import random
import logging
import urllib3

# Suppress the InsecureRequestWarning
urllib3.disable_warnings(urllib3.exceptions.InsecureRequestWarning)

# Initialize session
session = requests.Session()
api_url = "https://wikibase.example.com/w/api.php"  # Your Wikibase API URL

# Set up logging
logging.basicConfig(level=logging.INFO, format='%(asctime)s - %(levelname)s - %(message)s')

# Function to get CSRF token (if needed for write operations)
def get_csrf_token():
    try:
        response = session.get(api_url, params={
            "action": "query",
            "meta": "tokens",
            "type": "csrf",
            "format": "json"
        }, verify=False)  # Disable SSL verification
        response.raise_for_status()
        data = response.json()
        return data["query"]["tokens"]["csrftoken"]
    except requests.RequestException as e:
        logging.error(f"Error fetching CSRF token: {e}")
        return None

# Function to get all properties from Wikibase
def get_all_properties():
    properties = []
    apcontinue = None  # For pagination

    while True:
        params = {
            "action": "query",
            "list": "allpages",
            "apnamespace": 120,  # Namespace for properties
            "aplimit": 100,      # Adjust to a reasonable number, e.g., 100 per request
            "format": "json"
        }

        if apcontinue:
            params["apcontinue"] = apcontinue

        try:
            response = session.get(api_url, params=params, verify=False)  # Disable SSL verification
            response.raise_for_status()
            data = response.json()

            # Handle API errors and rate limits
            if "error" in data:
                logging.error(f"API error: {data['error']['info']}")
                break

            # Check if the request was successful
            if "query" in data:
                # Append current batch of properties to the list
                properties.extend(data["query"].get("allpages", []))
            else:
                logging.error(f"Error in response: {data}")
                break

            # Check if there's more data to fetch
            if "continue" in data:
                apcontinue = data["continue"].get("apcontinue")
            else:
                break

            # Adding a random delay to avoid hitting rate limits
            time.sleep(random.uniform(2, 5))  # Increase delay if hitting rate limits

        except requests.RequestException as e:
            logging.error(f"Request error: {e}")
            break

    return properties

def get_info_for_entity(qid):
    params = {
        "action": "wbgetentities",
        "ids": qid,
        "props": "labels|claims|descriptions|aliases",
        "languages": "en",
        "format": "json"
    }

    try:
        response = session.get(api_url, params=params, verify=False)  # Disable SSL verification
        response.raise_for_status()
        data = response.json()

        label = "No label found"
        description = "No description found"
        aliases = []
        claims = {}

        if "entities" in data and qid in data["entities"]:
            entity = data["entities"][qid]

            # Extract label
            if "labels" in entity and "en" in entity["labels"]:
                label = entity["labels"]["en"]["value"]

            # Extract description
            if "descriptions" in entity and "en" in entity["descriptions"]:
                description = entity["descriptions"]["en"]["value"]

            # Extract aliases
            if "aliases" in entity and "en" in entity["aliases"]:
                aliases = [alias["value"] for alias in entity["aliases"]["en"]]

            # Extract all claims
            if "claims" in entity:
                for prop_id, prop_claims in entity["claims"].items():
                    claims[prop_id] = []
                    for claim in prop_claims:
                        value = claim["mainsnak"].get("datavalue", {}).get("value")
                        claims[prop_id].append(value)

        return label, description, aliases, claims

    except requests.RequestException as e:
        logging.error(f"Error fetching entity data for QID {qid}: {e}")
        return "Error", "Error", [], {}

# Main logic
def main():
    # Get the CSRF token (if needed for write operations)
    # csrf_token = get_csrf_token()

    # Retrieve all properties
    properties = get_all_properties()

    # Extract QIDs from the titles
    qids = [prop['title'].replace("Item:", "") for prop in properties]
    # Print total number of entities
    logging.info(f"Total Entities: {len(qids)}")

    # Iterate through each QID and retrieve the label, description, aliases, and claims
    for qid in qids:
        label, description, aliases, claims = get_info_for_entity(qid)
        
        # Print information for each entity
        logging.info(f"QID: {qid}")
        logging.info(f"  Label: {label}")
        logging.info(f"  Description: {description}")
        logging.info(f"  Aliases: {', '.join(aliases)}")
        logging.info(f"  Claims: {claims}")
        logging.info("-" * 40)
        # Adding a delay between entity requests to avoid rate limits
        time.sleep(random.uniform(1, 3))

if __name__ == "__main__":
    main()
    

2024-10-20 23:08:58,043 - INFO - Total Entities: 192
2024-10-20 23:08:58,072 - INFO - QID: Q1
2024-10-20 23:08:58,073 - INFO -   Label: Rosenthal Ester(a)
2024-10-20 23:08:58,073 - INFO -   Description: Profile of Rosenthal Ester(a)
2024-10-20 23:08:58,073 - INFO -   Aliases: 
2024-10-20 23:08:58,074 - INFO -   Claims: {'P4': ['Unknown'], 'P5': [{'time': '+1927-05-26T00:00:00Z', 'timezone': 0, 'before': 0, 'after': 0, 'precision': 11, 'calendarmodel': 'http://www.wikidata.org/entity/Q1985727'}], 'P16': [{'time': '+1941-10-17T00:00:00Z', 'timezone': 0, 'before': 0, 'after': 0, 'precision': 11, 'calendarmodel': 'http://www.wikidata.org/entity/Q1985727'}], 'P17': [{'time': '+1929-06-16T00:00:00Z', 'timezone': 0, 'before': 0, 'after': 0, 'precision': 11, 'calendarmodel': 'http://www.wikidata.org/entity/Q1985727'}], 'P6': ['Lodz'], 'P9': ['Polen'], 'P10': ['00/09/1942'], 'P7': ['Chelmno'], 'P11': ['Unknown'], 'P12': ['Polen'], 'P13': ['Unknown'], 'P8': ['Polonaise'], 'P14': ['Da 3'], 'P15':

## Create a new Entity

This code you can create new property which will add to a specific entity or bulk add it to the every existing entity

In [34]:
import os
import requests
import json
import urllib3
import time
import re


# Disable SSL warnings (only if you're working in a non-production environment)
urllib3.disable_warnings(urllib3.exceptions.InsecureRequestWarning)

# Define the API endpoint
api_url = "https://wikibase.example.com/w/api.php"  # Replace with your actual API URL

# Your bot's credentials
USERNAME = "admin"  # Replace with your username
PASSWORD = "change-this-password"  # Replace with your password

# Directory containing the JSON profiles
input_directory = "/Users/ismail.ahouari/wikibase-release-pipeline/deploy/profiles/"  # Replace with your actual directory path

# Function to log in to Wikibase
def login_to_wikibase():
    session = requests.Session()
    
    # Step 1: Retrieve the login token
    params = {
        "action": "query",
        "meta": "tokens",
        "type": "login",
        "format": "json"
    }

    response = session.get(api_url, params=params, verify=False)

    if response.status_code == 200:
        data = response.json()
        login_token = data['query']['tokens']['logintoken']
    else:
        raise Exception(f"Failed to retrieve login token. Status code: {response.status_code}")

    # Step 2: Log in using the login token
    login_params = {
        "action": "clientlogin",
        "username": USERNAME,
        "password": PASSWORD,
        "logintoken": login_token,
        "loginreturnurl": api_url,  # Replace with your return URL
        "format": "json"
    }

    login_response = session.post(api_url, data=login_params, verify=False)

    if login_response.status_code == 200:
        login_data = login_response.json()
        if login_data.get("clientlogin", {}).get("status") == "PASS":
            print("Logged in successfully!")
        else:
            raise Exception(f"Failed to log in: {login_data}")
    else:
        raise Exception(f"Login request failed with status code: {login_response.status_code}")

    return session

# Function to retrieve CSRF token
def get_csrf_token(session):
    csrf_params = {
        "action": "query",
        "meta": "tokens",
        "type": "csrf",
        "format": "json"
    }

    csrf_response = session.get(api_url, params=csrf_params, verify=False)

    if csrf_response.status_code == 200:
        csrf_data = csrf_response.json()
        return csrf_data['query']['tokens']['csrftoken']
    else:
        raise Exception(f"Failed to retrieve CSRF token. Status code: {csrf_response.status_code}")

# Function to check if a property exists
def check_property_exists(label):
    params = {
        "action": "query",
        "list": "search",
        "srsearch": label,
        "srnamespace": 120,  # Namespace for properties
        "srwhat": "text",
        "srprop": "snippet",
        "format": "json"
    }

    try:
        response = session.get(api_url, params=params, verify=False)  # Disable SSL verification
        response.raise_for_status()
        data = response.json()

        if "query" in data and "search" in data["query"]:
            for result in data["query"]["search"]:
                if result['title'].lower() == f"property:{label.lower()}":
                    logging.info(f"Property '{label}' already exists with ID: {result['title']}")
                    return result['title']  # Return the existing property ID
        return None

    except requests.RequestException as e:
        logging.error(f"Error checking if property '{label}' exists: {e}")
        return None

# Function to create a new property called "Instance of"
def create_instance_of_property(session):
    csrf_token = get_csrf_token(session)
    if not csrf_token:
        logging.error("Unable to get CSRF token.")
        return None

    data = {
        "labels": {
            "en": {
                "language": "en",
                "value": "Instance of."
            }
        },
        "descriptions": {
            "en": {
                "language": "en",
                "value": "Property to specify that an item is an instance of a class or type"
            }
        },
        "datatype": "wikibase-item"  # This datatype is used to link to other items/entities, such as "Human"
    }

    params = {
        "action": "wbeditentity",
        "new": "property",
        "data": json.dumps(data),
        "format": "json",
        "token": csrf_token
    }

    try:
        response = session.post(api_url, data=params, verify=False)  # Disable SSL verification
        response.raise_for_status()
        data = response.json()

        if "error" in data:
            logging.error(f"API error: {data['error']['info']}")
            return None
        else:
            new_property_id = data["entity"]["id"]
            logging.info(f"New 'Instance of' property created with ID: {new_property_id}")
            return new_property_id

    except requests.RequestException as e:
        logging.error(f"Error creating new 'Instance of' property: {e}")
        return None

# Main logic to check for the property and create if it doesn't exist
def main():
    session = login_to_wikibase()
    label = "Instance of"
    
    # Check if the property already exists
    existing_property_id = check_property_exists(label)
    
    if existing_property_id:
        logging.info(f"Using existing property '{label}' with ID: {existing_property_id}")
    else:
        # If the property doesn't exist, create it
        new_property_id = create_instance_of_property(session)
        
        if new_property_id:
            logging.info(f"'Instance of' property created successfully with ID: {new_property_id}")
        else:
            logging.error("Failed to create the 'Instance of' property.")

if __name__ == "__main__":
    main()

Logged in successfully!


2024-10-21 16:26:38,500 - INFO - New 'Instance of' property created with ID: P21
2024-10-21 16:26:38,501 - INFO - 'Instance of' property created successfully with ID: P21


In [44]:
import os
import requests
import json
import urllib3
import logging

# Disable SSL warnings (only if you're working in a non-production environment)
urllib3.disable_warnings(urllib3.exceptions.InsecureRequestWarning)

# Define the API endpoint
api_url = "https://wikibase.example.com/w/api.php"  # Replace with your actual API URL

# Your bot's credentials
USERNAME = "admin"  # Replace with your username
PASSWORD = "change-this-password"  # Replace with your password

# Directory containing the JSON profiles
input_directory = "/Users/ismail.ahouari/wikibase-release-pipeline/deploy/profiles/"  # Replace with your actual directory path

# Function to log in to Wikibase
def login_to_wikibase():
    session = requests.Session()
    
    # Step 1: Retrieve the login token
    params = {
        "action": "query",
        "meta": "tokens",
        "type": "login",
        "format": "json"
    }

    response = session.get(api_url, params=params, verify=False)

    if response.status_code == 200:
        data = response.json()
        login_token = data['query']['tokens']['logintoken']
    else:
        raise Exception(f"Failed to retrieve login token. Status code: {response.status_code}")

    # Step 2: Log in using the login token
    login_params = {
        "action": "clientlogin",
        "username": USERNAME,
        "password": PASSWORD,
        "logintoken": login_token,
        "loginreturnurl": api_url,  # Replace with your return URL
        "format": "json"
    }

    login_response = session.post(api_url, data=login_params, verify=False)

    if login_response.status_code == 200:
        login_data = login_response.json()
        if login_data.get("clientlogin", {}).get("status") == "PASS":
            print("Logged in successfully!")
        else:
            raise Exception(f"Failed to log in: {login_data}")
    else:
        raise Exception(f"Login request failed with status code: {login_response.status_code}")

    return session

# Function to retrieve CSRF token
def get_csrf_token(session):
    csrf_params = {
        "action": "query",
        "meta": "tokens",
        "type": "csrf",
        "format": "json"
    }

    csrf_response = session.get(api_url, params=csrf_params, verify=False)

    if csrf_response.status_code == 200:
        csrf_data = csrf_response.json()
        return csrf_data['query']['tokens']['csrftoken']
    else:
        raise Exception(f"Failed to retrieve CSRF token. Status code: {csrf_response.status_code}")

# Function to check if a property exists
def check_property_exists(label):
    params = {
        "action": "query",
        "list": "search",
        "srsearch": label,
        "srnamespace": 120,  # Namespace for properties
        "srwhat": "text",
        "srprop": "snippet",
        "format": "json"
    }

    try:
        response = session.get(api_url, params=params, verify=False)
        response.raise_for_status()
        data = response.json()

        if "query" in data and "search" in data["query"]:
            for result in data["query"]["search"]:
                if result['title'].lower() == f"property:{label.lower()}":
                    logging.info(f"Property '{label}' already exists with ID: {result['title']}")
                    return result['title']  # Return the existing property ID
        return None

    except requests.RequestException as e:
        logging.error(f"Error checking if property '{label}' exists: {e}")
        return None

# Function to create a new property called "Instance of"
def create_instance_of_property(session):
    csrf_token = get_csrf_token(session)
    if not csrf_token:
        logging.error("Unable to get CSRF token.")
        return None

    data = {
        "labels": {
            "en": {
                "language": "en",
                "value": "Instance of (string)"
            }
        },
        "descriptions": {
            "en": {
                "language": "en",
                "value": "Property to specify that an item is an instance of a class or type, accepting string values"
            }
        },
        "datatype": "string"  # Changed to "string" datatype to accept strings instead of "wikibase-item"
    }

    params = {
        "action": "wbeditentity",
        "new": "property",
        "data": json.dumps(data),
        "format": "json",
        "token": csrf_token
    }

    try:
        response = session.post(api_url, data=params, verify=False)
        response.raise_for_status()
        data = response.json()

        if "error" in data:
            logging.error(f"API error: {data['error']['info']}")
            return None
        else:
            new_property_id = data["entity"]["id"]
            logging.info(f"New 'Instance of' property (string) created with ID: {new_property_id}")
            return new_property_id

    except requests.RequestException as e:
        logging.error(f"Error creating new 'Instance of' property: {e}")
        return None

# Main logic to check for the property and create if it doesn't exist
def main():
    session = login_to_wikibase()
    label = "Instance Of"
    
    # Check if the property already exists
    existing_property_id = check_property_exists(label)
    
    if existing_property_id:
        logging.info(f"Using existing property '{label}' with ID: {existing_property_id}")
    else:
        # If the property doesn't exist, create it
        new_property_id = create_instance_of_property(session)
        
        if new_property_id:
            logging.info(f"'Instance of' property created successfully with ID: {new_property_id}")
        else:
            logging.error("Failed to create the 'Instance of' property.")

if __name__ == "__main__":
    main()

Logged in successfully!


2024-10-21 17:03:32,277 - INFO - New 'Instance of' property (string) created with ID: P22
2024-10-21 17:03:32,277 - INFO - 'Instance of' property created successfully with ID: P22


### Create Enitty ID property

In [206]:
import os
import requests
import json
import urllib3
import logging

# Disable SSL warnings (only if you're working in a non-production environment)
urllib3.disable_warnings(urllib3.exceptions.InsecureRequestWarning)

# Define the API endpoint
api_url = "https://wikibase.example.com/w/api.php"  # Replace with your actual API URL

# Your bot's credentials
USERNAME = "admin"  # Replace with your username
PASSWORD = "change-this-password"  # Replace with your password

# Directory containing the JSON profiles
input_directory = "/Users/ismail.ahouari/Public/wikibase-release-pipeline/deploy/reecords/"  # Replace with your actual directory path

# Function to log in to Wikibase
def login_to_wikibase():
    session = requests.Session()
    
    # Step 1: Retrieve the login token
    params = {
        "action": "query",
        "meta": "tokens",
        "type": "login",
        "format": "json"
    }

    response = session.get(api_url, params=params, verify=False)

    if response.status_code == 200:
        data = response.json()
        login_token = data['query']['tokens']['logintoken']
    else:
        raise Exception(f"Failed to retrieve login token. Status code: {response.status_code}")

    # Step 2: Log in using the login token
    login_params = {
        "action": "clientlogin",
        "username": USERNAME,
        "password": PASSWORD,
        "logintoken": login_token,
        "loginreturnurl": api_url,  # Replace with your return URL
        "format": "json"
    }

    login_response = session.post(api_url, data=login_params, verify=False)

    if login_response.status_code == 200:
        login_data = login_response.json()
        if login_data.get("clientlogin", {}).get("status") == "PASS":
            print("Logged in successfully!")
        else:
            raise Exception(f"Failed to log in: {login_data}")
    else:
        raise Exception(f"Login request failed with status code: {login_response.status_code}")

    return session

# Function to retrieve CSRF token
def get_csrf_token(session):
    csrf_params = {
        "action": "query",
        "meta": "tokens",
        "type": "csrf",
        "format": "json"
    }

    csrf_response = session.get(api_url, params=csrf_params, verify=False)

    if csrf_response.status_code == 200:
        csrf_data = csrf_response.json()
        return csrf_data['query']['tokens']['csrftoken']
    else:
        raise Exception(f"Failed to retrieve CSRF token. Status code: {csrf_response.status_code}")

# Function to check if a property exists
def check_property_exists(label):
    params = {
        "action": "query",
        "list": "search",
        "srsearch": label,
        "srnamespace": 120,  # Namespace for properties
        "srwhat": "text",
        "srprop": "snippet",
        "format": "json"
    }

    try:
        response = session.get(api_url, params=params, verify=False)
        response.raise_for_status()
        data = response.json()

        if "query" in data and "search" in data["query"]:
            for result in data["query"]["search"]:
                if result['title'].lower() == f"property:{label.lower()}":
                    logging.info(f"Property '{label}' already exists with ID: {result['title']}")
                    return result['title']  # Return the existing property ID
        return None

    except requests.RequestException as e:
        logging.error(f"Error checking if property '{label}' exists: {e}")
        return None

# Function to create a new property called "New Property"
def create_string_property(session, label, description):
    csrf_token = get_csrf_token(session)
    if not csrf_token:
        logging.error("Unable to get CSRF token.")
        return None

    data = {
        "labels": {
            "en": {
                "language": "en",
                "value": label
            }
        },
        "descriptions": {
            "en": {
                "language": "en",
                "value": description
            }
        },
        "datatype": "string"  # This creates a property that accepts strings
    }

    params = {
        "action": "wbeditentity",
        "new": "property",
        "data": json.dumps(data),
        "format": "json",
        "token": csrf_token
    }

    try:
        response = session.post(api_url, data=params, verify=False)
        response.raise_for_status()
        data = response.json()

        if "error" in data:
            logging.error(f"API error: {data['error']['info']}")
            return None
        else:
            property_id = data["entity"]["id"]
            logging.info(f"New property created with ID: {property_id}")
            return property_id

    except requests.RequestException as e:
        logging.error(f"Error creating new property: {e}")
        return None

# Main logic to check for the property and create if it doesn't exist
def main():
    session = login_to_wikibase()
    label = "Entity ID"
    description = "This property accepts string attributes."

    # Check if the property already exists
    property_id = check_property_exists(label)
    
    if property_id:
        logging.info(f"Using existing property '{label}' with ID: {property_id}")
    else:
        # If the property doesn't exist, create it
        property_id = create_string_property(session, label, description)
        
        if property_id:
            logging.info(f"Property '{label}' created successfully with ID: {property_id}")
        else:
            logging.error("Failed to create the property.")

if __name__ == "__main__":
    main()

Logged in successfully!


2024-10-24 13:26:00,625 - INFO - New property created with ID: P26
2024-10-24 13:26:00,626 - INFO - Property 'Entity ID' created successfully with ID: P26


## UPDATE ENTITY PROFILE

### Adding New Claim/Properties to an existing entity

In [51]:
import os
import requests
import json
import urllib3
import logging

# Disable SSL warnings (only if you're working in a non-production environment)
urllib3.disable_warnings(urllib3.exceptions.InsecureRequestWarning)

# Define the API endpoint
api_url = "https://wikibase.example.com/w/api.php"  # Replace with your actual API URL

# Your bot's credentials
USERNAME = "admin"  # Replace with your username
PASSWORD = "change-this-password"  # Replace with your password

# Directory containing the JSON profiles
input_directory = "/Users/ismail.ahouari/wikibase-release-pipeline/deploy/profiles/"  # Replace with your actual directory path

# Function to log in to Wikibase
def login_to_wikibase():
    session = requests.Session()
    
    # Step 1: Retrieve the login token
    params = {
        "action": "query",
        "meta": "tokens",
        "type": "login",
        "format": "json"
    }

    response = session.get(api_url, params=params, verify=False)

    if response.status_code == 200:
        data = response.json()
        login_token = data['query']['tokens']['logintoken']
    else:
        raise Exception(f"Failed to retrieve login token. Status code: {response.status_code}")

    # Step 2: Log in using the login token
    login_params = {
        "action": "clientlogin",
        "username": USERNAME,
        "password": PASSWORD,
        "logintoken": login_token,
        "loginreturnurl": api_url,  # Replace with your return URL
        "format": "json"
    }

    login_response = session.post(api_url, data=login_params, verify=False)

    if login_response.status_code == 200:
        login_data = login_response.json()
        if login_data.get("clientlogin", {}).get("status") == "PASS":
            print("Logged in successfully!")
        else:
            raise Exception(f"Failed to log in: {login_data}")
    else:
        raise Exception(f"Login request failed with status code: {login_response.status_code}")

    return session

# Function to retrieve CSRF token
def get_csrf_token(session):
    csrf_params = {
        "action": "query",
        "meta": "tokens",
        "type": "csrf",
        "format": "json"
    }

    csrf_response = session.get(api_url, params=csrf_params, verify=False)

    if csrf_response.status_code == 200:
        csrf_data = csrf_response.json()
        return csrf_data['query']['tokens']['csrftoken']
    else:
        raise Exception(f"Failed to retrieve CSRF token. Status code: {csrf_response.status_code}")

# Function to fetch information for an entity
def get_info_for_entity(session, qid):
    params = {
        "action": "wbgetentities",
        "ids": qid,
        "props": "labels|claims|descriptions|aliases",
        "languages": "en",
        "format": "json"
    }

    try:
        response = session.get(api_url, params=params, verify=False)
        response.raise_for_status()
        data = response.json()

        label = "No label found"
        description = "No description found"
        aliases = []
        claims = {}

        if "entities" in data and qid in data["entities"]:
            entity = data["entities"][qid]

            # Extract label
            if "labels" in entity and "en" in entity["labels"]:
                label = entity["labels"]["en"]["value"]

            # Extract description
            if "descriptions" in entity and "en" in entity["descriptions"]:
                description = entity["descriptions"]["en"]["value"]

            # Extract aliases
            if "aliases" in entity and "en" in entity["aliases"]:
                aliases = [alias["value"] for alias in entity["aliases"]["en"]]

            # Extract all claims
            if "claims" in entity:
                for prop_id, prop_claims in entity["claims"].items():
                    claims[prop_id] = []
                    for claim in prop_claims:
                        value = claim["mainsnak"].get("datavalue", {}).get("value")
                        claims[prop_id].append(value)

        return label, description, aliases, claims

    except requests.RequestException as e:
        logging.error(f"Error fetching entity data for QID {qid}: {e}")
        return "Error", "Error", [], {}

# Function to edit an entity
def edit_entitys(session, qid, new_claims):
    csrf_token = get_csrf_token(session)
    if not csrf_token:
        logging.error("Unable to get CSRF token.")
        return

    for claim in new_claims:
        # Log the claim details for debugging
        logging.info(f"Attempting to add claim: {claim}")

        params = {
            "action": "wbcreateclaim",
            "entity": qid,
            "snaktype": claim['snaktype'],
            "property": claim['property'],
            "value": claim['value'],
            "format": "json",
            "token": csrf_token
        }

        try:
            response = session.post(api_url, data=params, verify=False)
            response.raise_for_status()
            data = response.json()

            if "error" in data:
                logging.error(f"API error: {data['error']['info']}")
            else:
                logging.info(f"Claim added to QID {qid}: {claim}")

        except requests.RequestException as e:
            logging.error(f"Error editing entity QID {qid}: {e}")

# Main logic
def main():
    session = login_to_wikibase()
    
    # Retrieve information for a specific entity
    qid = "Q1"  # Example QID
    label, description, aliases, claims = get_info_for_entity(session, qid)
    
    # Prepare new claims to add
    new_claims = [
    {
        "snaktype": "value",
        "property": "P22",
        "value": json.dumps("Person")  # Example string value
    }
]

    # Edit the entity by adding new claims
    edit_entitys(session, qid, new_claims)

if __name__ == "__main__":
    main()

2024-10-21 17:10:46,155 - INFO - Attempting to add claim: {'snaktype': 'value', 'property': 'P22', 'value': '"Person"'}
2024-10-21 17:10:46,235 - INFO - Claim added to QID Q1: {'snaktype': 'value', 'property': 'P22', 'value': '"Person"'}


Logged in successfully!


In [70]:
import os
import requests
import json
import urllib3
import time
import logging  # Added for logging errors

from datetime import datetime

# Disable SSL warnings (only if you're working in a non-production environment)
urllib3.disable_warnings(urllib3.exceptions.InsecureRequestWarning)

# Define the API endpoint
api_url = "https://wikibase.example.com/w/api.php"  # Replace with your actual API URL

# Your bot's credentials
USERNAME = "admin"  # Replace with your username
PASSWORD = "change-this-password"  # Replace with your password

# Directory containing the JSON profiles
input_directory = "/Users/ismail.ahouari/wikibase-release-pipeline/deploy/profiles/"  # Replace with your actual directory path

def login_to_wikibase():
    session = requests.Session()
    
    params = {
        "action": "query",
        "meta": "tokens",
        "type": "login",
        "format": "json"
    }

    response = session.get(api_url, params=params, verify=False)

    if response.status_code == 200:
        data = response.json()
        login_token = data['query']['tokens']['logintoken']
    else:
        raise Exception(f"Failed to retrieve login token. Status code: {response.status_code}")

    login_params = {
        "action": "clientlogin",
        "username": USERNAME,
        "password": PASSWORD,
        "logintoken": login_token,
        "loginreturnurl": api_url,
        "format": "json"
    }

    login_response = session.post(api_url, data=login_params, verify=False)

    if login_response.status_code == 200:
        login_data = login_response.json()
        if login_data.get("clientlogin", {}).get("status") == "PASS":
            print("Logged in successfully!")
        else:
            raise Exception(f"Failed to log in: {login_data}")
    else:
        raise Exception(f"Login request failed with status code: {login_response.status_code}")

    return session

def get_csrf_token(session):
    csrf_params = {
        "action": "query",
        "meta": "tokens",
        "type": "csrf",
        "format": "json"
    }

    csrf_response = session.get(api_url, params=csrf_params, verify=False)

    if csrf_response.status_code == 200:
        csrf_data = csrf_response.json()
        return csrf_data['query']['tokens']['csrftoken']
    else:
        raise Exception(f"Failed to retrieve CSRF token. Status code: {csrf_response.status_code}")

# Function to get all properties from Wikibase
def get_all_properties(session):
    properties = []
    apcontinue = None  # For pagination

    while True:
        params = {
            "action": "query",
            "list": "allpages",
            "apnamespace": 120,  # Namespace for properties
            "aplimit": "max",    # Adjust this to a reasonable number, max can be 500
            "format": "json"
        }

        if apcontinue:
            params["apcontinue"] = apcontinue

        response = session.get(api_url, params=params, verify=False)
        data = response.json()

        # Check if the request was successful
        if "query" in data:
            # Append current batch of properties to the list
            properties.extend(data["query"].get("allpages", []))
        else:
            logging.error(f"Error in response: {data}")
            break

        # Check if there's more data to fetch
        if "continue" in data:
            apcontinue = data["continue"]["apcontinue"]
        else:
            break

        # Adding a random delay to avoid hitting rate limits
        time.sleep(random.uniform(5, 10))  # Increase delay to 5-10 seconds

    return properties

def get_info_for_entity(session, qid):
    params = {
        "action": "wbgetentities",
        "ids": qid,
        "props": "labels|claims",
        "languages": "en",
        "format": "json"
    }

    response = session.get(api_url, params=params, verify=False)
    data = response.json()

    label = "No label found"
    claims = {}

    if "entities" in data and qid in data["entities"]:
        entity = data["entities"][qid]

        # Extract label
        if "labels" in entity and "en" in entity["labels"]:
            label = entity["labels"]["en"]["value"]

        # Extract all claims
        if "claims" in entity:
            for prop_id, prop_claims in entity["claims"].items():
                claims[prop_id] = []
                for claim in prop_claims:
                    value = claim["mainsnak"].get("datavalue", {}).get("value")
                    claims[prop_id].append(value)

    return label, claims

# Function to edit an entity with exponential backoff and throttling handling
def edit_entitys(session, csrf_token, qid, new_claims, max_retries=5):
    delay = 5  # Start with a 5-second delay to prevent immediate throttling
    retries = 0  # Initialize retries

    for attempt in range(max_retries):
        success = False

        for claim in new_claims:
            try:
                # Check if the claim already exists to avoid duplication
                _, existing_claims = get_info_for_entity(session, qid)
                if claim["property"] in existing_claims and claim["value"] in existing_claims[claim["property"]]:
                    logging.info(f"Claim already exists for QID {qid}, skipping: {claim}")
                    success = True  # Consider it a success if the claim already exists
                    break

                # Log the claim details for debugging
                logging.info(f"Attempt {attempt + 1}/{max_retries} to add claim: {claim}")

                params = {
                    "action": "wbcreateclaim",
                    "entity": qid,
                    "snaktype": claim['snaktype'],
                    "property": claim['property'],
                    "value": claim['value'],
                    "format": "json",
                    "token": csrf_token
                }

                response = session.post(api_url, data=params, verify=False)  # Disable SSL verification
                response.raise_for_status()
                data = response.json()

                if "error" in data:
                    logging.error(f"API error on attempt {attempt + 1}/{max_retries}: {data['error']['info']} | Full response: {json.dumps(data)}")
                    if "actionthrottledtext" in json.dumps(data):
                        logging.warning(f"Throttling detected. Will retry after {delay} seconds.")
                        time.sleep(delay)  # Wait before retrying
                        delay *= 2  # Exponential backoff
                        retries += 1  # Increment retries
                    else:
                        retries += 1  # Increment retries for non-throttling errors
                else:
                    logging.info(f"Claim added to QID {qid} on attempt {attempt + 1}/{max_retries}: {claim}")
                    success = True
                    break  # Exit the loop on success

            except requests.RequestException as e:
                logging.error(f"Error editing entity QID {qid} on attempt {attempt + 1}/{max_retries}: {e}")
                retries += 1  # Increment retries for network issues

        if success:
            break  # Exit if successful

        # If no success and retries are exhausted, log the failure
        if attempt == max_retries - 1:
            logging.error(f"Failed to add claims to QID {qid} after {max_retries} attempts.")

# Main logic
def main():
    # Log in to Wikibase
    session = login_to_wikibase()
    
    # Get the CSRF token (required for modifying entities)
    csrf_token = get_csrf_token(session)

    # Retrieve all properties
    properties = get_all_properties(session)

    # Extract QIDs from the titles
    qids = [prop['title'].replace("Item:", "") for prop in properties]

    # Print total number of entities
    print(f"Total Entities: {len(qids)}")

    # Prepare new claims to add
    new_claims = [
        {
            "snaktype": "value",
            "property": "P22",
            "value": json.dumps("Person")  # Example string value
        }
    ]

    # Iterate through each QID, retrieve the label, and add new claims
    for qid in qids:
        label, _ = get_info_for_entity(session, qid)
        print(f"QID: {qid}, Label: {label}")
        
        # Add new claims to the entity using the edit_entitys function
        edit_entitys(session, csrf_token, qid, new_claims)
        
        # Adding a random delay to avoid hitting rate limits
        time.sleep(random.uniform(5, 10))  # Increased delay to avoid throttling

if __name__ == "__main__":
    main()

2024-10-22 10:41:19,506 - INFO - Attempt 1/5 to add claim: {'snaktype': 'value', 'property': 'P22', 'value': '"Person"'}
2024-10-22 10:41:19,556 - INFO - Claim added to QID Q1 on attempt 1/5: {'snaktype': 'value', 'property': 'P22', 'value': '"Person"'}


Logged in successfully!
Total Entities: 192
QID: Q1, Label: Rosenthal Ester(a)


2024-10-22 10:41:25,024 - INFO - Attempt 1/5 to add claim: {'snaktype': 'value', 'property': 'P22', 'value': '"Person"'}
2024-10-22 10:41:25,081 - INFO - Claim added to QID Q10 on attempt 1/5: {'snaktype': 'value', 'property': 'P22', 'value': '"Person"'}


QID: Q10, Label: Lipka Sara Frajda


2024-10-22 10:41:31,087 - INFO - Attempt 1/5 to add claim: {'snaktype': 'value', 'property': 'P22', 'value': '"Person"'}
2024-10-22 10:41:31,141 - INFO - Claim added to QID Q100 on attempt 1/5: {'snaktype': 'value', 'property': 'P22', 'value': '"Person"'}


...

QID: Q97, Label: Ermann Salomon Leo


2024-10-22 11:08:20,537 - INFO - Attempt 1/5 to add claim: {'snaktype': 'value', 'property': 'P22', 'value': '"Person"'}
2024-10-22 11:08:20,595 - INFO - Claim added to QID Q98 on attempt 1/5: {'snaktype': 'value', 'property': 'P22', 'value': '"Person"'}


QID: Q98, Label: Joseph LEVY "Joseph dit Jos."


2024-10-22 11:08:29,270 - INFO - Attempt 1/5 to add claim: {'snaktype': 'value', 'property': 'P22', 'value': '"Person"'}
2024-10-22 11:08:29,324 - INFO - Claim added to QID Q99 on attempt 1/5: {'snaktype': 'value', 'property': 'P22', 'value': '"Person"'}


QID: Q99, Label: Wonagus Max


### Adding these Entity ID to Records

### BULK Update for All Existing the Entities in the wikibase(add 1 property automatically from each Json Profile Directory)

This code basiccaly take the newly added attribute in Recods of each JSON-profile and added it to existing Record of the wikibase but it requires the the to create the property first and update the give property ID accordingly in this code   

In [ ]:
import os
import requests
import json
import urllib3
import time
import logging  # Added for logging errors

from datetime import datetime

# Disable SSL warnings (only if you're working in a non-production environment)
urllib3.disable_warnings(urllib3.exceptions.InsecureRequestWarning)

# Define the API endpoint
api_url = "https://wikibase.example.com/w/api.php"  # Replace with your actual API URL

# Your bot's credentials
USERNAME = "admin"  # Replace with your username
PASSWORD = "change-this-password"  # Replace with your password

# Directory containing the JSON profiles
# Directory containing the JSON profiles
input_directory = "/Users/ismail.ahouari/wikibase-release-pipeline/deploy/profiles/"   # Replace with your actual directory path

def login_to_wikibase():
    session = requests.Session()
    
    params = {
        "action": "query",
        "meta": "tokens",
        "type": "login",
        "format": "json"
    }

    response = session.get(api_url, params=params, verify=False)

    if response.status_code == 200:
        data = response.json()
        login_token = data['query']['tokens']['logintoken']
    else:
        raise Exception(f"Failed to retrieve login token. Status code: {response.status_code}")

    login_params = {
        "action": "clientlogin",
        "username": USERNAME,
        "password": PASSWORD,
        "logintoken": login_token,
        "loginreturnurl": api_url,
        "format": "json"
    }

    login_response = session.post(api_url, data=login_params, verify=False)

    if login_response.status_code == 200:
        login_data = login_response.json()
        if login_data.get("clientlogin", {}).get("status") == "PASS":
            print("Logged in successfully!")
        else:
            raise Exception(f"Failed to log in: {login_data}")
    else:
        raise Exception(f"Login request failed with status code: {login_response.status_code}")

    return session

def get_csrf_token(session):
    csrf_params = {
        "action": "query",
        "meta": "tokens",
        "type": "csrf",
        "format": "json"
    }

    csrf_response = session.get(api_url, params=csrf_params, verify=False)

    if csrf_response.status_code == 200:
        csrf_data = csrf_response.json()
        return csrf_data['query']['tokens']['csrftoken']
    else:
        raise Exception(f"Failed to retrieve CSRF token. Status code: {csrf_response.status_code}")

# Function to get detailed information about an entity
def get_info_for_entity(session, qid):
    params = {
        "action": "wbgetentities",
        "ids": qid,
        "props": "labels|claims|descriptions|aliases",
        "languages": "en",
        "format": "json"
    }

    try:
        response = session.get(api_url, params=params, verify=False)  # Disable SSL verification
        response.raise_for_status()
        data = response.json()

        label = "No label found"
        description = "No description found"
        aliases = []
        claims = {}

        if "entities" in data and qid in data["entities"]:
            entity = data["entities"][qid]

            # Extract label
            if "labels" in entity and "en" in entity["labels"]:
                label = entity["labels"]["en"]["value"]

            # Extract description
            if "descriptions" in entity and "en" in entity["descriptions"]:
                description = entity["descriptions"]["en"]["value"]

            # Extract aliases
            if "aliases" in entity and "en" in entity["aliases"]:
                aliases = [alias["value"] for alias in entity["aliases"]["en"]]

            # Extract all claims
            if "claims" in entity:
                for prop_id, prop_claims in entity["claims"].items():
                    claims[prop_id] = []
                    for claim in prop_claims:
                        value = claim["mainsnak"].get("datavalue", {}).get("value")
                        claims[prop_id].append(value)

        return label, description, aliases, claims

    except requests.RequestException as e:
        logging.error(f"Error fetching entity data for QID {qid}: {e}")
        return "Error", "Error", [], {}

# Function to search for an existing entity by label and description
def find_existing_entity(session, label, description, language='en'):
    search_params = {
        'action': 'wbsearchentities',
        'search': label,
        'language': language,
        'format': 'json',
        'type': 'item'
    }

    search_response = session.get(api_url, params=search_params, verify=False)

    if search_response.status_code == 200:
        search_data = search_response.json()
        for entity in search_data.get('search', []):
            # Compare both the label and description to identify the correct entity
            if entity['label'] == label and entity.get('description', '') == description:
                print(f"Found existing entity: {entity['id']} for label: {label}")
                return entity['id']  # Return the ID of the matching entity
    else:
        print(f"Failed to search for entity with label: {label}. Status code: {search_response.status_code}")
    return None






def create_or_update_entity(session, csrf_token, person_data):
    label = f"{person_data['first_name']} {person_data['last_name']}"
    description = f"Profile of {label}"

    existing_entity_id = find_existing_entity(session, label, description)
    
    if existing_entity_id:
        print(f"Entity already exists: {existing_entity_id}. Proceeding to update.")
        return existing_entity_id

    entity_data = {
        'labels': {'en': {'language': 'en', 'value': label}},
        'descriptions': {'en': {'language': 'en', 'value': description}},
        'claims': []
    }

    response = session.post(api_url, data={
        'action': 'wbeditentity',
        'new': 'item',
        'token': csrf_token,
        'data': json.dumps(entity_data),
        'format': 'json'
    }, verify=False)

    if response.status_code == 200:
        response_data = response.json()
        if 'error' in response_data:
            if 'already has label' in response_data['error']['info']:
                print(f"Error during entity creation: {response_data['error']['info']}")
                
                # Print the full error message for debugging
                print("Full error response:", json.dumps(response_data['error'], indent=2))
                
                # Extract the entity ID from the "parameters" field in the error message
                conflicting_entity_id = None
                if 'messages' in response_data['error'] and isinstance(response_data['error']['messages'], list):
                    for message in response_data['error']['messages']:
                        if isinstance(message, dict) and 'parameters' in message and isinstance(message['parameters'], list):
                            for param in message['parameters']:
                                if param.startswith('[[Item:'):
                                    conflicting_entity_id = param.split(':')[1].split('|')[0].strip()
                                    break
                        if conflicting_entity_id:
                            break
                
                if conflicting_entity_id:
                    label, description, aliases, claims = get_info_for_entity(session, conflicting_entity_id)
                    print(f"Fetched existing entity details: Label - {label}, Description - {description}, Aliases - {aliases}, Claims - {claims}")
                    return conflicting_entity_id
                else:
                    print("Could not determine the conflicting entity ID from the error message.")
                    return None
            else:
                raise Exception(f"Failed to create entity: {response_data['error']['info']}")
        else:
            print(f"Created new entity: {response_data['entity']['id']}")
            return response_data['entity']['id']
    else:
        print(f"Failed to create entity for {label}. Status code: {response.status_code}")
        return None






def statement_exists(entity_data, property_id, value):
    claims = entity_data.get('claims', {})
    
    if property_id in claims:
        for claim in claims[property_id]:
            existing_value = claim['mainsnak'].get('datavalue', {}).get('value')
            if existing_value == value:
                return True
    return False

def get_entity_data(session, entity_id):
    retrieve_params = {
        'action': 'wbgetentities',
        'ids': entity_id,
        'format': 'json'
    }
    
    retrieve_response = session.get(api_url, params=retrieve_params, verify=False)
    
    if retrieve_response.status_code == 200:
        entity_data = retrieve_response.json().get('entities', {}).get(entity_id, {})
        return entity_data
    else:
        print(f"Failed to retrieve entity data for {entity_id}. Status code: {retrieve_response.status_code}")
        return None

def add_statements(session, csrf_token, entity_id, person_data):
    entity_data = get_entity_data(session, entity_id)

    if not entity_data:
        print(f"Skipping entity {entity_id} due to failure in retrieving entity data.")
        return

    statements = {
        "P1": {"value": person_data.get('household_org', "Unknown"), "type": "string"},
    }

    for prop_id, value_data in statements.items():
        if not statement_exists(entity_data, prop_id, value_data['value']):
            claim_params = {
                'action': 'wbcreateclaim',
                'entity': entity_id,
                'snaktype': 'value',
                'property': prop_id,
                'value': json.dumps(value_data['value']),
                'token': csrf_token,
                'format': 'json'
            }

            claim_response = session.post(api_url, data=claim_params, verify=False)

            if claim_response.status_code == 200:
                claim_data = claim_response.json()
                if 'error' in claim_data:
                    print(f"Failed to add statement for property {prop_id}: {claim_data['error']['info']}")
                else:
                    print(f"Statement added successfully for property {prop_id}")
            else:
                print(f"Failed to add statement for property {prop_id} with status code: {claim_response.status_code}")
        else:
            print(f"Statement for property {prop_id} already exists. Skipping.")

def process_profiles():
    session = login_to_wikibase()
    csrf_token = get_csrf_token(session)
    
    for filename in os.listdir(input_directory):
        if filename.endswith(".json"):
            file_path = os.path.join(input_directory, filename)
            with open(file_path, "r", encoding="utf-8") as file:
                person_data = json.load(file)
                entity_id = create_or_update_entity(session, csrf_token, person_data)
                if entity_id is None:
                    print(f"Skipping profile {filename} because entity creation or identification failed.")
                    continue
                print(f"Processing entity {entity_id} for {filename}")
                add_statements(session, csrf_token, entity_id, person_data)
                time.sleep(3)

# Run the process
process_profiles()



### Adding the Slug (Entity ID) to each record

In [271]:
import os
import requests
import json
import urllib3
import logging
import time

# Disable SSL warnings (only if you're working in a non-production environment)
urllib3.disable_warnings(urllib3.exceptions.InsecureRequestWarning)

# Define the API endpoint
api_url = "https://wikibase.example.com/w/api.php"  # Replace with your actual API URL

# Your bot's credentials
USERNAME = "admin"  # Replace with your username
PASSWORD = "change-this-password"  # Replace with your password

# Directory containing the JSON profiles
input_directory = "/Users/ismail.ahouari/Public/wikibase-release-pipeline/deploy/reecords/"  # Replace with your actual directory path

# Property ID for "Entity ID" (P26)
PROPERTY_ID = "P26"

# Function to log in to Wikibase
def login_to_wikibase():
    session = requests.Session()
    
    # Step 1: Retrieve the login token
    params = {
        "action": "query",
        "meta": "tokens",
        "type": "login",
        "format": "json"
    }

    response = session.get(api_url, params=params, verify=False)

    if response.status_code == 200:
        data = response.json()
        login_token = data['query']['tokens']['logintoken']
    else:
        raise Exception(f"Failed to retrieve login token. Status code: {response.status_code}")

    # Step 2: Log in using the login token
    login_params = {
        "action": "clientlogin",
        "username": USERNAME,
        "password": PASSWORD,
        "logintoken": login_token,
        "loginreturnurl": api_url,  # Replace with your return URL
        "format": "json"
    }

    login_response = session.post(api_url, data=login_params, verify=False)

    if login_response.status_code == 200:
        login_data = login_response.json()
        if login_data.get("clientlogin", {}).get("status") == "PASS":
            print("Logged in successfully!")
        else:
            raise Exception(f"Failed to log in: {login_data}")
    else:
        raise Exception(f"Login request failed with status code: {login_response.status_code}")

    return session

# Function to retrieve CSRF token
def get_csrf_token(session):
    csrf_params = {
        "action": "query",
        "meta": "tokens",
        "type": "csrf",
        "format": "json"
    }

    csrf_response = session.get(api_url, params=csrf_params, verify=False)

    if csrf_response.status_code == 200:
        csrf_data = csrf_response.json()
        return csrf_data['query']['tokens']['csrftoken']
    else:
        raise Exception(f"Failed to retrieve CSRF token. Status code: {csrf_response.status_code}")

# Function to check if a statement already exists
def statement_exists(entity_data, property_id, value):
    claims = entity_data.get('claims', {})
    
    if property_id in claims:
        for claim in claims[property_id]:
            existing_value = claim['mainsnak'].get('datavalue', {}).get('value')
            if existing_value == value:
                return True
    return False

# Function to get entity data
def get_entity_data(session, entity_id):
    retrieve_params = {
        'action': 'wbgetentities',
        'ids': entity_id,
        'format': 'json'
    }
    
    retrieve_response = session.get(api_url, params=retrieve_params, verify=False)
    
    if retrieve_response.status_code == 200:
        entity_data = retrieve_response.json().get('entities', {}).get(entity_id, {})
        return entity_data
    else:
        print(f"Failed to retrieve entity data for {entity_id}. Status code: {retrieve_response.status_code}")
        return None

# Function to add the slug as a statement for "Entity ID"
def add_slug_as_statement(session, csrf_token, entity_id, slug, property_id):
    entity_data = get_entity_data(session, entity_id)

    if not entity_data:
        print(f"Skipping entity {entity_id} due to failure in retrieving entity data.")
        return

    if not statement_exists(entity_data, property_id, slug):
        claim_params = {
            'action': 'wbcreateclaim',
            'entity': entity_id,
            'snaktype': 'value',
            'property': property_id,
            'value': json.dumps(slug),
            'token': csrf_token,
            'format': 'json'
        }

        claim_response = session.post(api_url, data=claim_params, verify=False)

        if claim_response.status_code == 200:
            claim_data = claim_response.json()
            if 'error' in claim_data:
                print(f"Failed to add statement for 'Entity ID': {claim_data['error']['info']}")
            else:
                print(f"Slug '{slug}' added successfully as 'Entity ID' for entity {entity_id}")
        else:
            print(f"Failed to add statement for 'Entity ID' with status code: {claim_response.status_code}")
    else:
        print(f"Statement for 'Entity ID' already exists for entity {entity_id}. Skipping.")

# Function to retrieve all entity IDs from Wikibase
def get_all_entities(session):
    entity_ids = []
    continue_param = None
    
    while True:
        params = {
            "action": "query",
            "list": "allpages",
            "apnamespace": 0,  # Namespace 0 for entities
            "aplimit": 50,     # Adjust this number as needed
            "format": "json"
        }
        
        if continue_param:
            params["apcontinue"] = continue_param

        response = session.get(api_url, params=params, verify=False)

        if response.status_code == 200:
            data = response.json()
            for page in data["query"]["allpages"]:
                entity_ids.append(f"Q{page['pageid']}")  # Assuming entity IDs are in the form of Qxxx
            
            if "continue" in data:
                continue_param = data["continue"].get("apcontinue")
            else:
                break
        else:
            print(f"Failed to retrieve entities. Status code: {response.status_code}")
            break

    return entity_ids

# Main processing logic for profiles
def process_profiles():
    session = login_to_wikibase()
    csrf_token = get_csrf_token(session)

    # Get all entities from Wikibase
    entity_ids = get_all_entities(session)
    
    # Process each profile and add slug to existing entities
    for filename in os.listdir(input_directory):
        if filename.endswith(".json"):
            file_path = os.path.join(input_directory, filename)
            with open(file_path, "r", encoding="utf-8") as file:
                person_data = json.load(file)
                slug = person_data.get("slug")
                
                if not slug:
                    print(f"No slug found in {filename}. Skipping.")
                    continue

                # Loop over all existing entities
                for entity_id in entity_ids:
                    print(f"Processing entity {entity_id} for profile {filename}")
                    add_slug_as_statement(session, csrf_token, entity_id, slug, PROPERTY_ID)
                    time.sleep(3)  # Optional delay to avoid overwhelming the server
    
    print("All profiles processed successfully.")

if __name__ == "__main__":
    process_profiles()

Logged in successfully!
Processing entity Q1 for profile dura-margarete.json
Slug 'dura-margarete' added successfully as 'Entity ID' for entity Q1
Processing entity Q1 for profile rothschild-elisabeth.json
Slug 'rothschild-elisabeth' added successfully as 'Entity ID' for entity Q1
Processing entity Q1 for profile rosenthal-rozenthal-albert-aron-abraham.json
Slug 'rosenthal-rozenthal-albert-aron-abraham' added successfully as 'Entity ID' for entity Q1
Processing entity Q1 for profile herrmann-robert.json
Slug 'herrmann-robert' added successfully as 'Entity ID' for entity Q1
Processing entity Q1 for profile wonagus-joseph.json
Slug 'wonagus-joseph' added successfully as 'Entity ID' for entity Q1
Processing entity Q1 for profile rudow-rudovs-elie-khonon-dit-hans.json
Slug 'rudow-rudovs-elie-khonon-dit-hans' added successfully as 'Entity ID' for entity Q1
Processing entity Q1 for profile rudow-rudovs-erich.json
Slug 'rudow-rudovs-erich' added successfully as 'Entity ID' for entity Q1
Proce

### remove Entities' statement

In [ ]:
import os
import requests
import json
import urllib3
import time
import logging

# Set up logging configuration
logging.basicConfig(
    filename="wikibase_processing.log",
    level=logging.INFO,
    format="%(asctime)s - %(levelname)s - %(message)s"
)

# Disable SSL warnings (only if you're working in a non-production environment)
urllib3.disable_warnings(urllib3.exceptions.InsecureRequestWarning)

# Define the API endpoint
api_url = "https://wikibase.example.com/w/api.php"  # Replace with your actual API URL

# Your bot's credentials
USERNAME = "admin"  # Replace with your username
PASSWORD = "change-this-password"  # Replace with your password

def login_to_wikibase():
    session = requests.Session()
    
    params = {
        "action": "query",
        "meta": "tokens",
        "type": "login",
        "format": "json"
    }

    response = session.get(api_url, params=params, verify=False)

    if response.status_code == 200:
        data = response.json()
        login_token = data['query']['tokens']['logintoken']
        logging.info("Login token retrieved successfully.")
    else:
        logging.error(f"Failed to retrieve login token. Status code: {response.status_code}")
        raise Exception(f"Failed to retrieve login token. Status code: {response.status_code}")

    login_params = {
        "action": "clientlogin",
        "username": USERNAME,
        "password": PASSWORD,
        "logintoken": login_token,
        "loginreturnurl": api_url,
        "format": "json"
    }

    login_response = session.post(api_url, data=login_params, verify=False)

    if login_response.status_code == 200:
        login_data = login_response.json()
        if login_data.get("clientlogin", {}).get("status") == "PASS":
            logging.info("Logged in successfully!")
        else:
            logging.error(f"Failed to log in: {login_data}")
            raise Exception(f"Failed to log in: {login_data}")
    else:
        logging.error(f"Login request failed with status code: {login_response.status_code}")
        raise Exception(f"Login request failed with status code: {login_response.status_code}")

    return session

def get_csrf_token(session):
    csrf_params = {
        "action": "query",
        "meta": "tokens",
        "type": "csrf",
        "format": "json"
    }

    csrf_response = session.get(api_url, params=csrf_params, verify=False)

    if csrf_response.status_code == 200:
        csrf_data = csrf_response.json()
        logging.info("CSRF token retrieved successfully.")
        return csrf_data['query']['tokens']['csrftoken']
    else:
        logging.error(f"Failed to retrieve CSRF token. Status code: {csrf_response.status_code}")
        raise Exception(f"Failed to retrieve CSRF token. Status code: {csrf_response.status_code}")
    

def get_all_entities(session):
    """Retrieve all entity IDs in the Wikibase instance."""
    all_entities = []
    params = {
        'action': 'query',
        'list': 'allpages',
        'apnamespace': 120,  # Namespace 0 typically represents items
        'format': 'json',
        'aplimit': 'max'
    }

    while True:
        response = session.get(api_url, params=params, verify=False)
        if response.status_code == 200:
            data = response.json()
            for page in data['query']['allpages']:
                title = page['title']
                # Add all entities without filtering by "Q" prefix
                all_entities.append(title)
            logging.info(f"Retrieved batch of entities. Total so far: {len(all_entities)}")

            if 'continue' in data:
                params.update(data['continue'])
            else:
                break
        else:
            logging.error(f"Failed to retrieve entities. Status code: {response.status_code}")
            break

    logging.info(f"Total entities found: {len(all_entities)}")
    return all_entities

def remove_all_p26_statements(session, csrf_token, entity_id):
    """Remove all P26 statements from a given entity."""
    entity_data = get_entity_data(session, entity_id)
    if not entity_data:
        logging.warning(f"Skipping entity {entity_id} due to failure in retrieving entity data.")
        return

    claims = entity_data.get('claims', {})
    if "P26" in claims:
        for claim in claims["P26"]:
            claim_id = claim['id']
            # Remove each claim for P26
            remove_params = {
                'action': 'wbremoveclaims',
                'claim': claim_id,
                'token': csrf_token,
                'format': 'json'
            }
            remove_response = session.post(api_url, data=remove_params, verify=False)
            if remove_response.status_code == 200:
                logging.info(f"Removed statement {claim_id} for property P26 in entity {entity_id}")
            else:
                logging.error(f"Failed to remove statement {claim_id} for property P26 in entity {entity_id}. Status code: {remove_response.status_code}")

def get_entity_data(session, entity_id):
    """Retrieve data for a specific entity."""
    
    # Ensure the entity_id is in the correct format (e.g., "Q1" instead of "Item:Q1")
    entity_id = entity_id.replace("Item:", "")
    
    retrieve_params = {
        'action': 'wbgetentities',
        'ids': entity_id,
        'format': 'json'
    }

    # Log the request parameters for debugging
    logging.info(f"Requesting data for entity {entity_id} with params: {retrieve_params}")
    
    retrieve_response = session.get(api_url, params=retrieve_params, verify=False)

    # Log the raw API response
    logging.info(f"Raw response for entity {entity_id}: {retrieve_response.text}")

    if retrieve_response.status_code == 200:
        entity_data = retrieve_response.json().get('entities', {}).get(entity_id, {})
        
        # Log the retrieved entity data (should show claims and other details if successful)
        logging.info(f"Retrieved data for entity {entity_id}: {json.dumps(entity_data, indent=2)}")

        # Return the entity data if it is not empty, otherwise log a warning
        if entity_data:
            return entity_data
        else:
            logging.warning(f"No data found for entity {entity_id}. The response might be empty or malformed.")
            return None
    else:
        logging.error(f"Failed to retrieve entity data for {entity_id}. Status code: {retrieve_response.status_code}")
        return None

def process_entities():
    """Process all entities to remove any existing P26 statements."""
    session = login_to_wikibase()
    csrf_token = get_csrf_token(session)

    logging.info("Starting to process all entities...")

    all_entities = get_all_entities(session)
    logging.info(f"Total entities to process: {len(all_entities)}")

    for entity_id in all_entities:
        logging.info(f"Processing entity {entity_id}")
        remove_all_p26_statements(session, csrf_token, entity_id)
        time.sleep(1)  # To prevent overloading the server with requests

# Run the process to remove all P26 statements from every entity
process_entities()

#### Create Geoname property

Logged in successfully!
Property 'GeoNames ID' created with ID: P23


#### ADDING QUATIFIERS TO EXIT STATEMENT  ---- NOT DONE YET!

In [40]:
import os
import requests
import json
import time
import logging

from datetime import datetime

# Disable SSL warnings (only if you're working in a non-production environment)
requests.packages.urllib3.disable_warnings(requests.packages.urllib3.exceptions.InsecureRequestWarning)

# Define the API endpoint
api_url = "https://wikibase.example.com/w/api.php"

# Your bot's credentials
USERNAME = "admin"
PASSWORD = "change-this-password"

# Directory containing the JSON profiles
input_directory = "/path/to/profiles/"

def login_to_wikibase():
    session = requests.Session()
    
    params = {
        "action": "query",
        "meta": "tokens",
        "type": "login",
        "format": "json"
    }

    response = session.get(api_url, params=params, verify=False)

    if response.status_code == 200:
        data = response.json()
        login_token = data['query']['tokens']['logintoken']
    else:
        raise Exception(f"Failed to retrieve login token. Status code: {response.status_code}")

    login_params = {
        "action": "clientlogin",
        "username": USERNAME,
        "password": PASSWORD,
        "logintoken": login_token,
        "loginreturnurl": api_url,
        "format": "json"
    }

    login_response = session.post(api_url, data=login_params, verify=False)

    if login_response.status_code == 200:
        login_data = login_response.json()
        if login_data.get("clientlogin", {}).get("status") == "PASS":
            print("Logged in successfully!")
        else:
            raise Exception(f"Failed to log in: {login_data}")
    else:
        raise Exception(f"Login request failed with status code: {login_response.status_code}")

    return session

def get_csrf_token(session):
    csrf_params = {
        "action": "query",
        "meta": "tokens",
        "type": "csrf",
        "format": "json"
    }

    csrf_response = session.get(api_url, params=csrf_params, verify=False)

    if csrf_response.status_code == 200:
        csrf_data = csrf_response.json()
        return csrf_data['query']['tokens']['csrftoken']
    else:
        raise Exception(f"Failed to retrieve CSRF token. Status code: {csrf_response.status_code}")

def get_entity_data(session, entity_id):
    params = {
        "action": "wbgetentities",
        "ids": entity_id,
        "props": "labels|claims|descriptions|aliases",
        "languages": "en",
        "format": "json"
    }

    try:
        response = session.get(api_url, params=params, verify=False)
        response.raise_for_status()
        return response.json().get('entities', {}).get(entity_id, {})
    except requests.RequestException as e:
        logging.error(f"Error fetching entity data for QID {entity_id}: {e}")
        return {}

def statement_exists(entity_data, property_id, value):
    claims = entity_data.get('claims', {})
    
    if property_id in claims:
        for claim in claims[property_id]:
            existing_value = claim['mainsnak'].get('datavalue', {}).get('value')
            if existing_value == value:
                return True
    return False

def add_qualifier(session, csrf_token, claim_id, qualifier_property, qualifier_value):
    params = {
        'action': 'wbsetqualifier',
        'claim': claim_id,
        'property': qualifier_property,
        'value': json.dumps(qualifier_value['datavalue']['value']),
        'snaktype': qualifier_value['snaktype'],
        'token': csrf_token,
        'format': 'json'
    }

    response = session.post(api_url, data=params, verify=False)
    if response.status_code == 200:
        response_data = response.json()
        if 'error' in response_data:
            if 'already a qualifier' in response_data['error']['info']:
                print(f"The statement already has this qualifier: {response_data['error']['info']}")
            else:
                print(f"Failed to add qualifier for claim {claim_id}: {response_data['error']['info']}")
        else:
            print(f"Qualifier added successfully for claim {claim_id}")
    else:
        print(f"Failed to add qualifier for claim {claim_id}. Status code: {response.status_code}")

def get_claim_id(entity_data, property_id, value):
    claims = entity_data.get('claims', {})
    if property_id in claims:
        for claim in claims[property_id]:
            existing_value = claim['mainsnak'].get('datavalue', {}).get('value')
            if existing_value == value:
                return claim['id']
    return None



def qualifier_exists(claim, qualifier_property, qualifier_value):
    """
    Checks if a qualifier with the given property and value already exists on the claim.
    """
    qualifiers = claim.get('qualifiers', {}).get(qualifier_property, [])
    for qualifier in qualifiers:
        existing_value = qualifier.get('datavalue', {}).get('value')
        if existing_value == qualifier_value:
            return True
    return False

def add_qualifier(session, csrf_token, claim_id, qualifier_property, qualifier_value):
    """
    Adds a qualifier to a specific claim if it does not already exist.
    """
    if not claim_id:
        print(f"Cannot add qualifier. Claim ID is invalid or does not exist.")
        return

    # Check if the claim already has this qualifier
    claim_data = get_claim_data(session, claim_id)
    if qualifier_exists(claim_data, qualifier_property, qualifier_value['datavalue']['value']):
        print(f"Qualifier {qualifier_property} with value {qualifier_value['datavalue']['value']} already exists on claim {claim_id}. Skipping.")
        return

    params = {
        'action': 'wbsetqualifier',
        'claim': claim_id,
        'property': qualifier_property,
        'value': json.dumps(qualifier_value['datavalue']['value']),
        'snaktype': qualifier_value['snaktype'],
        'token': csrf_token,
        'format': 'json'
    }

    response = session.post(api_url, data=params, verify=False)
    response_data = response.json()
    
    if response.status_code == 200:
        if 'error' in response_data:
            print(f"Failed to add qualifier for claim {claim_id}: {response_data['error']['info']}")
        else:
            print(f"Qualifier added successfully for claim {claim_id}")
    else:
        print(f"Failed to add qualifier for claim {claim_id}. Status code: {response.status_code}, Response: {response_data}")



def add_statements_and_qualifiers(session, csrf_token, entity_id, person_data):
    """
    Adds statements and qualifiers to the entity.
    """
    entity_data = get_entity_data(session, entity_id)

    if not entity_data:
        print(f"Skipping entity {entity_id} due to failure in retrieving entity data.")
        return

    person_details = person_data.get('data', {})
    related_places = person_data.get('related-places', [])

    # Assign "Unknown" if the field is missing or empty
    statements = {
        "P207": {"value": person_details.get('birth_place', "Unknown") or "Unknown", "type": "string"},
        "P166": {"value": person_details.get('birth_country', "Unknown") or "Unknown", "type": "string"},
        "P186": {"value": person_details.get('exit_19411016_to_19440910_place', "Unknown") or "Unknown", "type": "string"},
        "P209": {"value": person_details.get('nationality', "Unknown") or "Unknown", "type": "string"},
    }

    # A map to associate properties with the corresponding relatedField for qualifier
    property_to_related_field = {
        "P207": "birth_place",
        "P166": "birth_country",
        "P186": "exit_19411016_to_19440910_place",
        "P209": "nationality"
    }

    for prop_id, value_data in statements.items():
        if statement_exists(entity_data, prop_id, value_data['value']):
            print(f"Statement for property {prop_id} already exists. Adding qualifiers if needed.")
            
            # Retrieve all claims for this property
            claims = entity_data.get('claims', {}).get(prop_id, [])
            for claim in claims:
                existing_value = claim['mainsnak'].get('datavalue', {}).get('value')
                if existing_value == value_data['value']:
                    claim_id = claim['id']

                    # Find the related place data for the current property
                    related_field = property_to_related_field.get(prop_id)
                    qualifier_value_data = next(
                        (place for place in related_places if place['relatedField'] == related_field),
                        None
                    )

                    # Use "Unknown" if the relatedField data is missing or empty
                    qualifier_value_str = str(qualifier_value_data['geonameId']) if qualifier_value_data and qualifier_value_data['geonameId'] else "Unknown"

                    qualifier_property = "P243"  # Replace with the actual qualifier property you want to add
                    qualifier_value = {
                        "snaktype": "value",
                        "property": qualifier_property,
                        "datavalue": {
                            "value": qualifier_value_str,
                            "type": "string"
                        }
                    }

                    # Add the qualifier to this claim
                    try:
                        add_qualifier(session, csrf_token, claim_id, qualifier_property, qualifier_value)
                    except Exception as e:
                        print(f"Failed to add qualifier for claim {claim_id}: {e}")
        else:
            print(f"No existing statement found for property {prop_id}, skipping.")

    time.sleep(2)  # Adjust as needed to prevent rate-limiting issues








def get_claim_data(session, claim_id):
    """
    Fetches the details of a specific claim by its ID.
    """
    params = {
        'action': 'wbgetclaims',
        'claim': claim_id,
        'format': 'json'
    }
    
    response = session.get(api_url, params=params, verify=False)
    data = response.json()
    
    if response.status_code == 200 and 'claims' in data:
        return data['claims']
    else:
        print(f"Failed to retrieve claim data for claim ID: {claim_id}. Status code: {response.status_code}, Response: {data}")
        return {}

def qualifier_exists(claim, qualifier_property, qualifier_value):
    """
    Checks if a qualifier with the given property and value already exists on the claim.
    """
    qualifiers = claim.get('qualifiers', {}).get(qualifier_property, [])
    for qualifier in qualifiers:
        existing_value = qualifier.get('datavalue', {}).get('value')
        if existing_value == qualifier_value:
            return True
    return False

def add_statements_and_qualifiers(session, csrf_token, entity_id, person_data):
    """
    Adds statements and qualifiers to the entity.
    """
    entity_data = get_entity_data(session, entity_id)

    if not entity_data:
        print(f"Skipping entity {entity_id} due to failure in retrieving entity data.")
        return

    person_details = person_data.get('data', {})
    related_places = person_data.get('related-places', [])

    # Assign "Unknown" if the field is missing or empty
    statements = {
        "P207": {"value": person_details.get('birth_place', "Unknown") or "Unknown", "type": "string"},
        "P166": {"value": person_details.get('birth_country', "Unknown") or "Unknown", "type": "string"},
        "P173": {"value": person_details.get('death_country', "Unknown") or "Unknown", "type": "string"},
        "P186": {"value": person_details.get('exit_19411016_to_19440910_place', "Unknown") or "Unknown", "type": "string"},
        "P184": {"value": person_details.get('exit_19400510_to_19411015_place', "Unknown") or "Unknown", "type": "string"},
        "P178": {"value": person_details.get('convoy_place', "Unknown") or "Unknown", "type": "string"},
        "P180": {"value": person_details.get('enter_place', "Unknown") or "Unknown", "type": "string"},
        "P209": {"value": person_details.get('nationality', "Unknown") or "Unknown", "type": "string"},
        "P172": {"value": person_details.get('death_place_alt', "Unknown") or "Unknown", "type": "string"}
    }

    # A map to associate properties with the corresponding relatedField for qualifier
    property_to_related_field = {
        "P207": "birth_place",
        "P166": "birth_country",
        "P186": "exit_19411016_to_19440910_place",
        "P184": "exit_19400510_to_19411015_place",
        "P209": "nationality",
        "P173": "death_place",
        "P180": "enter_place",
        "P178": "convoy_place",
        "P172":"death_place_alt"
    }

    for prop_id, value_data in statements.items():
        if statement_exists(entity_data, prop_id, value_data['value']):
            print(f"Statement for property {prop_id} already exists. Adding qualifiers if needed.")
            
            # Retrieve all claims for this property
            claims = entity_data.get('claims', {}).get(prop_id, [])
            for claim in claims:
                existing_value = claim['mainsnak'].get('datavalue', {}).get('value')
                if existing_value == value_data['value']:
                    claim_id = claim['id']

                    # Find the related place data for the current property
                    related_field = property_to_related_field.get(prop_id)
                    qualifier_value_data = next(
                        (place for place in related_places if place['relatedField'] == related_field),
                        None
                    )

                    # Use "Unknown" if the relatedField data is missing or empty
                    qualifier_value_str = str(qualifier_value_data['geonameId']) if qualifier_value_data and qualifier_value_data['geonameId'] else "Unknown"

                    qualifier_property = "P243"  # Replace with the actual qualifier property you want to add
                    qualifier_value = {
                        "snaktype": "value",
                        "property": qualifier_property,
                        "datavalue": {
                            "value": qualifier_value_str,
                            "type": "string"
                        }
                    }

                    # Debugging Output
                    print(f"Adding qualifier: claim_id={claim_id}, property={qualifier_property}, value={qualifier_value_str}")

                    # Add the qualifier to this claim
                    try:
                        add_qualifier(session, csrf_token, claim_id, qualifier_property, qualifier_value)
                    except Exception as e:
                        print(f"Failed to add qualifier for claim {claim_id}: {e}")
        else:
            print(f"No existing statement found for property {prop_id}, skipping.")

    time.sleep(2)  # Adjust as needed to prevent rate-limiting issues



    
def get_property_id_for_related_field(related_field):
    field_to_property_map = {
        "Exit Place 1940-1941": "P207",
        "birth_country": "P166",
        "death_place": "P208",
        "death_place_alt": "P172",
        "death_country": "P173",
        "death_country_alt": "P174",
        "convoy_place": "P178",
        "exit_19411016_to_19440910_place": "P186"
    }
    return field_to_property_map.get(related_field)

# Directory containing the JSON profiles
input_directory = "/Users/ismail.ahouari/wikibase-release-pipeline/deploy/profils/"   # Replace with your actual directory path

def process_profiles():
    session = login_to_wikibase()
    csrf_token = get_csrf_token(session)
    
    for filename in os.listdir(input_directory):
        if filename.endswith(".json"):
            file_path = os.path.join(input_directory, filename)
            with open(file_path, "r", encoding="utf-8") as file:
                person_data = json.load(file)
                entity_id = create_or_update_entity(session, csrf_token, person_data)
                if entity_id is None:
                    print(f"Skipping profile {filename} because entity creation or identification failed.")
                    continue
                print(f"Processing entity {entity_id} for {filename}")
                add_statements_and_qualifiers(session, csrf_token, entity_id, person_data)
                time.sleep(3)  # Adjust as needed

# Run the process
process_profiles()











Logged in successfully!
Error during entity creation: Item [[Item:Q514|Q514]] already has label "Wolf Judith (Judithe, Jehudit)" associated with language code en, using the same description text.
Fetched existing entity details: Label - Wolf Judith (Judithe, Jehudit), Description - Profile of Wolf Judith (Judithe, Jehudit), Aliases - [], Claims - {'P142': ['Unknown'], 'P53': [{'time': '+1930-11-07T00:00:00Z', 'timezone': 0, 'before': 0, 'after': 0, 'precision': 11, 'calendarmodel': 'http://www.wikidata.org/entity/Q1985727'}], 'P162': [{'time': '+1930-11-07T00:00:00Z', 'timezone': 0, 'before': 0, 'after': 0, 'precision': 11, 'calendarmodel': 'http://www.wikidata.org/entity/Q1985727'}], 'P207': ['Lodz'], 'P166': ['Pologne'], 'P170': ['194?'], 'P208': ['Unknown'], 'P172': ['Unknown'], 'P173': ['Unknown'], 'P174': ['Unknown'], 'P209': ['Polonaise'], 'P177': ['L-01'], 'P178': ['Luxembourg'], 'P179': [{'time': '+1941-10-16T00:00:00Z', 'timezone': 0, 'before': 0, 'after': 0, 'precision': 11, 

In [80]:
import os
import requests
import json
import time
import logging

from datetime import datetime

# Disable SSL warnings (only if you're working in a non-production environment)
requests.packages.urllib3.disable_warnings(requests.packages.urllib3.exceptions.InsecureRequestWarning)

# Define the API endpoint
api_url = "https://wikibase.example.com/w/api.php"

# Your bot's credentials
USERNAME = "admin"
PASSWORD = "change-this-password"

# Directory containing the JSON profiles
input_directory = "/path/to/profiles/"

def login_to_wikibase():
    session = requests.Session()
    
    params = {
        "action": "query",
        "meta": "tokens",
        "type": "login",
        "format": "json"
    }

    response = session.get(api_url, params=params, verify=False)

    if response.status_code == 200:
        data = response.json()
        login_token = data['query']['tokens']['logintoken']
    else:
        raise Exception(f"Failed to retrieve login token. Status code: {response.status_code}")

    login_params = {
        "action": "clientlogin",
        "username": USERNAME,
        "password": PASSWORD,
        "logintoken": login_token,
        "loginreturnurl": api_url,
        "format": "json"
    }

    login_response = session.post(api_url, data=login_params, verify=False)

    if login_response.status_code == 200:
        login_data = login_response.json()
        if login_data.get("clientlogin", {}).get("status") == "PASS":
            print("Logged in successfully!")
        else:
            raise Exception(f"Failed to log in: {login_data}")
    else:
        raise Exception(f"Login request failed with status code: {login_response.status_code}")

    return session

def get_csrf_token(session):
    csrf_params = {
        "action": "query",
        "meta": "tokens",
        "type": "csrf",
        "format": "json"
    }

    csrf_response = session.get(api_url, params=csrf_params, verify=False)

    if csrf_response.status_code == 200:
        csrf_data = csrf_response.json()
        return csrf_data['query']['tokens']['csrftoken']
    else:
        raise Exception(f"Failed to retrieve CSRF token. Status code: {csrf_response.status_code}")

def get_entity_data(session, entity_id):
    params = {
        "action": "wbgetentities",
        "ids": entity_id,
        "props": "labels|claims|descriptions|aliases",
        "languages": "en",
        "format": "json"
    }

    try:
        response = session.get(api_url, params=params, verify=False)
        response.raise_for_status()
        return response.json().get('entities', {}).get(entity_id, {})
    except requests.RequestException as e:
        logging.error(f"Error fetching entity data for QID {entity_id}: {e}")
        return {}

def statement_exists(entity_data, property_id, value):
    claims = entity_data.get('claims', {})
    
    if property_id in claims:
        for claim in claims[property_id]:
            existing_value = claim['mainsnak'].get('datavalue', {}).get('value')
            if existing_value == value:
                return True
    return False
def entity_exists(session, label, description, language="en"):
    """
    Check if an entity with the same label and description already exists.
    """
    search_params = {
        "action": "wbsearchentities",
        "search": label,
        "language": language,
        "type": "item",
        "format": "json"
    }

    response = session.get(api_url, params=search_params, verify=False)

    if response.status_code == 200:
        search_results = response.json().get('search', [])
        for result in search_results:
            # Check if the description matches as well
            if result.get('description') == description:
                return result['id']  # Return the entity ID if it exists
    return None


def add_qualifier(session, csrf_token, claim_id, qualifier_property, qualifier_value):
    params = {
        'action': 'wbsetqualifier',
        'claim': claim_id,
        'property': qualifier_property,
        'value': json.dumps(qualifier_value['datavalue']['value']),
        'snaktype': qualifier_value['snaktype'],
        'token': csrf_token,
        'format': 'json'
    }

    response = session.post(api_url, data=params, verify=False)
    if response.status_code == 200:
        response_data = response.json()
        if 'error' in response_data:
            if 'already a qualifier' in response_data['error']['info']:
                print(f"The statement already has this qualifier: {response_data['error']['info']}")
            else:
                print(f"Failed to add qualifier for claim {claim_id}: {response_data['error']['info']}")
        else:
            print(f"Qualifier added successfully for claim {claim_id}")
    else:
        print(f"Failed to add qualifier for claim {claim_id}. Status code: {response.status_code}")

def get_claim_id(entity_data, property_id, value):
    claims = entity_data.get('claims', {})
    if property_id in claims:
        for claim in claims[property_id]:
            existing_value = claim['mainsnak'].get('datavalue', {}).get('value')
            if existing_value == value:
                return claim['id']
    return None

def add_statements_and_qualifiers(session, csrf_token, entity_id, person_data):
    """
    Adds statements and qualifiers to the entity.
    """
    entity_data = get_entity_data(session, entity_id)

    if not entity_data:
        print(f"Skipping entity {entity_id} due to failure in retrieving entity data.")
        return

    person_details = person_data.get('data', {})
    related_places = person_data.get('related-places', [])

    # Assign "Unknown" if the field is missing or empty
    statements = {
        "P1": {"value": person_details.get('household_organization', "Unknown") or "Unknown", "type": "string"},
        "P2": {"value": person_details.get('first_name', "Unknown") or "Unknown", "type": "string"},
        "P3": {"value": person_details.get('last_name', "Unknown") or "Unknown", "type": "string"},
        "P4": {"value": person_details.get('last_name_changed', "Unknown") or "Unknown", "type": "string"},
        "P5": {"value": person_details.get('birth_date', "Unknown") or "Unknown", "type": "string"},
        "P6": {"value": person_details.get('birth_place', "Unknown") or "Unknown", "type": "string"},
        "P7": {"value": person_details.get('death_place', "Unknown") or "Unknown", "type": "string"},
        "P8": {"value": person_details.get('nationality', "Unknown") or "Unknown", "type": "string"},
        "P9": {"value": person_details.get('birth_country', "Unknown") or "Unknown", "type": "string"},
        "P10": {"value": person_details.get('death_date_notes', "Unknown") or "Unknown", "type": "string"},
        "P11": {"value": person_details.get('alternative_death_place', "Unknown") or "Unknown", "type": "string"},
        "P12": {"value": person_details.get('death_country', "Unknown") or "Unknown", "type": "string"},
        "P13": {"value": person_details.get('alternative_death_country', "Unknown") or "Unknown", "type": "string"},
        "P14": {"value": person_details.get('convoy', "Unknown") or "Unknown", "type": "string"},
        "P15": {"value": person_details.get('convoy_place', "Unknown") or "Unknown", "type": "string"},
        "P16": {"value": person_details.get('convoy_date', "Unknown") or "Unknown", "type": "string"},
        "P17": {"value": person_details.get('enter_date', "Unknown") or "Unknown", "type": "string"},
        "P18": {"value": person_details.get('exit_place_1940_1941', "Unknown") or "Unknown", "type": "string"},
        "P19": {"value": person_details.get('exit_place_1941_1944', "Unknown") or "Unknown", "type": "string"},
        "P20": {"value": person_details.get('profession', "Unknown") or "Unknown", "type": "string"},
        "P21": {"value": person_details.get('instance_of', "Unknown") or "Unknown", "type": "string"},
        "P22": {"value": person_details.get('instance_of_alt', "Unknown") or "Unknown", "type": "string"},
        "P23": {"value": person_details.get('geonames_id', "Unknown") or "Unknown", "type": "string"}
    }

    # A map to associate properties with the corresponding relatedField for qualifier
    property_to_related_field = {
        "P6": "birth_place",
        "P9": "birth_country",
        "P7": "death_place",
        "P12": "death_country",
        "P11": "alternative_death_place",
        "P13": "alternative_death_country",
        "P15": "convoy_place",
        "P18": "exit_place_1940_1941",
        "P19": "exit_place_1941_1944"
    }

    for prop_id, value_data in statements.items():
        if statement_exists(entity_data, prop_id, value_data['value']):
            print(f"Statement for property {prop_id} already exists. Adding qualifiers if needed.")
            
            # Retrieve all claims for this property
            claims = entity_data.get('claims', {}).get(prop_id, [])
            for claim in claims:
                existing_value = claim['mainsnak'].get('datavalue', {}).get('value')
                if existing_value == value_data['value']:
                    claim_id = claim['id']

                    # Find the related place data for the current property
                    related_field = property_to_related_field.get(prop_id)
                    qualifier_value_data = next(
                        (place for place in related_places if place['relatedField'] == related_field),
                        None
                    )

                    # Use "Unknown" if the relatedField data is missing or empty
                    qualifier_value_str = str(qualifier_value_data['geonameId']) if qualifier_value_data and qualifier_value_data['geonameId'] else "Unknown"

                    qualifier_property = "P23"  # GeoNames ID as qualifier
                    qualifier_value = {
                        "snaktype": "value",
                        "property": qualifier_property,
                        "datavalue": {
                            "value": qualifier_value_str,
                            "type": "string"
                        }
                    }

                    # Debugging Output
                    print(f"Adding qualifier: claim_id={claim_id}, property={qualifier_property}, value={qualifier_value_str}")

                    # Add the qualifier to this claim
                    try:
                        add_qualifier(session, csrf_token, claim_id, qualifier_property, qualifier_value)
                    except Exception as e:
                        print(f"Failed to add qualifier for claim {claim_id}: {e}")
        else:
            print(f"No existing statement found for property {prop_id}, skipping.")

    time.sleep(2)  # Adjust as needed to prevent rate-limiting issues

# Directory containing the JSON profiles
input_directory = "/Users/ismail.ahouari/public/wikibase-release-pipeline/deploy/reecords/"   # Replace with your actual

def process_profiles():
    session = login_to_wikibase()
    csrf_token = get_csrf_token(session)
    
    for filename in os.listdir(input_directory):
        if filename.endswith(".json"):
            file_path = os.path.join(input_directory, filename)
            with open(file_path, "r", encoding="utf-8") as file:
                person_data = json.load(file)
                entity_id = create_or_update_entity(session, csrf_token, person_data)
                if entity_id is None:
                    print(f"Skipping profile {filename} because entity creation or identification failed.")
                    continue
                print(f"Processing entity {entity_id} for {filename}")
                add_statements_and_qualifiers(session, csrf_token, entity_id, person_data)
                time.sleep(3)  # Adjust as needed

# Run the process
process_profiles()

Logged in successfully!
Failed to create entity: {'error': {'code': 'modification-failed', 'info': 'Item [[Item:Q2|Q2]] already has label "Dura Margarete" associated with language code en, using the same description text.', 'messages': [{'name': 'wikibase-validator-label-with-description-conflict', 'parameters': ['Dura Margarete', 'en', '[[Item:Q2|Q2]]'], 'html': {'*': 'Item <a href="/wiki/Item:Q2" title="Item:Q2">Q2</a> already has label "Dura Margarete" associated with language code en, using the same description text.'}}], '*': 'See https://wikibase.example.com/w/api.php for API usage. Subscribe to the mediawiki-api-announce mailing list at &lt;https://lists.wikimedia.org/postorius/lists/mediawiki-api-announce.lists.wikimedia.org/&gt; for notice of API deprecations and breaking changes.'}}
Skipping profile dura-margarete.json because entity creation or identification failed.
Failed to create entity: {'error': {'code': 'modification-failed', 'info': 'Item [[Item:Q3|Q3]] already has l

In [289]:
import os
import requests
import json
import time
import logging
from datetime import datetime

requests.packages.urllib3.disable_warnings(requests.packages.urllib3.exceptions.InsecureRequestWarning)

api_url = "https://wikibase.example.com/w/api.php"
USERNAME = "admin"
PASSWORD = "change-this-password"
input_directory = "/Users/ismail.ahouari/Public/wikibase-release-pipeline/deploy/reecords/"

def login_to_wikibase():
    session = requests.Session()
    params = {"action": "query", "meta": "tokens", "type": "login", "format": "json"}
    response = session.get(api_url, params=params, verify=False)
    login_token = response.json()['query']['tokens']['logintoken']
    login_params = {"action": "clientlogin", "username": USERNAME, "password": PASSWORD, "logintoken": login_token, "loginreturnurl": api_url, "format": "json"}
    session.post(api_url, data=login_params, verify=False)
    print("Logged in successfully!")
    return session

def get_csrf_token(session):
    csrf_params = {"action": "query", "meta": "tokens", "type": "csrf", "format": "json"}
    csrf_response = session.get(api_url, params=csrf_params, verify=False)
    return csrf_response.json()['query']['tokens']['csrftoken']

def get_entity_data(session, entity_id):
    params = {"action": "wbgetentities", "ids": entity_id, "props": "labels|claims|descriptions|aliases", "languages": "en", "format": "json"}
    response = session.get(api_url, params=params, verify=False)
    return response.json().get('entities', {}).get(entity_id, {})

def add_qualifier(session, csrf_token, claim_id, qualifier_property, qualifier_value):
    params = {'action': 'wbsetqualifier', 'claim': claim_id, 'property': qualifier_property, 'value': json.dumps(qualifier_value['datavalue']['value']), 'snaktype': qualifier_value['snaktype'], 'token': csrf_token, 'format': 'json'}
    response = session.post(api_url, data=params, verify=False)
    response_data = response.json()
    if response.status_code == 200 and 'success' in response_data:
        print(f"Qualifier added successfully for claim {claim_id}")
    else:
        print(f"Failed to add qualifier for claim {claim_id}: {response_data}")

def create_or_update_entity(session, csrf_token, person_data):
    slug = person_data.get('slug')
    entity_id = search_entity_by_slug(session, slug)
    if entity_id is None:
        print(f"No existing entity found for slug: {slug}. Skipping.")
    else:
        print(f"Entity for slug {slug} found: {entity_id}")
    return entity_id

def search_entity_by_slug(session, slug):
    params = {"action": "wbsearchentities", "search": slug, "language": "en", "format": "json"}
    response = session.get(api_url, params=params, verify=False)
    search_results = response.json().get('search', [])
    return search_results[0]['id'] if search_results else None

def add_statements_and_qualifiers(session, csrf_token, entity_id, person_data):
    entity_data = get_entity_data(session, entity_id)
    if not entity_data:
        print(f"Skipping entity {entity_id} due to failure in retrieving entity data.")
        return

    person_details = person_data.get('data', {})
    related_places = person_data.get('related-places', [])

    statements = {
        "P6": {"value": person_details.get('birth_place', "Unknown"), "type": "string"},
        "P7": {"value": person_details.get('death_place', "Unknown"), "type": "string"},
        "P8": {"value": person_details.get('nationality', "Unknown"), "type": "string"},
        "P9": {"value": person_details.get('birth_country', "Unknown"), "type": "string"},
        "P11": {"value": person_details.get('death_place_alt', "Unknown"), "type": "string"},
        "P12": {"value": person_details.get('death_country', "Unknown"), "type": "string"},
        "P15": {"value": person_details.get('convoy_place', "Unknown"), "type": "string"},
        "P18": {"value": person_details.get('exit_1940_1941_place', "Unknown"), "type": "string"},
        "P19": {"value": person_details.get('exit_1941_1944_place', "Unknown"), "type": "string"}
    }

    property_to_related_field = {
        "P6": "birth_place",
        "P7": "death_place",
        "P8": "nationality",
        "P9": "birth_country",
        "P11": "death_place_alt",
        "P12": "death_country",
        "P15": "convoy_place",
        "P18": "exit_1940_1941_place",
        "P19": "exit_1941_1944_place"
    }

    for prop_id, value_data in statements.items():
        claims = entity_data.get('claims', {}).get(prop_id, [])
        if claims:
            print(f"Found existing statement for property {prop_id}. Adding qualifiers if necessary.")
            for claim in claims:
                if claim['mainsnak'].get('datavalue', {}).get('value') == value_data['value']:
                    claim_id = claim['id']
                    related_field = property_to_related_field.get(prop_id)
                    qualifier_value_data = next((place for place in related_places if place['relatedField'] == related_field), None)
                    qualifier_value_str = str(qualifier_value_data['geonameId']) if qualifier_value_data and qualifier_value_data['geonameId'] else "Unknown"
                    qualifier_property = "P243"
                    qualifier_value = {"snaktype": "value", "property": qualifier_property, "datavalue": {"value": qualifier_value_str, "type": "string"}}
                    add_qualifier(session, csrf_token, claim_id, qualifier_property, qualifier_value)
        else:
            print(f"No existing statement found for property {prop_id}, skipping adding qualifiers.")

def process_profiles():
    session = login_to_wikibase()
    csrf_token = get_csrf_token(session)
    for filename in os.listdir(input_directory):
        if filename.endswith(".json"):
            file_path = os.path.join(input_directory, filename)
            with open(file_path, "r", encoding="utf-8") as file:
                person_data = json.load(file)
                entity_id = create_or_update_entity(session, csrf_token, person_data)
                if entity_id:
                    print(f"Processing entity {entity_id} for {filename}")
                    add_statements_and_qualifiers(session, csrf_token, entity_id, person_data)
                time.sleep(3)

process_profiles()

Logged in successfully!
No existing entity found for slug: dura-margarete. Skipping.
No existing entity found for slug: rothschild-elisabeth. Skipping.
No existing entity found for slug: rosenthal-rozenthal-albert-aron-abraham. Skipping.


KeyboardInterrupt: 

### Create Property for GeoNames

In [ ]:
import requests
import json
import os

# Disable SSL warnings (only for testing)
requests.packages.urllib3.disable_warnings(requests.packages.urllib3.exceptions.InsecureRequestWarning)

# Define the API endpoint and credentials
api_url = "http://wikibase.example.com/w/api.php"
USERNAME = "admin"
PASSWORD = "change-this-password"

# Mapping properties to their related fields in JSON
property_to_related_field = {
    "P6": "birth_place",
    "P7": "death_place",
    "P8": "nationality",
    "P9": "birth_country",
    "P11": "death_place_alt",
    "P12": "death_country",
    "P15": "convoy_place",
    "P18": "exit_place_1940_1941",
    "P19": "exit_place_1941_1944"
}

# Function to log in to Wikibase
def login_to_wikibase():
    session = requests.Session()

    params = {
        "action": "query",
        "meta": "tokens",
        "type": "login",
        "format": "json"
    }

    response = session.get(api_url, params=params, verify=False)
    login_token = response.json()['query']['tokens']['logintoken']

    login_params = {
        "action": "clientlogin",
        "username": USERNAME,
        "password": PASSWORD,
        "logintoken": login_token,
        "loginreturnurl": api_url,
        "format": "json"
    }

    session.post(api_url, data=login_params, verify=False)
    return session

# Function to get the CSRF token
def get_csrf_token(session):
    params = {
        "action": "query",
        "meta": "tokens",
        "type": "csrf",
        "format": "json"
    }

    response = session.get(api_url, params=params, verify=False)
    return response.json()['query']['tokens']['csrftoken']

# Function to retrieve entity data (to get the claims)
def get_entity_data(session, entity_id):
    params = {
        "action": "wbgetentities",
        "ids": entity_id,
        "props": "claims",
        "languages": "en",
        "format": "json"
    }

    response = session.get(api_url, params=params, verify=False)
    entity_data = response.json().get('entities', {}).get(entity_id, {})
    
    # Debugging: Print the entity data to inspect claims
    print(f"Entity Data for {entity_id}:")
    print(json.dumps(entity_data, indent=4))
    
    return entity_data

# Function to check if a qualifier exists
def qualifier_exists(claim, qualifier_property, qualifier_value):
    qualifiers = claim.get('qualifiers', {}).get(qualifier_property, [])
    for qualifier in qualifiers:
        if qualifier.get('datavalue', {}).get('value') == qualifier_value:
            return True
    return False

# Function to add a qualifier to a specific claim
def add_qualifier(session, csrf_token, claim_id, qualifier_property, qualifier_value):
    # Ensure the value is treated as a string, since it's an external ID
    qualifier_value = str(qualifier_value)
    
    params = {
        'action': 'wbsetqualifier',
        'claim': claim_id,
        'property': qualifier_property,
        'value': json.dumps(qualifier_value),  # Pass the value directly as a string
        'snaktype': 'value',  # Ensure the snak type is "value"
        'token': csrf_token,
        'format': 'json'
    }

    response = session.post(api_url, data=params, verify=False)
    response_data = response.json()

    if response.status_code == 200 and 'success' in response_data:
        print(f"Qualifier added successfully to claim {claim_id}.")
    else:
        print(f"Failed to add qualifier: {response_data}")

# Function to get the GeoNames ID from the JSON based on relatedField
# Function to get the GeoNames ID from the JSON based on relatedField
def get_geoname_id_from_json(person_data, related_field):
    related_places = person_data.get('related-places', [])
    
    # Look for the matching relatedField in the JSON
    for place in related_places:
        if place['relatedField'] == related_field:
            geoname_id = place.get('geonameId')
            if geoname_id:
                return geoname_id
            else:
                return 0  # Return 0 if no geonameId is available
    return 0  # Return 0 if the related field doesn't exist

# Function to add qualifier to a specific entity and property
def add_qualifier_to_entity(session, csrf_token, entity_id, person_data, property_to_related_field):
    entity_data = get_entity_data(session, entity_id)

    if not entity_data:
        print(f"Failed to retrieve data for entity {entity_id}.")
        return

    claims = entity_data.get('claims', {})

    # Loop through all mapped properties and related fields
    for prop_id, related_field in property_to_related_field.items():
        if prop_id in claims:
            # Get the GeoNames ID from the JSON for the related field
            qualifier_value = get_geoname_id_from_json(person_data, related_field)
            
            for claim in claims[prop_id]:
                claim_id = claim['id']
                qualifier_property = "P22"  # GeoNames ID property

                if qualifier_value != "Unknown":
                    # Add GeoNames ID qualifier
                    if not qualifier_exists(claim, qualifier_property, qualifier_value):
                        add_qualifier(session, csrf_token, claim_id, qualifier_property, qualifier_value)
                    else:
                        print(f"Qualifier already exists for claim {claim_id}. Skipping.")
                else:
                    print(f"No GeoNames ID found for related field '{related_field}'. Skipping.")
        else:
            print(f"No claims found for property {prop_id} in entity {entity_id}. Skipping.")

# Main script to process the specific entity's JSON and add qualifiers
def process_entity(entity_id, json_file_path):
    session = login_to_wikibase()
    csrf_token = get_csrf_token(session)

    # Read the JSON file for the specific entity
    with open(json_file_path, "r", encoding="utf-8") as file:
        person_data = json.load(file)
        # Add qualifiers to the entity based on the mapped properties
        add_qualifier_to_entity(session, csrf_token, entity_id, person_data, property_to_related_field)

# Example usage: processing one entity (Q181) and its corresponding JSON file
process_entity("Q181", "/Users/ismail.ahouari/Documents/GitHub/wikibase-everywhere/data/Reecords/wolf-paula.json")




In [ ]:
import requests
import logging
import json

# Define the API URL of your Wikibase instance
api_url = "http://wikibase.example.com/w/api.php"  # Replace with your actual Wikibase URL

# Set up logging for debugging purposes
logging.basicConfig(level=logging.INFO)

# Function to retrieve all entities (items) from Wikibase
def get_all_entities():
    session = requests.Session()
    entities = []

    # The API query to get all pages of namespace 0 (main content namespace, which includes items)
    params = {
        "action": "query",
        "list": "allpages",        # List all pages
        "apnamespace": 120,        # Namespace 120 is for items (main content)
        "apfilterredir": "nonredirects",  # Avoid redirects
        "aplimit": "max",          # Limit to the maximum number of results
        "format": "json"           # Ensure the result is in JSON format
    }

    while True:
        response = session.get(api_url, params=params)
        data = response.json()

        # Debug: Print response to understand what is being retrieved
        logging.info("Response from API (allpages): %s", json.dumps(data, indent=2))

        # Extracting the pages (entities) from the response
        all_pages = data.get("query", {}).get("allpages", [])
        if not all_pages:
            logging.info("No pages found in this batch.")
            break  # Exit if no entities were found

        for page in all_pages:
            entity_id = page["title"]
            # Remove 'Item:' prefix from the entity ID to keep just the QID (e.g., Q97, Q98)
            entity_id = entity_id.replace("Item:", "")
            if entity_id.startswith("Q"):  # Only process entities with IDs starting with 'Q'
                entities.append(entity_id)

        # Debug: Print current list of entities found
        logging.info("Current list of entities: %s", entities)

        # Check if there's more data to fetch (pagination)
        if "continue" in data:
            params["apcontinue"] = data["continue"]["apcontinue"]
        else:
            break

    return entities


# Function to retrieve data for a specific entity and its label
def get_entity_data(session, entity_id):
    """Retrieve data for a specific entity and its label."""
    
    # Log the entity_id before processing
    logging.info(f"Processing entity: {entity_id}")
    
    retrieve_params = {
        'action': 'wbgetentities',
        'ids': entity_id,
        'props': 'labels',  # Include labels (titles) in the response
        'languages': 'en',  # Specify the language (you can adjust as needed)
        'format': 'json'
    }

    # Log the request parameters for debugging
    logging.info(f"Requesting data for entity {entity_id} with params: {retrieve_params}")
    
    retrieve_response = session.get(api_url, params=retrieve_params)

    # Log the raw API response
    logging.info(f"Raw response for entity {entity_id}: {retrieve_response.text}")

    if retrieve_response.status_code == 200:
        entity_data = retrieve_response.json().get('entities', {}).get(entity_id, {})

        # Debug: print the full entity data response
        logging.info(f"Full response for entity {entity_id}: {json.dumps(entity_data, indent=2)}")

        # Check if the entity has labels and extract the label
        label = None
        if "labels" in entity_data:
            # Try to fetch the English label first
            label = entity_data["labels"].get("en", {}).get("value", None)
            if not label:  # If no English label, try fallback languages
                # Try first available label in any language
                label = next(iter(entity_data["labels"].values()), {}).get("value", "No label available")

        # Log the label (title)
        logging.info(f"Entity {entity_id} label: {label}")

        # Return the entity data along with the label (title)
        return {
            "entity_id": entity_id,
            "label": label,
            "data": entity_data
        }
    else:
        logging.error(f"Failed to retrieve entity data for {entity_id}. Status code: {retrieve_response.status_code}")
        return None


# Main function to process all entities and extract their labels
def process_all_entities():
    session = requests.Session()
    entities = get_all_entities()  # Retrieve all entities
    
    all_entity_data = []  # List to store all retrieved entity data

    for entity_id in entities:
        # For each entity, retrieve its label and data
        entity_data = get_entity_data(session, entity_id)
        if entity_data:
            all_entity_data.append(entity_data)
            logging.info(f"Processed data for {entity_data['entity_id']} - Label: {entity_data['label']}")
        else:
            logging.warning(f"No data found for entity {entity_id}.")

    # Optionally, print or return all the gathered entity data
    logging.info(f"All processed entity data: {json.dumps(all_entity_data, indent=2)}")
    return all_entity_data


# Run the script
process_all_entities()

In [ ]:
import requests
import logging
import json
import os

# Define the API URL of your Wikibase instance
api_url = "http://wikibase.example.com/w/api.php"  # Replace with your actual Wikibase URL

# Set up logging for debugging purposes
logging.basicConfig(level=logging.INFO)

# Function to retrieve all entities (items) from Wikibase
def get_all_entities():
    session = requests.Session()
    entities = []

    # The API query to get all pages of namespace 0 (main content namespace, which includes items)
    params = {
        "action": "query",
        "list": "allpages",        # List all pages
        "apnamespace": 120,        # Namespace 120 is for items (main content)
        "apfilterredir": "nonredirects",  # Avoid redirects
        "aplimit": "max",          # Limit to the maximum number of results
        "format": "json"           # Ensure the result is in JSON format
    }

    while True:
        response = session.get(api_url, params=params)
        data = response.json()

        # Debug: Print response to understand what is being retrieved
        logging.info("Response from API (allpages): %s", json.dumps(data, indent=2))

        # Extracting the pages (entities) from the response
        all_pages = data.get("query", {}).get("allpages", [])
        if not all_pages:
            logging.info("No pages found in this batch.")
            break  # Exit if no entities were found

        for page in all_pages:
            entity_id = page["title"]
            # Remove 'Item:' prefix from the entity ID to keep just the QID (e.g., Q97, Q98)
            entity_id = entity_id.replace("Item:", "")
            if entity_id.startswith("Q"):  # Only process entities with IDs starting with 'Q'
                entities.append(entity_id)

        # Debug: Print current list of entities found
        logging.info("Current list of entities: %s", entities)

        # Check if there's more data to fetch (pagination)
        if "continue" in data:
            params["apcontinue"] = data["continue"]["apcontinue"]
        else:
            break

    return entities


# Function to retrieve data for a specific entity and its label
def get_entity_data(session, entity_id):
    """Retrieve data for a specific entity and its label."""
    
    # Log the entity_id before processing
    logging.info(f"Processing entity: {entity_id}")
    
    retrieve_params = {
        'action': 'wbgetentities',
        'ids': entity_id,
        'props': 'labels',  # Include labels (titles) in the response
        'languages': 'en',  # Specify the language (you can adjust as needed)
        'format': 'json'
    }

    # Log the request parameters for debugging
    logging.info(f"Requesting data for entity {entity_id} with params: {retrieve_params}")
    
    retrieve_response = session.get(api_url, params=retrieve_params)

    # Log the raw API response
    logging.info(f"Raw response for entity {entity_id}: {retrieve_response.text}")

    if retrieve_response.status_code == 200:
        entity_data = retrieve_response.json().get('entities', {}).get(entity_id, {})

        # Debug: print the full entity data response
        logging.info(f"Full response for entity {entity_id}: {json.dumps(entity_data, indent=2)}")

        # Check if the entity has labels and extract the label
        label = None
        if "labels" in entity_data:
            # Try to fetch the English label first
            label = entity_data["labels"].get("en", {}).get("value", None)
            if not label:  # If no English label, try fallback languages
                # Try first available label in any language
                label = next(iter(entity_data["labels"].values()), {}).get("value", "No label available")

        # Log the label (title)
        logging.info(f"Entity {entity_id} label: {label}")

        # Return the entity data along with the label (title)
        return {
            "entity_id": entity_id,
            "label": label,
            "data": entity_data
        }
    else:
        logging.error(f"Failed to retrieve entity data for {entity_id}. Status code: {retrieve_response.status_code}")
        return None


# Main function to process all entities and extract their labels
def process_all_entities():
    session = requests.Session()
    entities = get_all_entities()  # Retrieve all entities

    simplified_entity_data = []  # List to store simplified entity data

    output_directory = "/Users/ismail.ahouari/Documents/GitHub/wikibase-everywhere/data/Reecords"
    os.makedirs(output_directory, exist_ok=True)

    for entity_id in entities:
        # For each entity, retrieve its label and data
        entity_data = get_entity_data(session, entity_id)
        if entity_data:
            label = entity_data['label']
            slug = label.replace(" ", "_").replace("/", "_").replace("\\", "_")
            simplified_entity_data.append((entity_data['entity_id'], slug))

            # Generate file paths based on slug
            file_name = slug
            json_file_path = os.path.join(output_directory, f"{file_name}.json")
            excel_file_path = os.path.join(output_directory, f"{file_name}.xlsx")

            # Log paths for debugging
            logging.info(f"JSON Path: {json_file_path}, Excel Path: {excel_file_path}")

            # Output paths
            print(f"\"{entity_data['entity_id']}\", \"{json_file_path}\")")
        else:
            logging.warning(f"No data found for entity {entity_id}.")

    return simplified_entity_data

# Run the script
process_all_entities()


In [44]:
import requests
import logging
import json
import os

# Define the API URL of your Wikibase instance
api_url = "http://wikibase.example.com/w/api.php"  # Replace with your actual Wikibase URL

# Set up logging for debugging purposes
logging.basicConfig(level=logging.INFO)

# Function to retrieve all entities (items) from Wikibase
def get_all_entities():
    session = requests.Session()
    entities = []

    # The API query to get all pages of namespace 120 (items)
    params = {
        "action": "query",
        "list": "allpages",        # List all pages
        "apnamespace": 120,       # Namespace 120 is for items (main content)
        "apfilterredir": "nonredirects",  # Avoid redirects
        "aplimit": "max",         # Limit to the maximum number of results
        "format": "json"          # Ensure the result is in JSON format
    }

    while True:
        response = session.get(api_url, params=params)
        data = response.json()

        # Extracting the pages (entities) from the response
        all_pages = data.get("query", {}).get("allpages", [])
        if not all_pages:
            break  # Exit if no entities were found

        for page in all_pages:
            entity_id = page["title"].replace("Item:", "")
            if entity_id.startswith("Q"):  # Only process entities with IDs starting with 'Q'
                entities.append(entity_id)

        # Check if there's more data to fetch (pagination)
        if "continue" in data:
            params["apcontinue"] = data["continue"]["apcontinue"]
        else:
            break

    return entities


# Function to retrieve data for a specific entity and its label
def get_entity_data(session, entity_id):
    retrieve_params = {
        'action': 'wbgetentities',
        'ids': entity_id,
        'props': 'labels',  # Include labels (titles) in the response
        'languages': 'en',  # Specify the language (you can adjust as needed)
        'format': 'json'
    }

    retrieve_response = session.get(api_url, params=retrieve_params)

    if retrieve_response.status_code == 200:
        entity_data = retrieve_response.json().get('entities', {}).get(entity_id, {})
        label = None
        if "labels" in entity_data:
            # Try to fetch the English label first
            label = entity_data["labels"].get("en", {}).get("value", None)
            if not label:  # If no English label, try fallback languages
                label = next(iter(entity_data["labels"].values()), {}).get("value", "No label available")
        return {
            "entity_id": entity_id,
            "label": label
        }
    else:
        return None


# Main function to process all entities and generate desired output
def process_all_entities():
    session = requests.Session()
    entities = get_all_entities()  # Retrieve all entities

    output_directory = "/Users/ismail.ahouari/Documents/GitHub/wikibase-everywhere/data/Reecords"
    os.makedirs(output_directory, exist_ok=True)

    for entity_id in entities:
        entity_data = get_entity_data(session, entity_id)
        if entity_data:
            label = entity_data['label']
            # Generate slug
            slug = label.lower().replace(" ", "-").replace("/", "-").replace("\\", "-").replace("(", "").replace(")", "").strip("-")
            file_name = f"{slug}.json"
            json_file_path = os.path.join(output_directory, file_name)

            # Print the output in the specified format
            print(f"\"{entity_data['entity_id']}\", \"{json_file_path}\"")
        else:
            logging.warning(f"No data found for entity {entity_id}.")


# Run the script
process_all_entities()

"Q1", "/Users/ismail.ahouari/Documents/GitHub/wikibase-everywhere/data/Reecords/rosenthal-estera.json"
"Q10", "/Users/ismail.ahouari/Documents/GitHub/wikibase-everywhere/data/Reecords/lipka-sara-frajda.json"
"Q100", "/Users/ismail.ahouari/Documents/GitHub/wikibase-everywhere/data/Reecords/rudow,-rudovs-erich.json"
"Q101", "/Users/ismail.ahouari/Documents/GitHub/wikibase-everywhere/data/Reecords/rosenthal-maria---macha.json"
"Q102", "/Users/ismail.ahouari/Documents/GitHub/wikibase-everywhere/data/Reecords/borenstein-hanna-helene.json"
"Q103", "/Users/ismail.ahouari/Documents/GitHub/wikibase-everywhere/data/Reecords/wonagus-ida.json"
"Q104", "/Users/ismail.ahouari/Documents/GitHub/wikibase-everywhere/data/Reecords/gerson-elisabeth-elise.json"
"Q105", "/Users/ismail.ahouari/Documents/GitHub/wikibase-everywhere/data/Reecords/springut-gisela.json"
"Q106", "/Users/ismail.ahouari/Documents/GitHub/wikibase-everywhere/data/Reecords/michel-carlo.json"
"Q107", "/Users/ismail.ahouari/Documents/Git

In [46]:
import requests
import logging
import json
import os
import re  # Importing regex module to handle the string cleanup

# Define the API URL of your Wikibase instance
api_url = "http://wikibase.example.com/w/api.php"  # Replace with your actual Wikibase URL

# Set up logging for debugging purposes
logging.basicConfig(level=logging.INFO)

# Function to retrieve all entities (items) from Wikibase
def get_all_entities():
    session = requests.Session()
    entities = []

    # The API query to get all pages of namespace 120 (items)
    params = {
        "action": "query",
        "list": "allpages",        # List all pages
        "apnamespace": 120,       # Namespace 120 is for items (main content)
        "apfilterredir": "nonredirects",  # Avoid redirects
        "aplimit": "max",         # Limit to the maximum number of results
        "format": "json"          # Ensure the result is in JSON format
    }

    while True:
        response = session.get(api_url, params=params)
        data = response.json()

        # Extracting the pages (entities) from the response
        all_pages = data.get("query", {}).get("allpages", [])
        if not all_pages:
            break  # Exit if no entities were found

        for page in all_pages:
            entity_id = page["title"].replace("Item:", "")
            if entity_id.startswith("Q"):  # Only process entities with IDs starting with 'Q'
                entities.append(entity_id)

        # Check if there's more data to fetch (pagination)
        if "continue" in data:
            params["apcontinue"] = data["continue"]["apcontinue"]
        else:
            break

    return entities


# Function to retrieve data for a specific entity and its label
def get_entity_data(session, entity_id):
    retrieve_params = {
        'action': 'wbgetentities',
        'ids': entity_id,
        'props': 'labels',  # Include labels (titles) in the response
        'languages': 'en',  # Specify the language (you can adjust as needed)
        'format': 'json'
    }

    retrieve_response = session.get(api_url, params=retrieve_params)

    if retrieve_response.status_code == 200:
        entity_data = retrieve_response.json().get('entities', {}).get(entity_id, {})
        label = None
        if "labels" in entity_data:
            # Try to fetch the English label first
            label = entity_data["labels"].get("en", {}).get("value", None)
            if not label:  # If no English label, try fallback languages
                label = next(iter(entity_data["labels"].values()), {}).get("value", "No label available")
        return {
            "entity_id": entity_id,
            "label": label
        }
    else:
        return None


# Main function to process all entities and generate desired output
def process_all_entities():
    session = requests.Session()
    entities = get_all_entities()  # Retrieve all entities

    output_directory = "/Users/ismail.ahouari/Documents/GitHub/wikibase-everywhere/data/Reecords"
    os.makedirs(output_directory, exist_ok=True)

    for entity_id in entities:
        entity_data = get_entity_data(session, entity_id)
        if entity_data:
            label = entity_data['label']
            
            # Generate slug - keep letters and spaces, remove parentheses and non-letter characters, make lowercase
            slug = re.sub(r'[^a-zA-Z\s]', '', label)  # Remove anything except letters and spaces
            slug = slug.lower().replace(" ", "-")  # Convert to lowercase and replace spaces with hyphens
            slug = re.sub(r'-+', '-', slug)  # Replace consecutive hyphens with a single hyphen
            
            file_name = f"{slug}.json"
            json_file_path = os.path.join(output_directory, file_name)

            # Print the output in the specified format
            print(f"\"{entity_data['entity_id']}\", \"{json_file_path}\"")
        else:
            logging.warning(f"No data found for entity {entity_id}.")


# Run the script
process_all_entities()

"Q1", "/Users/ismail.ahouari/Documents/GitHub/wikibase-everywhere/data/Reecords/rosenthal-estera.json"
"Q10", "/Users/ismail.ahouari/Documents/GitHub/wikibase-everywhere/data/Reecords/lipka-sara-frajda.json"
"Q100", "/Users/ismail.ahouari/Documents/GitHub/wikibase-everywhere/data/Reecords/rudow-rudovs-erich.json"
"Q101", "/Users/ismail.ahouari/Documents/GitHub/wikibase-everywhere/data/Reecords/rosenthal-maria-macha.json"
"Q102", "/Users/ismail.ahouari/Documents/GitHub/wikibase-everywhere/data/Reecords/borenstein-hanna-helene.json"
"Q103", "/Users/ismail.ahouari/Documents/GitHub/wikibase-everywhere/data/Reecords/wonagus-ida.json"
"Q104", "/Users/ismail.ahouari/Documents/GitHub/wikibase-everywhere/data/Reecords/gerson-elisabeth-elise.json"
"Q105", "/Users/ismail.ahouari/Documents/GitHub/wikibase-everywhere/data/Reecords/springut-gisela.json"
"Q106", "/Users/ismail.ahouari/Documents/GitHub/wikibase-everywhere/data/Reecords/michel-carlo.json"
"Q107", "/Users/ismail.ahouari/Documents/GitHub

In [68]:
import requests
import logging
import json
import os
import re  # Importing regex module to handle the string cleanup

# Define the API URL of your Wikibase instance
api_url = "http://wikibase.example.com/w/api.php"  # Replace with your actual Wikibase URL

# Set up logging for debugging purposes
logging.basicConfig(level=logging.INFO)

# Function to retrieve all entities (items) from Wikibase
def get_all_entities():
    session = requests.Session()
    entities = []

    # The API query to get all pages of namespace 120 (items)
    params = {
        "action": "query",
        "list": "allpages",        # List all pages
        "apnamespace": 120,       # Namespace 120 is for items (main content)
        "apfilterredir": "nonredirects",  # Avoid redirects
        "aplimit": "max",         # Limit to the maximum number of results
        "format": "json"          # Ensure the result is in JSON format
    }

    while True:
        response = session.get(api_url, params=params)
        data = response.json()

        # Extracting the pages (entities) from the response
        all_pages = data.get("query", {}).get("allpages", [])
        if not all_pages:
            break  # Exit if no entities were found

        for page in all_pages:
            entity_id = page["title"].replace("Item:", "")
            if entity_id.startswith("Q"):  # Only process entities with IDs starting with 'Q'
                entities.append(entity_id)

        # Check if there's more data to fetch (pagination)
        if "continue" in data:
            params["apcontinue"] = data["continue"]["apcontinue"]
        else:
            break

    return entities


# Function to retrieve data for a specific entity and its label
def get_entity_data(session, entity_id):
    retrieve_params = {
        'action': 'wbgetentities',
        'ids': entity_id,
        'props': 'labels',  # Include labels (titles) in the response
        'languages': 'en',  # Specify the language (you can adjust as needed)
        'format': 'json'
    }

    retrieve_response = session.get(api_url, params=retrieve_params)

    if retrieve_response.status_code == 200:
        entity_data = retrieve_response.json().get('entities', {}).get(entity_id, {})
        label = None
        if "labels" in entity_data:
            # Try to fetch the English label first
            label = entity_data["labels"].get("en", {}).get("value", None)
            if not label:  # If no English label, try fallback languages
                label = next(iter(entity_data["labels"].values()), {}).get("value", "No label available")
        return {
            "entity_id": entity_id,
            "label": label
        }
    else:
        return None


# Main function to process all entities and generate desired output
def process_all_entities():
    session = requests.Session()
    entities = get_all_entities()  # Retrieve all entities

    output_directory = "/Users/ismail.ahouari/Documents/GitHub/wikibase-everywhere/data/Records"
    os.makedirs(output_directory, exist_ok=True)

    entity_file_mapping = {}  # Dictionary to store entity_id and corresponding file path

    for entity_id in entities:
        entity_data = get_entity_data(session, entity_id)
        if entity_data:
            label = entity_data['label']
            
            # Generate slug - keep letters and spaces, remove parentheses and non-letter characters, make lowercase
            slug = re.sub(r'[^a-zA-Z\s]', '', label)  # Remove anything except letters and spaces
            slug = slug.lower().replace(" ", "-")  # Convert to lowercase and replace spaces with hyphens
            slug = re.sub(r'-+', '-', slug)  # Replace consecutive hyphens with a single hyphen
            
            file_name = f"{slug}.json"
            json_file_path = os.path.join(output_directory, file_name)

            # Store the entity_id and corresponding file path in the dictionary
            entity_file_mapping[entity_data['entity_id']] = json_file_path

        else:
            logging.warning(f"No data found for entity {entity_id}.")
    
    return entity_file_mapping  # Return the dictionary of entity to file path mappings


# Function to process an individual entity (example usage)
def process_entity(entity_id, file_path):
    # Process the entity with the given ID and file path
    print(f"Processing entity {entity_id} and saving to {file_path}")
    # Your custom logic for processing the entity can be placed here.
    # For example, if you need to save some data to the file, you can use json.dump() or any other processing.

    # Example:
    data_to_save = {"entity_id": entity_id, "file_path": file_path}
    with open(file_path, "w") as f:
        json.dump(data_to_save, f, indent=4)

    print(f"Entity {entity_id} processed and saved to {file_path}")
    
if __name__ == "__main__":
    entity_file_mapping = process_all_entities()

    # Output the final dictionary of entity IDs and file paths
    print("\nEntity to JSON file mapping:")
    for entity_id, file_path in entity_file_mapping.items():
        print(f"\"{entity_id}\", \"{file_path}\"")




Entity to JSON file mapping:
"Q1", "/Users/ismail.ahouari/Documents/GitHub/wikibase-everywhere/data/Records/rosenthal-estera.json"
"Q10", "/Users/ismail.ahouari/Documents/GitHub/wikibase-everywhere/data/Records/lipka-sara-frajda.json"
"Q100", "/Users/ismail.ahouari/Documents/GitHub/wikibase-everywhere/data/Records/rudow-rudovs-erich.json"
"Q101", "/Users/ismail.ahouari/Documents/GitHub/wikibase-everywhere/data/Records/rosenthal-maria-macha.json"
"Q102", "/Users/ismail.ahouari/Documents/GitHub/wikibase-everywhere/data/Records/borenstein-hanna-helene.json"
"Q103", "/Users/ismail.ahouari/Documents/GitHub/wikibase-everywhere/data/Records/wonagus-ida.json"
"Q104", "/Users/ismail.ahouari/Documents/GitHub/wikibase-everywhere/data/Records/gerson-elisabeth-elise.json"
"Q105", "/Users/ismail.ahouari/Documents/GitHub/wikibase-everywhere/data/Records/springut-gisela.json"
"Q106", "/Users/ismail.ahouari/Documents/GitHub/wikibase-everywhere/data/Records/michel-carlo.json"
"Q107", "/Users/ismail.aho

In [69]:
import requests
import json
import os

# Disable SSL warnings (only for testing)
requests.packages.urllib3.disable_warnings(requests.packages.urllib3.exceptions.InsecureRequestWarning)

# Define the API endpoint and credentials
api_url = "http://wikibase.example.com/w/api.php"
USERNAME = "admin"
PASSWORD = "change-this-password"

# Mapping properties to their related fields in JSON
property_to_related_field = {
    "P6": "birth_place",
    "P7": "death_place",
    "P8": "nationality",
    "P9": "birth_country",
    "P11": "death_place_alt",
    "P12": "death_country",
    "P15": "convoy_place",
    "P18": "exit_place_1940_1941",
    "P19": "exit_place_1941_1944"
}

# Function to log in to Wikibase
def login_to_wikibase():
    session = requests.Session()

    params = {
        "action": "query",
        "meta": "tokens",
        "type": "login",
        "format": "json"
    }

    response = session.get(api_url, params=params, verify=False)
    login_token = response.json()['query']['tokens']['logintoken']

    login_params = {
        "action": "clientlogin",
        "username": USERNAME,
        "password": PASSWORD,
        "logintoken": login_token,
        "loginreturnurl": api_url,
        "format": "json"
    }

    session.post(api_url, data=login_params, verify=False)
    return session

# Function to get the CSRF token
def get_csrf_token(session):
    params = {
        "action": "query",
        "meta": "tokens",
        "type": "csrf",
        "format": "json"
    }

    response = session.get(api_url, params=params, verify=False)
    return response.json()['query']['tokens']['csrftoken']

# Function to retrieve entity data (to get the claims)
def get_entity_data(session, entity_id):
    params = {
        "action": "wbgetentities",
        "ids": entity_id,
        "props": "claims",
        "languages": "en",
        "format": "json"
    }

    response = session.get(api_url, params=params, verify=False)
    entity_data = response.json().get('entities', {}).get(entity_id, {})
    
    # Debugging: Print the entity data to inspect claims
    print(f"Entity Data for {entity_id}:")
    print(json.dumps(entity_data, indent=4))
    
    return entity_data

# Function to check if a qualifier exists
def qualifier_exists(claim, qualifier_property, qualifier_value):
    qualifiers = claim.get('qualifiers', {}).get(qualifier_property, [])
    for qualifier in qualifiers:
        if qualifier.get('datavalue', {}).get('value') == qualifier_value:
            return True
    return False

# Function to add a qualifier to a specific claim
def add_qualifier(session, csrf_token, claim_id, qualifier_property, qualifier_value):
    # Ensure the value is treated as a string, since it's an external ID
    qualifier_value = str(qualifier_value)
    
    params = {
        'action': 'wbsetqualifier',
        'claim': claim_id,
        'property': qualifier_property,
        'value': json.dumps(qualifier_value),  # Pass the value directly as a string
        'snaktype': 'value',  # Ensure the snak type is "value"
        'token': csrf_token,
        'format': 'json'
    }

    response = session.post(api_url, data=params, verify=False)
    response_data = response.json()

    if response.status_code == 200 and 'success' in response_data:
        print(f"Qualifier added successfully to claim {claim_id}.")
    else:
        print(f"Failed to add qualifier: {response_data}")

# Function to get the GeoNames ID from the JSON based on relatedField
def get_geoname_id_from_json(person_data, related_field):
    related_places = person_data.get('related-places', [])
    
    # Look for the matching relatedField in the JSON
    for place in related_places:
        if place['relatedField'] == related_field:
            geoname_id = place.get('geonameId')
            if geoname_id:
                return geoname_id
            else:
                return 0  # Return 0 if no geonameId is available
    return 0  # Return 0 if the related field doesn't exist

# Function to add qualifier to a specific entity and property
def add_qualifier_to_entity(session, csrf_token, entity_id, person_data, property_to_related_field):
    entity_data = get_entity_data(session, entity_id)

    if not entity_data:
        print(f"Failed to retrieve data for entity {entity_id}.")
        return

    claims = entity_data.get('claims', {})

    # Loop through all mapped properties and related fields
    for prop_id, related_field in property_to_related_field.items():
        if prop_id in claims:
            # Get the GeoNames ID from the JSON for the related field
            qualifier_value = get_geoname_id_from_json(person_data, related_field)
            
            for claim in claims[prop_id]:
                claim_id = claim['id']
                qualifier_property = "P22"  # GeoNames ID property

                if qualifier_value != "Unknown":
                    # Add GeoNames ID qualifier
                    if not qualifier_exists(claim, qualifier_property, qualifier_value):
                        add_qualifier(session, csrf_token, claim_id, qualifier_property, qualifier_value)
                    else:
                        print(f"Qualifier already exists for claim {claim_id}. Skipping.")
                else:
                    print(f"No GeoNames ID found for related field '{related_field}'. Skipping.")
        else:
            print(f"No claims found for property {prop_id} in entity {entity_id}. Skipping.")

# Main script to process the specific entity's JSON and add qualifiers
def process_entity(entity_id, json_file_path):
    session = login_to_wikibase()
    csrf_token = get_csrf_token(session)

    # Read the JSON file for the specific entity
    with open(json_file_path, "r", encoding="utf-8") as file:
        person_data = json.load(file)
        # Add qualifiers to the entity based on the mapped properties
        add_qualifier_to_entity(session, csrf_token, entity_id, person_data, property_to_related_field)

# Example: entity_file_mapping dictionary with entity IDs and their respective file paths
# Example usage: process all entities using the entity_file_mapping dictionary
for entity_id, json_file_path in entity_file_mapping.items():
    process_entity(entity_id, json_file_path)

FileNotFoundError: [Errno 2] No such file or directory: '/Users/ismail.ahouari/Documents/GitHub/wikibase-everywhere/data/Records/rosenthal-estera.json'

In [70]:
import requests
import json
import os

# Disable SSL warnings (only for testing)
requests.packages.urllib3.disable_warnings(requests.packages.urllib3.exceptions.InsecureRequestWarning)

# Define the API endpoint and credentials
api_url = "http://wikibase.example.com/w/api.php"
USERNAME = "admin"
PASSWORD = "change-this-password"

# Mapping properties to their related fields in JSON
property_to_related_field = {
    "P6": "birth_place",
    "P7": "death_place",
    "P8": "nationality",
    "P9": "birth_country",
    "P11": "death_place_alt",
    "P12": "death_country",
    "P15": "convoy_place",
    "P18": "exit_place_1940_1941",
    "P19": "exit_place_1941_1944"
}

# Function to log in to Wikibase
def login_to_wikibase():
    session = requests.Session()

    params = {
        "action": "query",
        "meta": "tokens",
        "type": "login",
        "format": "json"
    }

    response = session.get(api_url, params=params, verify=False)
    login_token = response.json()['query']['tokens']['logintoken']

    login_params = {
        "action": "clientlogin",
        "username": USERNAME,
        "password": PASSWORD,
        "logintoken": login_token,
        "loginreturnurl": api_url,
        "format": "json"
    }

    session.post(api_url, data=login_params, verify=False)
    return session

# Function to get the CSRF token
def get_csrf_token(session):
    params = {
        "action": "query",
        "meta": "tokens",
        "type": "csrf",
        "format": "json"
    }

    response = session.get(api_url, params=params, verify=False)
    return response.json()['query']['tokens']['csrftoken']

# Function to retrieve entity data (to get the claims)
def get_entity_data(session, entity_id):
    params = {
        "action": "wbgetentities",
        "ids": entity_id,
        "props": "claims",
        "languages": "en",
        "format": "json"
    }

    response = session.get(api_url, params=params, verify=False)
    entity_data = response.json().get('entities', {}).get(entity_id, {})
    
    # Debugging: Print the entity data to inspect claims
    print(f"Entity Data for {entity_id}:")
    print(json.dumps(entity_data, indent=4))
    
    return entity_data

# Function to check if a qualifier exists
def qualifier_exists(claim, qualifier_property, qualifier_value):
    qualifiers = claim.get('qualifiers', {}).get(qualifier_property, [])
    for qualifier in qualifiers:
        if qualifier.get('datavalue', {}).get('value') == qualifier_value:
            return True
    return False

# Function to add a qualifier to a specific claim
def add_qualifier(session, csrf_token, claim_id, qualifier_property, qualifier_value):
    # Ensure the value is treated as a string, since it's an external ID
    qualifier_value = str(qualifier_value)
    
    params = {
        'action': 'wbsetqualifier',
        'claim': claim_id,
        'property': qualifier_property,
        'value': json.dumps(qualifier_value),  # Pass the value directly as a string
        'snaktype': 'value',  # Ensure the snak type is "value"
        'token': csrf_token,
        'format': 'json'
    }

    response = session.post(api_url, data=params, verify=False)
    response_data = response.json()

    if response.status_code == 200 and 'success' in response_data:
        print(f"Qualifier added successfully to claim {claim_id}.")
    else:
        print(f"Failed to add qualifier: {response_data}")

# Function to get the GeoNames ID from the JSON based on relatedField
def get_geoname_id_from_json(person_data, related_field):
    related_places = person_data.get('related-places', [])
    
    # Debugging: Print the related places to ensure data structure
    print(f"Related Places: {json.dumps(related_places, indent=4)}")
    
    # Look for the matching relatedField in the JSON
    for place in related_places:
        if place['relatedField'] == related_field:
            geoname_id = place.get('geonameId')
            if geoname_id:
                return geoname_id
            else:
                return 0  # Return 0 if no geonameId is available
    return 0  # Return 0 if the related field doesn't exist

# Function to add qualifier to a specific entity and property
def add_qualifier_to_entity(session, csrf_token, entity_id, person_data, property_to_related_field):
    entity_data = get_entity_data(session, entity_id)

    if not entity_data:
        print(f"Failed to retrieve data for entity {entity_id}.")
        return

    claims = entity_data.get('claims', {})

    # Loop through all mapped properties and related fields
    for prop_id, related_field in property_to_related_field.items():
        if prop_id in claims:
            # Get the GeoNames ID from the JSON for the related field
            qualifier_value = get_geoname_id_from_json(person_data, related_field)
            
            for claim in claims[prop_id]:
                claim_id = claim['id']
                qualifier_property = "P22"  # GeoNames ID property

                if qualifier_value != "Unknown":
                    # Add GeoNames ID qualifier
                    if not qualifier_exists(claim, qualifier_property, qualifier_value):
                        add_qualifier(session, csrf_token, claim_id, qualifier_property, qualifier_value)
                    else:
                        print(f"Qualifier already exists for claim {claim_id}. Skipping.")
                else:
                    print(f"No GeoNames ID found for related field '{related_field}'. Skipping.")
        else:
            print(f"No claims found for property {prop_id} in entity {entity_id}. Skipping.")

# Main script to process the specific entity's JSON and add qualifiers
def process_entity(entity_id, json_file_path):
    # Check if the JSON file exists before proceeding
    if not os.path.exists(json_file_path):
        print(f"File {json_file_path} does not exist. Skipping.")
        return
    
    session = login_to_wikibase()
    csrf_token = get_csrf_token(session)

    # Read the JSON file for the specific entity
    with open(json_file_path, "r", encoding="utf-8") as file:
        person_data = json.load(file)
        # Add qualifiers to the entity based on the mapped properties
        add_qualifier_to_entity(session, csrf_token, entity_id, person_data, property_to_related_field)


# Example usage: process all entities using the entity_file_mapping dictionary
for entity_id, json_file_path in entity_file_mapping.items():
    process_entity(entity_id, json_file_path)

File /Users/ismail.ahouari/Documents/GitHub/wikibase-everywhere/data/Records/rosenthal-estera.json does not exist. Skipping.
Entity Data for Q10:
{
    "type": "item",
    "id": "Q10",
    "claims": {
        "P4": [
            {
                "mainsnak": {
                    "snaktype": "value",
                    "property": "P4",
                    "hash": "928729860d6a1fbd2b0d2f5ffb874833c30491ba",
                    "datavalue": {
                        "value": "Borenstein",
                        "type": "string"
                    },
                    "datatype": "string"
                },
                "type": "statement",
                "id": "Q10$3C4806B8-4F6A-4E60-8DF7-59FFAF0F6453",
                "rank": "normal"
            }
        ],
        "P5": [
            {
                "mainsnak": {
                    "snaktype": "value",
                    "property": "P5",
                    "hash": "8f797297599a1b285883c5e83dab3290c2a3e5f3",
          

KeyboardInterrupt: 

In [71]:
import requests
import json
import os

# Disable SSL warnings (only for testing)
requests.packages.urllib3.disable_warnings(requests.packages.urllib3.exceptions.InsecureRequestWarning)

# Define the API endpoint and credentials
api_url = "http://wikibase.example.com/w/api.php"
USERNAME = "admin"
PASSWORD = "change-this-password"

# Mapping properties to their related fields in JSON
property_to_related_field = {
    "P6": "birth_place",
    "P7": "death_place",
    "P8": "nationality",
    "P9": "birth_country",
    "P11": "death_place_alt",
    "P12": "death_country",
    "P15": "convoy_place",
    "P18": "exit_place_1940_1941",
    "P19": "exit_place_1941_1944"
}

# Function to log in to Wikibase
def login_to_wikibase():
    session = requests.Session()

    params = {
        "action": "query",
        "meta": "tokens",
        "type": "login",
        "format": "json"
    }

    response = session.get(api_url, params=params, verify=False)
    login_token = response.json()['query']['tokens']['logintoken']

    login_params = {
        "action": "clientlogin",
        "username": USERNAME,
        "password": PASSWORD,
        "logintoken": login_token,
        "loginreturnurl": api_url,
        "format": "json"
    }

    session.post(api_url, data=login_params, verify=False)
    return session

# Function to get the CSRF token
def get_csrf_token(session):
    params = {
        "action": "query",
        "meta": "tokens",
        "type": "csrf",
        "format": "json"
    }

    response = session.get(api_url, params=params, verify=False)
    return response.json()['query']['tokens']['csrftoken']

# Function to retrieve entity data (to get the claims)
def get_entity_data(session, entity_id):
    params = {
        "action": "wbgetentities",
        "ids": entity_id,
        "props": "claims",
        "languages": "en",
        "format": "json"
    }

    response = session.get(api_url, params=params, verify=False)
    entity_data = response.json().get('entities', {}).get(entity_id, {})
    
    # Debugging: Print the entity data to inspect claims
    print(f"Entity Data for {entity_id}:")
    print(json.dumps(entity_data, indent=4))
    
    return entity_data

# Function to check if a qualifier exists and return it
def qualifier_exists(claim, qualifier_property, qualifier_value):
    qualifiers = claim.get('qualifiers', {}).get(qualifier_property, [])
    for qualifier in qualifiers:
        existing_value = qualifier.get('datavalue', {}).get('value')
        if existing_value == qualifier_value:
            return True, qualifier  # Return True and the existing qualifier if the value matches
    return False, None  # Return False if no matching qualifier is found

# Function to add a qualifier to a specific claim
def add_qualifier(session, csrf_token, claim_id, qualifier_property, qualifier_value):
    qualifier_value = str(qualifier_value)
    
    params = {
        'action': 'wbsetqualifier',
        'claim': claim_id,
        'property': qualifier_property,
        'value': json.dumps(qualifier_value),  # Pass the value directly as a string
        'snaktype': 'value',  # Ensure the snak type is "value"
        'token': csrf_token,
        'format': 'json'
    }

    response = session.post(api_url, data=params, verify=False)
    response_data = response.json()

    if response.status_code == 200 and 'success' in response_data:
        print(f"Qualifier added successfully to claim {claim_id}.")
    else:
        print(f"Failed to add qualifier: {response_data}")

# Function to update an existing qualifier
def update_qualifier(session, csrf_token, claim_id, qualifier_id, qualifier_property, qualifier_value):
    params = {
        'action': 'wbsetqualifier',
        'claim': claim_id,
        'qualifier': qualifier_id,
        'property': qualifier_property,
        'value': json.dumps(qualifier_value),
        'snaktype': 'value',
        'token': csrf_token,
        'format': 'json'
    }

    response = session.post(api_url, data=params, verify=False)
    response_data = response.json()

    if response.status_code == 200 and 'success' in response_data:
        print(f"Qualifier updated successfully for claim {claim_id}.")
    else:
        print(f"Failed to update qualifier: {response_data}")

# Function to get the GeoNames ID from the JSON based on relatedField
def get_geoname_id_from_json(person_data, related_field):
    related_places = person_data.get('related-places', [])
    
    # Debugging: Print the related places to ensure data structure
    print(f"Related Places: {json.dumps(related_places, indent=4)}")
    
    for place in related_places:
        if place['relatedField'] == related_field:
            geoname_id = place.get('geonameId')
            if geoname_id:
                return geoname_id
            else:
                return 0  # Return 0 if no geonameId is available
    return 0  # Return 0 if the related field doesn't exist

# Function to add or update qualifier to a specific entity and property
def add_qualifier_to_entity(session, csrf_token, entity_id, person_data, property_to_related_field):
    entity_data = get_entity_data(session, entity_id)

    if not entity_data:
        print(f"Failed to retrieve data for entity {entity_id}.")
        return

    claims = entity_data.get('claims', {})

    for prop_id, related_field in property_to_related_field.items():
        if prop_id in claims:
            qualifier_value = get_geoname_id_from_json(person_data, related_field)
            
            for claim in claims[prop_id]:
                claim_id = claim['id']
                qualifier_property = "P22"  # GeoNames ID property

                # Check if a qualifier already exists
                exists, existing_qualifier = qualifier_exists(claim, qualifier_property, qualifier_value)

                if exists:
                    print(f"GeoNames ID already exists for claim {claim_id}. Skipping.")
                    continue  # Skip if the qualifier already exists

                # If the GeoNames ID is different, update it
                if exists and existing_qualifier.get('datavalue', {}).get('value') != qualifier_value:
                    print(f"GeoNames ID changed for claim {claim_id}. Updating...")
                    update_qualifier(session, csrf_token, claim_id, existing_qualifier['id'], qualifier_property, qualifier_value)
                else:
                    # Add the GeoNames ID qualifier if it doesn't exist
                    if qualifier_value != 0:
                        add_qualifier(session, csrf_token, claim_id, qualifier_property, qualifier_value)
                    else:
                        print(f"No GeoNames ID found for related field '{related_field}'. Skipping.")
        else:
            print(f"No claims found for property {prop_id} in entity {entity_id}. Skipping.")

# Main script to process the specific entity's JSON and add or update qualifiers
def process_entity(entity_id, json_file_path):
    if not os.path.exists(json_file_path):
        print(f"File {json_file_path} does not exist. Skipping.")
        return
    
    session = login_to_wikibase()
    csrf_token = get_csrf_token(session)

    with open(json_file_path, "r", encoding="utf-8") as file:
        person_data = json.load(file)
        add_qualifier_to_entity(session, csrf_token, entity_id, person_data, property_to_related_field)

# Example usage: process all entities using the entity_file_mapping dictionary
for entity_id, json_file_path in entity_file_mapping.items():
    process_entity(entity_id, json_file_path)

File /Users/ismail.ahouari/Documents/GitHub/wikibase-everywhere/data/Records/rosenthal-estera.json does not exist. Skipping.
Entity Data for Q10:
{
    "type": "item",
    "id": "Q10",
    "claims": {
        "P4": [
            {
                "mainsnak": {
                    "snaktype": "value",
                    "property": "P4",
                    "hash": "928729860d6a1fbd2b0d2f5ffb874833c30491ba",
                    "datavalue": {
                        "value": "Borenstein",
                        "type": "string"
                    },
                    "datatype": "string"
                },
                "type": "statement",
                "id": "Q10$3C4806B8-4F6A-4E60-8DF7-59FFAF0F6453",
                "rank": "normal"
            }
        ],
        "P5": [
            {
                "mainsnak": {
                    "snaktype": "value",
                    "property": "P5",
                    "hash": "8f797297599a1b285883c5e83dab3290c2a3e5f3",
          

In [65]:
import requests
import json
import os

# Disable SSL warnings (only for testing)
requests.packages.urllib3.disable_warnings(requests.packages.urllib3.exceptions.InsecureRequestWarning)

# Define the API endpoint and credentials
api_url = "http://wikibase.example.com/w/api.php"
USERNAME = "admin"
PASSWORD = "change-this-password"

# Mapping properties to their related fields in JSON
property_to_related_field = {
    "P6": "birth_place",
    "P7": "death_place",
    "P8": "nationality",
    "P9": "birth_country",
    "P11": "death_place_alt",
    "P12": "death_country",
    "P15": "convoy_place",
    "P18": "exit_place_1940_1941",
    "P19": "exit_place_1941_1944"
}

# Function to log in to Wikibase
def login_to_wikibase():
    session = requests.Session()

    params = {
        "action": "query",
        "meta": "tokens",
        "type": "login",
        "format": "json"
    }

    response = session.get(api_url, params=params, verify=False)
    login_token = response.json()['query']['tokens']['logintoken']

    login_params = {
        "action": "clientlogin",
        "username": USERNAME,
        "password": PASSWORD,
        "logintoken": login_token,
        "loginreturnurl": api_url,
        "format": "json"
    }

    session.post(api_url, data=login_params, verify=False)
    return session

# Function to get the CSRF token
def get_csrf_token(session):
    params = {
        "action": "query",
        "meta": "tokens",
        "type": "csrf",
        "format": "json"
    }

    response = session.get(api_url, params=params, verify=False)
    return response.json()['query']['tokens']['csrftoken']

# Function to retrieve entity data (to get the claims)
def get_entity_data(session, entity_id):
    params = {
        "action": "wbgetentities",
        "ids": entity_id,
        "props": "claims",
        "languages": "en",
        "format": "json"
    }

    response = session.get(api_url, params=params, verify=False)
    entity_data = response.json().get('entities', {}).get(entity_id, {})
    
    # Debugging: Print the entity data to inspect claims
    print(f"Entity Data for {entity_id}:")
    print(json.dumps(entity_data, indent=4))
    
    return entity_data

# Function to check if a qualifier exists and return it
def qualifier_exists(claim, qualifier_property, qualifier_value):
    qualifiers = claim.get('qualifiers', {}).get(qualifier_property, [])
    for qualifier in qualifiers:
        existing_value = qualifier.get('datavalue', {}).get('value')
        if existing_value == qualifier_value:
            return True, qualifier  # Return True and the existing qualifier if the value matches
    return False, None  # Return False if no matching qualifier is found

# Function to add a qualifier to a specific claim
def add_qualifier(session, csrf_token, claim_id, qualifier_property, qualifier_value):
    qualifier_value = str(qualifier_value)
    
    params = {
        'action': 'wbsetqualifier',
        'claim': claim_id,
        'property': qualifier_property,
        'value': json.dumps(qualifier_value),  # Pass the value directly as a string
        'snaktype': 'value',  # Ensure the snak type is "value"
        'token': csrf_token,
        'format': 'json'
    }

    response = session.post(api_url, data=params, verify=False)
    response_data = response.json()

    if response.status_code == 200 and 'success' in response_data:
        print(f"Qualifier added successfully to claim {claim_id}.")
    else:
        print(f"Failed to add qualifier: {response_data}")

# Function to update an existing qualifier
def update_qualifier(session, csrf_token, claim_id, qualifier_id, qualifier_property, qualifier_value):
    params = {
        'action': 'wbsetqualifier',
        'claim': claim_id,
        'qualifier': qualifier_id,
        'property': qualifier_property,
        'value': json.dumps(qualifier_value),
        'snaktype': 'value',
        'token': csrf_token,
        'format': 'json'
    }

    response = session.post(api_url, data=params, verify=False)
    response_data = response.json()

    if response.status_code == 200 and 'success' in response_data:
        print(f"Qualifier updated successfully for claim {claim_id}.")
    else:
        print(f"Failed to update qualifier: {response_data}")

# Function to get the GeoNames ID from the JSON based on relatedField
def get_geoname_id_from_json(person_data, related_field):
    related_places = person_data.get('related-places', [])
    
    # Debugging: Print the related places to ensure data structure
    print(f"Related Places: {json.dumps(related_places, indent=4)}")
    
    for place in related_places:
        if place['relatedField'] == related_field:
            geoname_id = place.get('geonameId')
            if geoname_id:
                return geoname_id
            else:
                return 0  # Return 0 if no geonameId is available
    return 0  # Return 0 if the related field doesn't exist

# Function to add or update qualifier to a specific entity and property
def add_qualifier_to_entity(session, csrf_token, entity_id, person_data, property_to_related_field):
    entity_data = get_entity_data(session, entity_id)

    if not entity_data:
        print(f"Failed to retrieve data for entity {entity_id}.")
        return

    claims = entity_data.get('claims', {})

    for prop_id, related_field in property_to_related_field.items():
        if prop_id in claims:
            qualifier_value = get_geoname_id_from_json(person_data, related_field)
            
            for claim in claims[prop_id]:
                claim_id = claim['id']
                qualifier_property = "P22"  # GeoNames ID property

                # Check if a qualifier already exists
                exists, existing_qualifier = qualifier_exists(claim, qualifier_property, qualifier_value)

                # Even if qualifier exists, force an update
                if exists:
                    print(f"GeoNames ID already exists for claim {claim_id}. Updating...")
                    update_qualifier(session, csrf_token, claim_id, existing_qualifier['id'], qualifier_property, qualifier_value)
                else:
                    # Add the GeoNames ID qualifier if it doesn't exist
                    if qualifier_value != 0:
                        add_qualifier(session, csrf_token, claim_id, qualifier_property, qualifier_value)
                    else:
                        print(f"No GeoNames ID found for related field '{related_field}'. Skipping.")
        else:
            print(f"No claims found for property {prop_id} in entity {entity_id}. Skipping.")

# Main script to process the specific entity's JSON and add or update qualifiers
def process_entity(entity_id, json_file_path):
    if not os.path.exists(json_file_path):
        print(f"File {json_file_path} does not exist. Skipping.")
        return
    
    session = login_to_wikibase()
    csrf_token = get_csrf_token(session)

    with open(json_file_path, "r", encoding="utf-8") as file:
        person_data = json.load(file)
        add_qualifier_to_entity(session, csrf_token, entity_id, person_data, property_to_related_field)

# Example usage: process all entities using the entity_file_mapping dictionary
for entity_id, json_file_path in entity_file_mapping.items():
    process_entity(entity_id, json_file_path)

Entity Data for Q1:
{
    "type": "item",
    "id": "Q1",
    "claims": {
        "P4": [
            {
                "mainsnak": {
                    "snaktype": "value",
                    "property": "P4",
                    "hash": "148716f96a9ad503ae678e4f167bd9a41fa16b75",
                    "datavalue": {
                        "value": "Unknown",
                        "type": "string"
                    },
                    "datatype": "string"
                },
                "type": "statement",
                "id": "Q1$2B2DA790-A9E5-43EB-98E8-E03F765CD7D6",
                "rank": "normal"
            }
        ],
        "P5": [
            {
                "mainsnak": {
                    "snaktype": "value",
                    "property": "P5",
                    "hash": "133e8fc5fe65d1b9b543b01df0cb9db8ec9c0632",
                    "datavalue": {
                        "value": {
                            "time": "+1927-05-26T00:00:00Z",
          

KeyboardInterrupt: 

### adding Geonames as Qualifiers

In [274]:
import os
import requests
import json
import time
import logging

# Disable SSL warnings (for testing purposes)
requests.packages.urllib3.disable_warnings(requests.packages.urllib3.exceptions.InsecureRequestWarning)

# Logging setup
logging.basicConfig(level=logging.INFO, format="%(asctime)s - %(levelname)s - %(message)s")

# API credentials and endpoints
api_url = "https://wikibase.example.com/w/api.php"
USERNAME = "admin"
PASSWORD = "change-this-password"
input_directory = "/Users/ismail.ahouari/Public/wikibase-release-pipeline/deploy/reecords/"

# Property mappings
PROPERTY_ID_ENTITY = "P26"  # Entity ID property
QUALIFIER_PROPERTY_ID = "P25"  # Qualifier for GeoNames ID
property_to_related_field = {
    "P6": "birth_place",
    "P7": "death_place",
    "P8": "nationality",
    "P9": "birth_country",
    "P11": "death_place_alt",
    "P12": "death_country",
    "P15": "convoy_place",
    "P18": "exit_place_1940_1941",
    "P19": "exit_place_1941_1944"
}

# Function to log in to Wikibase
def login_to_wikibase():
    session = requests.Session()
    params = {"action": "query", "meta": "tokens", "type": "login", "format": "json"}
    response = session.get(api_url, params=params, verify=False)
    if response.status_code == 200:
        login_token = response.json()['query']['tokens']['logintoken']
        login_params = {
            "action": "clientlogin",
            "username": USERNAME,
            "password": PASSWORD,
            "logintoken": login_token,
            "loginreturnurl": api_url,
            "format": "json"
        }
        login_response = session.post(api_url, data=login_params, verify=False)
        if login_response.status_code == 200:
            logging.info("Logged in successfully")
            return session
    logging.error("Login failed")
    return None

# Function to get CSRF token
def get_csrf_token(session):
    params = {"action": "query", "meta": "tokens", "type": "csrf", "format": "json"}
    response = session.get(api_url, params=params, verify=False)
    if response.status_code == 200:
        return response.json()['query']['tokens']['csrftoken']
    logging.error("Failed to retrieve CSRF token")
    return None

# Function to retrieve all entities with their "Entity ID" (P26) values with debugging
def get_entities_with_slugs(session):
    entities_with_slugs = {}
    continue_param = None
    while True:
        params = {
            "action": "query",
            "list": "allpages",
            "apnamespace": 0,
            "aplimit": 50,
            "format": "json"
        }
        if continue_param:
            params["apcontinue"] = continue_param
        response = session.get(api_url, params=params, verify=False)
        if response.status_code == 200:
            data = response.json()
            for page in data["query"]["allpages"]:
                entity_id = f"Q{page['pageid']}"
                entity_data = get_entity_data(session, entity_id)
                slug = get_statement_value(entity_data, PROPERTY_ID_ENTITY)
                
                # Debugging: Log each entity's slug value
                if slug:
                    logging.info(f"Entity {entity_id} has slug '{slug}'")
                    entities_with_slugs[slug] = entity_id
                else:
                    logging.warning(f"Entity {entity_id} has no 'P26' value. Skipping.")
            if "continue" in data:
                continue_param = data["continue"].get("apcontinue")
            else:
                break
        else:
            logging.error("Failed to retrieve entities. Status code: %s", response.status_code)
            break
    return entities_with_slugs

# Get value of a specific statement
def get_statement_value(entity_data, property_id):
    claims = entity_data.get("claims", {})
    if property_id in claims:
        return claims[property_id][0]["mainsnak"].get("datavalue", {}).get("value")
    return None

# Add qualifiers based on matching JSON file
def add_qualifiers_from_json(session, csrf_token, entity_id, person_data):
    entity_data = get_entity_data(session, entity_id)
    if not entity_data:
        logging.error(f"Failed to retrieve data for entity {entity_id}")
        return
    claims = entity_data.get("claims", {})
    for prop_id, related_field in property_to_related_field.items():
        if prop_id in claims:
            geoname_id = get_geoname_id_from_json(person_data, related_field)
            for claim in claims[prop_id]:
                claim_id = claim['id']
                if geoname_id and not qualifier_exists(claim, QUALIFIER_PROPERTY_ID, geoname_id):
                    add_qualifier(session, csrf_token, claim_id, QUALIFIER_PROPERTY_ID, geoname_id)

# Additional functions: add_qualifier, get_geoname_id_from_json, etc.
# (same as previously shared)

# Main function with retry and logging
def process_all_entities():
    session = login_to_wikibase()
    if not session:
        logging.error("Unable to initiate session")
        return
    csrf_token = get_csrf_token(session)
    if not csrf_token:
        logging.error("Unable to retrieve CSRF token")
        return

    entities_with_slugs = get_entities_with_slugs(session)
        for filename in os.listdir(input_directory):
            if filename.endswith(".json"):
                file_path = os.path.join(input_directory, filename)
                with open(file_path, "r", encoding="utf-8") as file:
                    person_data = json.load(file)
                    slug = person_data.get("slug")
                    entity_id = entities_with_slugs.get(slug)
                    if entity_id:
                        logging.info(f"Processing {filename} for entity {entity_id}")
                        add_qualifiers_from_json(session, csrf_token, entity_id, person_data)
                        time.sleep(5)  # Adjust delay for rate limiting
                    else:
                        logging.warning(f"No matching entity for slug '{slug}' found in {filename}. Skipping.")

if __name__ == "__main__":
    process_all_entities()

2024-10-25 14:13:36,404 - INFO - Logged in successfully
2024-10-25 14:13:36,556 - INFO - Entity Q1 has slug 'mayer-kurt-josef'
2024-10-25 14:13:36,558 - WARNING - No matching entity for slug 'dura-margarete' found in dura-margarete.json. Skipping.
2024-10-25 14:13:36,558 - WARNING - No matching entity for slug 'rothschild-elisabeth' found in rothschild-elisabeth.json. Skipping.
2024-10-25 14:13:36,559 - WARNING - No matching entity for slug 'rosenthal-rozenthal-albert-aron-abraham' found in rosenthal-rozenthal-albert-aron-abraham.json. Skipping.
2024-10-25 14:13:36,560 - WARNING - No matching entity for slug 'herrmann-robert' found in herrmann-robert.json. Skipping.
2024-10-25 14:13:36,561 - WARNING - No matching entity for slug 'wonagus-joseph' found in wonagus-joseph.json. Skipping.
2024-10-25 14:13:36,562 - WARNING - No matching entity for slug 'rudow-rudovs-elie-khonon-dit-hans' found in rudow-rudovs-elie-khonon-dit-hans.json. Skipping.
2024-10-25 14:13:36,562 - WARNING - No matchi

Failed to add qualifier to claim Q1$21C87E7A-A01B-4D23-9F6B-43B7ACC53765.
Failed to add qualifier to claim Q1$71ABA085-7C84-4D84-B267-E821130EDF18.
Failed to add qualifier to claim Q1$EEB78BDB-DF23-47D1-8796-54A4FDBCF987.


2024-10-25 14:13:41,759 - WARNING - No matching entity for slug 'salomon-joseph-bruno' found in salomon-joseph-bruno.json. Skipping.
2024-10-25 14:13:41,763 - WARNING - No matching entity for slug 'nath-natt-leib-lejb-lejba' found in nath-natt-leib-lejb-lejba.json. Skipping.
2024-10-25 14:13:41,764 - WARNING - No matching entity for slug 'kahn-ludwig' found in kahn-ludwig.json. Skipping.
2024-10-25 14:13:41,765 - WARNING - No matching entity for slug 'levy-rebecca-dite-rely' found in levy-rebecca-dite-rely.json. Skipping.
2024-10-25 14:13:41,766 - WARNING - No matching entity for slug 'schupak-bluma' found in schupak-bluma.json. Skipping.
2024-10-25 14:13:41,767 - WARNING - No matching entity for slug 'rachel-geller-rachela-geller' found in rachel-geller-rachela-geller.json. Skipping.
2024-10-25 14:13:41,767 - WARNING - No matching entity for slug 'deutscher-rachel-ryfka' found in deutscher-rachel-ryfka.json. Skipping.
2024-10-25 14:13:41,768 - WARNING - No matching entity for slug 'sc

# HERE


In [280]:
import os
import requests
import json
import time
import logging

# Disable SSL warnings (for testing purposes)
requests.packages.urllib3.disable_warnings(requests.packages.urllib3.exceptions.InsecureRequestWarning)

# Logging setup
logging.basicConfig(level=logging.INFO, format="%(asctime)s - %(levelname)s - %(message)s")

# API credentials and endpoints
api_url = "https://wikibase.example.com/w/api.php"
USERNAME = "admin"
PASSWORD = "change-this-password"
input_directory = "/Users/ismail.ahouari/Public/wikibase-release-pipeline/deploy/reecords/"

# Property mappings
PROPERTY_ID_ENTITY = "P26"  # Entity ID property
QUALIFIER_PROPERTY_ID = "P25"  # Qualifier for GeoNames ID
property_to_related_field = {
    "P6": "birth_place",
    "P7": "death_place",
    "P8": "nationality",
    "P9": "birth_country",
    "P11": "death_place_alt",
    "P12": "death_country",
    "P15": "convoy_place",
    "P18": "exit_place_1940_1941",
    "P19": "exit_place_1941_1944"
}

# Function to log in to Wikibase
def login_to_wikibase():
    session = requests.Session()
    params = {"action": "query", "meta": "tokens", "type": "login", "format": "json"}
    response = session.get(api_url, params=params, verify=False)
    if response.status_code == 200:
        login_token = response.json()['query']['tokens']['logintoken']
        login_params = {
            "action": "clientlogin",
            "username": USERNAME,
            "password": PASSWORD,
            "logintoken": login_token,
            "loginreturnurl": api_url,
            "format": "json"
        }
        login_response = session.post(api_url, data=login_params, verify=False)
        if login_response.status_code == 200:
            logging.info("Logged in successfully")
            return session
    logging.error("Login failed")
    return None

# Function to get CSRF token
def get_csrf_token(session):
    params = {"action": "query", "meta": "tokens", "type": "csrf", "format": "json"}
    response = session.get(api_url, params=params, verify=False)
    if response.status_code == 200:
        return response.json()['query']['tokens']['csrftoken']
    logging.error("Failed to retrieve CSRF token")
    return None

# Retrieve all entities with their "Entity ID" (P26) values with debugging
def get_entities_with_slugs(session):
    entities_with_slugs = {}
    continue_param = None
    while True:
        params = {
            "action": "query",
            "list": "allpages",
            "apnamespace": 120,
            "aplimit": 50,
            "format": "json"
        }
        if continue_param:
            params["apcontinue"] = continue_param
        response = session.get(api_url, params=params, verify=False)
        if response.status_code == 200:
            data = response.json()
            for page in data["query"]["allpages"]:
                entity_id = f"Q{page['pageid']}"
                entity_data = get_entity_data(session, entity_id)
                slug = get_statement_value(entity_data, PROPERTY_ID_ENTITY)
                
                # Debugging: Log each entity's slug value
                if slug:
                    logging.info(f"Entity {entity_id} has slug '{slug}'")
                    entities_with_slugs[slug] = entity_id
                else:
                    logging.warning(f"Entity {entity_id} has no 'P26' value. Skipping.")
            if "continue" in data:
                continue_param = data["continue"].get("apcontinue")
            else:
                break
        else:
            logging.error("Failed to retrieve entities. Status code: %s", response.status_code)
            break
    return entities_with_slugs

# Helper function to get the value of a specific statement
def get_statement_value(entity_data, property_id):
    claims = entity_data.get("claims", {})
    if property_id in claims:
        return claims[property_id][0]["mainsnak"].get("datavalue", {}).get("value")
    return None

# Function to retrieve GeoNames ID based on relatedField
def get_geoname_id_from_json(person_data, related_field):
    related_places = person_data.get("related-places", [])
    for place in related_places:
        if place['relatedField'] == related_field:
            return place.get('geonameId')
    return None

# Function to add qualifiers based on matching JSON file
def add_qualifiers_from_json(session, csrf_token, entity_id, person_data):
    entity_data = get_entity_data(session, entity_id)
    if not entity_data:
        logging.error(f"Failed to retrieve data for entity {entity_id}")
        return
    claims = entity_data.get("claims", {})
    for prop_id, related_field in property_to_related_field.items():
        if prop_id in claims:
            geoname_id = get_geoname_id_from_json(person_data, related_field)
            for claim in claims[prop_id]:
                claim_id = claim['id']
                if geoname_id and not qualifier_exists(claim, QUALIFIER_PROPERTY_ID, geoname_id):
                    add_qualifier(session, csrf_token, claim_id, QUALIFIER_PROPERTY_ID, geoname_id)

# Check if a qualifier already exists
def qualifier_exists(claim, qualifier_property, qualifier_value):
    qualifiers = claim.get("qualifiers", {}).get(qualifier_property, [])
    return any(qualifier.get("datavalue", {}).get("value") == qualifier_value for qualifier in qualifiers)

def process_all_entities():
    session = login_to_wikibase()
    if not session:
        logging.error("Unable to initiate session")
        return
    csrf_token = get_csrf_token(session)
    if not csrf_token:
        logging.error("Unable to retrieve CSRF token")
        return

    entities_with_slugs = get_entities_with_slugs(session)
    
    # Log the complete mapping of slugs to entity IDs for debugging
    logging.info(f"Retrieved entities with slugs: {json.dumps(entities_with_slugs, indent=2)}")
    
    for filename in os.listdir(input_directory):
        if filename.endswith(".json"):
            file_path = os.path.join(input_directory, filename)
            with open(file_path, "r", encoding="utf-8") as file:
                # Load JSON data and access the slug at the root level
                person_data = json.load(file)
                slug = person_data.get("slug", "unknown")
                
                # Log the slug value and filename
                logging.info(f"Processing file: {filename} with slug: {slug}")

                # Continue processing if entity is found
                entity_id = entities_with_slugs.get(slug)
                if entity_id:
                    logging.info(f"Processing {filename} for entity {entity_id}")
                    add_qualifiers_from_json(session, csrf_token, entity_id, person_data)
                    time.sleep(5)  # Adjust delay for rate limiting
                else:
                    # Log a warning with details when no match is found
                    logging.warning(f"No matching entity for slug '{slug}' found in {filename}. Skipping.")

if __name__ == "__main__":
    process_all_entities()

2024-10-25 14:37:10,441 - INFO - Logged in successfully
2024-10-25 14:37:10,526 - WARNING - Entity Q22 has no 'P26' value. Skipping.
2024-10-25 14:37:10,552 - WARNING - Entity Q31 has no 'P26' value. Skipping.
2024-10-25 14:37:10,595 - WARNING - Entity Q121 has no 'P26' value. Skipping.
2024-10-25 14:37:10,620 - WARNING - Entity Q122 has no 'P26' value. Skipping.
2024-10-25 14:37:10,646 - WARNING - Entity Q123 has no 'P26' value. Skipping.
2024-10-25 14:37:10,675 - WARNING - Entity Q124 has no 'P26' value. Skipping.
2024-10-25 14:37:10,699 - WARNING - Entity Q125 has no 'P26' value. Skipping.
2024-10-25 14:37:10,722 - WARNING - Entity Q126 has no 'P26' value. Skipping.
2024-10-25 14:37:10,748 - WARNING - Entity Q127 has no 'P26' value. Skipping.
2024-10-25 14:37:10,773 - WARNING - Entity Q128 has no 'P26' value. Skipping.
2024-10-25 14:37:10,797 - WARNING - Entity Q129 has no 'P26' value. Skipping.
2024-10-25 14:37:10,831 - WARNING - Entity Q130 has no 'P26' value. Skipping.
2024-10-25

KeyboardInterrupt: 

In [282]:
import os
import requests
import json
import time
import logging

# Disable SSL warnings (for testing purposes)
requests.packages.urllib3.disable_warnings(requests.packages.urllib3.exceptions.InsecureRequestWarning)

# Logging setup
logging.basicConfig(level=logging.INFO, format="%(asctime)s - %(levelname)s - %(message)s")

# API credentials and endpoints
api_url = "https://wikibase.example.com/w/api.php"
USERNAME = "admin"
PASSWORD = "change-this-password"
input_directory = "/Users/ismail.ahouari/Public/wikibase-release-pipeline/deploy/reecords/"

# Property mappings
PROPERTY_ID_ENTITY = "P26"  # Entity ID property
QUALIFIER_PROPERTY_ID = "P25"  # Qualifier for GeoNames ID
property_to_related_field = {
    "P6": "birth_place",
    "P7": "death_place",
    "P8": "nationality",
    "P9": "birth_country",
    "P11": "death_place_alt",
    "P12": "death_country",
    "P15": "convoy_place",
    "P18": "exit_place_1940_1941",
    "P19": "exit_place_1941_1944"
}

# Function to log in to Wikibase
def login_to_wikibase():
    session = requests.Session()
    params = {"action": "query", "meta": "tokens", "type": "login", "format": "json"}
    response = session.get(api_url, params=params, verify=False)
    if response.status_code == 200:
        login_token = response.json()['query']['tokens']['logintoken']
        login_params = {
            "action": "clientlogin",
            "username": USERNAME,
            "password": PASSWORD,
            "logintoken": login_token,
            "loginreturnurl": api_url,
            "format": "json"
        }
        login_response = session.post(api_url, data=login_params, verify=False)
        if login_response.status_code == 200:
            logging.info("Logged in successfully")
            return session
    logging.error("Login failed")
    return None

# Function to get CSRF token
def get_csrf_token(session):
    params = {"action": "query", "meta": "tokens", "type": "csrf", "format": "json"}
    response = session.get(api_url, params=params, verify=False)
    if response.status_code == 200:
        return response.json()['query']['tokens']['csrftoken']
    logging.error("Failed to retrieve CSRF token")
    return None

# Retrieve all entities with their "Entity ID" (P26) values with debugging
def get_entities_with_slugs(session):
    entities_with_slugs = {}
    continue_param = None
    while True:
        params = {
            "action": "query",
            "list": "allpages",
            "apnamespace": 0,
            "aplimit": 50,
            "format": "json"
        }
        if continue_param:
            params["apcontinue"] = continue_param
        response = session.get(api_url, params=params, verify=False)
        if response.status_code == 200:
            data = response.json()
            for page in data["query"]["allpages"]:
                entity_id = f"Q{page['pageid']}"
                entity_data = get_entity_data(session, entity_id)
                slug = get_statement_value(entity_data, PROPERTY_ID_ENTITY)
                
                # Debugging: Log each entity's slug value
                if slug:
                    logging.info(f"Entity {entity_id} has slug '{slug}'")
                    entities_with_slugs[slug] = entity_id
                else:
                    logging.warning(f"Entity {entity_id} has no 'P26' value. Skipping.")
            if "continue" in data:
                continue_param = data["continue"].get("apcontinue")
            else:
                break
        else:
            logging.error("Failed to retrieve entities. Status code: %s", response.status_code)
            break
    return entities_with_slugs

# Helper function to get the value of a specific statement
def get_statement_value(entity_data, property_id):
    claims = entity_data.get("claims", {})
    if property_id in claims:
        return claims[property_id][0]["mainsnak"].get("datavalue", {}).get("value")
    return None

# Function to retrieve GeoNames ID based on relatedField
def get_geoname_id_from_json(person_data, related_field):
    related_places = person_data.get("related-places", [])
    for place in related_places:
        if place['relatedField'] == related_field:
            return place.get('geonameId')
    return None

# Function to add qualifiers based on matching JSON file with added debugging
def add_qualifiers_from_json(session, csrf_token, entity_id, person_data):
    entity_data = get_entity_data(session, entity_id)
    if not entity_data:
        logging.error(f"Failed to retrieve data for entity {entity_id}")
        return

    logging.info(f"Retrieved data for entity {entity_id}: {json.dumps(entity_data, indent=2)}")
    
    claims = entity_data.get("claims", {})
    for prop_id, related_field in property_to_related_field.items():
        if prop_id in claims:
            logging.info(f"Processing property {prop_id} for entity {entity_id}")

            # Retrieve GeoNames ID based on related field
            geoname_id = get_geoname_id_from_json(person_data, related_field)
            if not geoname_id:
                logging.warning(f"No GeoNames ID found for related field '{related_field}' in entity {entity_id}. Skipping.")
                continue

            for claim in claims[prop_id]:
                claim_id = claim['id']
                logging.info(f"Checking qualifiers for claim {claim_id} of property {prop_id} on entity {entity_id}")

                # Check if qualifier already exists
                if qualifier_exists(claim, QUALIFIER_PROPERTY_ID, geoname_id):
                    logging.info(f"Qualifier with GeoNames ID '{geoname_id}' already exists for claim {claim_id}. Skipping.")
                else:
                    # Log attempt to add a new qualifier
                    logging.info(f"Adding qualifier with GeoNames ID '{geoname_id}' to claim {claim_id} for property {prop_id}")
                    add_qualifier(session, csrf_token, claim_id, QUALIFIER_PROPERTY_ID, geoname_id)

# Function to add a qualifier to a specific claim
def add_qualifier(session, csrf_token, claim_id, qualifier_property_id, qualifier_value):
    params = {
        "action": "wbsetqualifier",
        "claim": claim_id,
        "property": qualifier_property_id,
        "value": json.dumps({"entity-type": "string", "numeric-id": qualifier_value}),
        "token": csrf_token,
        "format": "json"
    }
    response = session.post(api_url, data=params, verify=False)
    if response.status_code == 200:
        logging.info(f"Qualifier {qualifier_property_id} with value {qualifier_value} added to claim {claim_id}")
    else:
        logging.error(f"Failed to add qualifier {qualifier_property_id} with value {qualifier_value} to claim {claim_id}")

# Check if a qualifier already exists
def qualifier_exists(claim, qualifier_property, qualifier_value):
    qualifiers = claim.get("qualifiers", {}).get(qualifier_property, [])
    return any(qualifier.get("datavalue", {}).get("value") == qualifier_value for qualifier in qualifiers)

def process_all_entities():
    session = login_to_wikibase()
    if not session:
        logging.error("Unable to initiate session")
        return
    csrf_token = get_csrf_token(session)
    if not csrf_token:
        logging.error("Unable to retrieve CSRF token")
        return

    entities_with_slugs = get_entities_with_slugs(session)
    
    # Log the complete mapping of slugs to entity IDs for debugging
    logging.info(f"Retrieved entities with slugs: {json.dumps(entities_with_slugs, indent=2)}")
    
    for filename in os.listdir(input_directory):
        if filename.endswith(".json"):
            file_path = os.path.join(input_directory, filename)
            with open(file_path, "r", encoding="utf-8") as file:
                # Load JSON data and access the slug at the root level
                person_data = json.load(file)
                slug = person_data.get("slug", "unknown")
                
                # Log the slug value and filename
                logging.info(f"Processing file: {filename} with slug: {slug}")

                # Continue processing if entity is found
                entity_id = entities_with_slugs.get(slug)
                if entity_id:
                    logging.info(f"Processing {filename} for entity {entity_id}")
                    add_qualifiers_from_json(session, csrf_token, entity_id, person_data)
                    time.sleep(5)  # Adjust delay for rate limiting
                else:
                    # Log a warning with details when no match is found
                    logging.warning(f"No matching entity for slug '{slug}' found in {filename}. Skipping.")

if __name__ == "__main__":
    process_all_entities()

2024-10-25 14:44:38,359 - INFO - Logged in successfully
2024-10-25 14:44:38,439 - INFO - Entity Q1 has slug 'mayer-kurt-josef'
2024-10-25 14:44:38,440 - INFO - Retrieved entities with slugs: {
  "mayer-kurt-josef": "Q1"
}
2024-10-25 14:44:38,442 - INFO - Processing file: dura-margarete.json with slug: dura-margarete
2024-10-25 14:44:38,442 - WARNING - No matching entity for slug 'dura-margarete' found in dura-margarete.json. Skipping.
2024-10-25 14:44:38,443 - INFO - Processing file: rothschild-elisabeth.json with slug: rothschild-elisabeth
2024-10-25 14:44:38,443 - WARNING - No matching entity for slug 'rothschild-elisabeth' found in rothschild-elisabeth.json. Skipping.
2024-10-25 14:44:38,444 - INFO - Processing file: rosenthal-rozenthal-albert-aron-abraham.json with slug: rosenthal-rozenthal-albert-aron-abraham
2024-10-25 14:44:38,444 - WARNING - No matching entity for slug 'rosenthal-rozenthal-albert-aron-abraham' found in rosenthal-rozenthal-albert-aron-abraham.json. Skipping.
202

In [277]:
import os
import json

# Example directory to save profiles

json_directory = "/Users/ismail.ahouari/Public/wikibase-release-pipeline/deploy/reecords/"




# Counter to track the number of records printed
record_count = 0
max_records = 10

# Loop through each file in the JSON directory
for filename in os.listdir(json_directory):
    if filename.endswith(".json") and record_count < max_records:
        file_path = os.path.join(json_directory, filename)
        
        # Load the JSON data and retrieve the slug
        with open(file_path, "r", encoding="utf-8") as file:
            json_data = json.load(file)
            slug = json_data.get("slug", "unknown")  # Default to 'unknown' if slug is missing
            
            # Print the slug
            print(f"Record {record_count + 1}: {slug}")
            
            # Increment the counter
            record_count += 1

Record 1: dura-margarete
Record 2: rothschild-elisabeth
Record 3: rosenthal-rozenthal-albert-aron-abraham
Record 4: herrmann-robert
Record 5: wonagus-joseph
Record 6: rudow-rudovs-elie-khonon-dit-hans
Record 7: rudow-rudovs-erich
Record 8: borenstein-elsa
Record 9: weinberg-martha
Record 10: steinberger-adolf


In [202]:
import requests
import json
import os
import logging

# Set up logging configuration
logging.basicConfig(level=logging.DEBUG, format='%(asctime)s - %(levelname)s - %(message)s')

# Disable SSL warnings (only for testing)
requests.packages.urllib3.disable_warnings(requests.packages.urllib3.exceptions.InsecureRequestWarning)

# Define the API endpoint and credentials
api_url = "https://wikibase.example.com/w/api.php"
USERNAME = "admin"
PASSWORD = "change-this-password"

# Mapping properties to their related fields in JSON
property_to_related_field = {
    "P6": "birth_place",
    "P7": "death_place",
    "P8": "nationality",
    "P9": "birth_country",
    "P11": "death_place_alt",
    "P12": "death_country",
    "P15": "convoy_place",
    "P18": "exit_place_1940_1941",
    "P19": "exit_place_1941_1944"
}

# Path to the JSON directory
json_directory = "/Users/ismail.ahouari/Public/wikibase-release-pipeline/deploy/reecords"

# Function to log in to Wikibase
def login_to_wikibase():
    logging.info("Attempting to log in to Wikibase...")
    session = requests.Session()

    try:
        params = {
            "action": "query",
            "meta": "tokens",
            "type": "login",
            "format": "json"
        }

        response = session.get(api_url, params=params, verify=False)
        login_token = response.json()['query']['tokens']['logintoken']
        logging.debug(f"Login token received: {login_token}")

        login_params = {
            "action": "clientlogin",
            "username": USERNAME,
            "password": PASSWORD,
            "logintoken": login_token,
            "loginreturnurl": api_url,
            "format": "json"
        }

        response = session.post(api_url, data=login_params, verify=False)
        logging.info("Login successful!")
        return session
    except Exception as e:
        logging.error(f"Failed to log in to Wikibase: {e}")
        return None

# Function to get the CSRF token
def get_csrf_token(session):
    logging.info("Fetching CSRF token...")
    try:
        params = {
            "action": "query",
            "meta": "tokens",
            "type": "csrf",
            "format": "json"
        }

        response = session.get(api_url, params=params, verify=False)
        csrf_token = response.json()['query']['tokens']['csrftoken']
        logging.debug(f"CSRF token: {csrf_token}")
        return csrf_token
    except Exception as e:
        logging.error(f"Failed to get CSRF token: {e}")
        return None

# Function to retrieve all entities (QIDs) from Wikibase, handling pagination
def get_all_entities(session):
    logging.info("Retrieving all entities from Wikibase...")

    entities = {}
    try:
        params = {
            "action": "query",
            "list": "allpages",
            "apnamespace": 120,  # Namespace 120 is for Wikibase items (Q-entities)
            "aplimit": "max",    # Get the maximum number of results per request
            "format": "json"
        }

        while True:
            response = session.get(api_url, params=params, verify=False)
            data = response.json()

            # Retrieve the entities (pages) from the response
            pages = data.get('query', {}).get('allpages', [])
            logging.info(f"Retrieved {len(pages)} entities in this batch.")

            for page in pages:
                qid = page['title']  # This should be the QID (e.g., Q1, Q2, etc.)
                label = page['title']  # You can retrieve the label here if needed
                entities[qid] = label
                logging.debug(f"Entity found: QID: {qid}, Label: {label}")

            # Check if there's more data to retrieve (pagination)
            if 'continue' in data:
                params['apcontinue'] = data['continue']['apcontinue']
                logging.info(f"Continuing to next batch of entities with apcontinue token: {params['apcontinue']}")
            else:
                break  # No more pages to retrieve, exit the loop

        logging.info(f"Total entities retrieved: {len(entities)}")
        return entities

    except Exception as e:
        logging.error(f"Failed to retrieve entities: {e}")
        return {}

# Function to match entities to JSON files by checking if the label matches the JSON filename
def map_entities_to_json(entities, json_directory):
    logging.info("Mapping entities to corresponding JSON files based on labels...")
    entity_to_json_map = {}

    try:
        # List all JSON files in the directory
        json_files = os.listdir(json_directory)
        logging.debug(f"Found {len(json_files)} JSON files in the directory.")

        # Loop through each JSON file in the directory
        for json_file in json_files:
            if json_file.endswith(".json"):
                json_path = os.path.join(json_directory, json_file)

                # Strip the .json extension to get the file name (assuming it's the label)
                file_label = json_file.replace(".json", "").strip().lower()

                # Debugging: Log the current JSON file being processed
                logging.debug(f"Processing JSON file: {json_file}, label extracted: {file_label}")

                # Loop through each entity and check if the label matches the file name
                for qid, label in entities.items():
                    entity_label = label.strip().lower()  # Normalize label for comparison

                    # Debugging: Log the comparison between entity label and file label
                    logging.debug(f"Comparing entity '{label}' (QID: {qid}) with file label '{file_label}'")

                    if entity_label == file_label:
                        entity_to_json_map[qid] = json_path
                        logging.info(f"Mapped entity {qid} with label '{label}' to JSON file {json_file}")
                        break  # Stop looping through entities once a match is found
                else:
                    logging.debug(f"No match found for JSON file: {json_file}")
        
        logging.info(f"Total entities mapped: {len(entity_to_json_map)}")
        return entity_to_json_map
    except Exception as e:
        logging.error(f"Failed to map entities to JSON files: {e}")
        return {}

# Function to retrieve entity data (to get the claims)
def get_entity_data(session, entity_id):
    logging.info(f"Fetching data for entity {entity_id}...")
    try:
        params = {
            "action": "wbgetentities",
            "ids": entity_id,
            "props": "claims",
            "languages": "en",
            "format": "json"
        }

        response = session.get(api_url, params=params, verify=False)
        entity_data = response.json().get('entities', {}).get(entity_id, {})
        
        logging.debug(f"Entity data for {entity_id}: {json.dumps(entity_data, indent=4)}")
        return entity_data
    except Exception as e:
        logging.error(f"Failed to retrieve data for entity {entity_id}: {e}")
        return {}

# Function to check if a qualifier exists
def qualifier_exists(claim, qualifier_property, qualifier_value):
    qualifiers = claim.get('qualifiers', {}).get(qualifier_property, [])
    for qualifier in qualifiers:
        if qualifier.get('datavalue', {}).get('value') == qualifier_value:
            return True
    return False

# Function to add a qualifier to a specific claim
def add_qualifier(session, csrf_token, claim_id, qualifier_property, qualifier_value):
    logging.info(f"Adding qualifier to claim {claim_id}...")
    try:
        qualifier_value = str(qualifier_value)  # Ensure the value is treated as a string

        params = {
            'action': 'wbsetqualifier',
            'claim': claim_id,
            'property': qualifier_property,
            'value': json.dumps(qualifier_value),  # Pass the value directly as a string
            'snaktype': 'value',  # Ensure the snak type is "value"
            'token': csrf_token,
            'format': 'json'
        }

        response = session.post(api_url, data=params, verify=False)
        response_data = response.json()

        if response.status_code == 200 and 'success' in response_data:
            logging.info(f"Qualifier added successfully to claim {claim_id}.")
        else:
            logging.error(f"Failed to add qualifier: {response_data}")
    except Exception as e:
        logging.error(f"Exception while adding qualifier: {e}")

# Function to get the GeoNames ID from the JSON based on relatedField
def get_geoname_id_from_json(person_data, related_field):
    related_places = person_data.get('related-places', [])
    
    for place in related_places:
        if place['relatedField'] == related_field:
            geoname_id = place.get('geonameId')
            return geoname_id if geoname_id else 0

    return 0

def add_qualifier_to_entity(session, csrf_token, entity_id, person_data, property_to_related_field):
    logging.info(f"Processing entity {entity_id} for adding qualifiers...")
    entity_data = get_entity_data(session, entity_id)

    if not entity_data:
        logging.error(f"Failed to retrieve data for entity {entity_id}. Skipping...")
        return

    claims = entity_data.get('claims', {})

    # Loop through all mapped properties and related fields
    for prop_id, related_field in property_to_related_field.items():
        if prop_id in claims:
            # Get the GeoNames ID from the JSON for the related field
            qualifier_value = get_geoname_id_from_json(person_data, related_field)
            
            for claim in claims[prop_id]:
                claim_id = claim['id']
                qualifier_property = "P25"  # GeoNames ID property

                logging.debug(f"Checking if qualifier already exists for claim {claim_id}")
                
                if qualifier_value and not qualifier_exists(claim, qualifier_property, qualifier_value):
                    add_qualifier(session, csrf_token, claim_id, qualifier_property, qualifier_value)
                else:
                    logging.info(f"Qualifier already exists or GeoNames ID is unknown for claim {claim_id}, skipping.")
        else:
            logging.info(f"No claims found for property {prop_id} in entity {entity_id}, skipping.")

# Function to process multiple entities
def process_multiple_entities(entity_to_json_map):
    session = login_to_wikibase()
    if not session:
        logging.error("Session creation failed, cannot process entities.")
        return
    
    csrf_token = get_csrf_token(session)
    if not csrf_token:
        logging.error("Failed to retrieve CSRF token, cannot proceed with entity processing.")
        return

    for entity_id, json_file_path in entity_to_json_map.items():
        try:
            logging.info(f"Processing entity {entity_id} with JSON file {json_file_path}...")
            
            # Read the JSON file for the specific entity
            with open(json_file_path, "r", encoding="utf-8") as file:
                person_data = json.load(file)
                
                # Add qualifiers to the entity based on the mapped properties
                add_qualifier_to_entity(session, csrf_token, entity_id, person_data, property_to_related_field)
        except Exception as e:
            logging.error(f"Error processing entity {entity_id}: {e}")

# Main function to automate the entire process
def automate_process():
    logging.info("Starting the automated process...")
    
    session = login_to_wikibase()
    if not session:
        logging.error("Failed to create a session, exiting...")
        return

    # Step 1: Retrieve all entities (QIDs) from Wikibase
    entities = get_all_entities(session)
    if not entities:
        logging.error("No entities retrieved, exiting...")
        return

    # Step 2: Map entities to their corresponding JSON files
    entity_to_json_map = map_entities_to_json(entities, json_directory)
    if not entity_to_json_map:
        logging.error("No entities were mapped to JSON files, exiting...")
        return

    # Step 3: Process each entity
    process_multiple_entities(entity_to_json_map)

# Call the automation process
automate_process()

2024-10-24 12:25:26,386 - INFO - Starting the automated process...
2024-10-24 12:25:26,404 - INFO - Attempting to log in to Wikibase...
2024-10-24 12:25:27,251 - INFO - Login successful!
2024-10-24 12:25:27,253 - INFO - Retrieving all entities from Wikibase...
2024-10-24 12:25:27,364 - INFO - Retrieved 379 entities in this batch.
2024-10-24 12:25:27,366 - INFO - Total entities retrieved: 379
2024-10-24 12:25:27,367 - INFO - Mapping entities to corresponding JSON files based on labels...
2024-10-24 12:25:27,477 - INFO - Total entities mapped: 0
2024-10-24 12:25:27,478 - ERROR - No entities were mapped to JSON files, exiting...


In [205]:
import requests
import json
import os
import logging

# Set up logging configuration
logging.basicConfig(level=logging.DEBUG, format='%(asctime)s - %(levelname)s - %(message)s')

# Disable SSL warnings (only for testing)
requests.packages.urllib3.disable_warnings(requests.packages.urllib3.exceptions.InsecureRequestWarning)

# Define the API endpoint and credentials
api_url = "https://wikibase.example.com/w/api.php"
USERNAME = "admin"
PASSWORD = "change-this-password"

# Mapping properties to their related fields in JSON
property_to_related_field = {
    "P6": "birth_place",
    "P7": "death_place",
    "P8": "nationality",
    "P9": "birth_country",
    "P11": "death_place_alt",
    "P12": "death_country",
    "P15": "convoy_place",
    "P18": "exit_place_1940_1941",
    "P19": "exit_place_1941_1944"
}

# Path to the JSON directory
json_directory = "/Users/ismail.ahouari/Public/wikibase-release-pipeline/deploy/reecords"

# Function to log in to Wikibase
def login_to_wikibase():
    logging.info("Attempting to log in to Wikibase...")
    session = requests.Session()

    try:
        params = {
            "action": "query",
            "meta": "tokens",
            "type": "login",
            "format": "json"
        }

        response = session.get(api_url, params=params, verify=False)
        login_token = response.json()['query']['tokens']['logintoken']
        logging.debug(f"Login token received: {login_token}")

        login_params = {
            "action": "clientlogin",
            "username": USERNAME,
            "password": PASSWORD,
            "logintoken": login_token,
            "loginreturnurl": api_url,
            "format": "json"
        }

        response = session.post(api_url, data=login_params, verify=False)
        logging.info("Login successful!")
        return session
    except Exception as e:
        logging.error(f"Failed to log in to Wikibase: {e}")
        return None

# Function to get the CSRF token
def get_csrf_token(session):
    logging.info("Fetching CSRF token...")
    try:
        params = {
            "action": "query",
            "meta": "tokens",
            "type": "csrf",
            "format": "json"
        }

        response = session.get(api_url, params=params, verify=False)
        csrf_token = response.json()['query']['tokens']['csrftoken']
        logging.debug(f"CSRF token: {csrf_token}")
        return csrf_token
    except Exception as e:
        logging.error(f"Failed to get CSRF token: {e}")
        return None

# Function to retrieve all entities (Labels only) from Wikibase, handling pagination
def get_all_entities(session):
    logging.info("Retrieving all entity labels from Wikibase...")

    entities = {}
    try:
        params = {
            "action": "query",
            "list": "allpages",
            "apnamespace": 120,  # Namespace 120 is for Wikibase items (Q-entities)
            "aplimit": "max",    # Get the maximum number of results per request
            "format": "json"
        }

        while True:
            response = session.get(api_url, params=params, verify=False)
            data = response.json()

            # Retrieve the entities (pages) from the response
            pages = data.get('query', {}).get('allpages', [])
            logging.info(f"Retrieved {len(pages)} entities in this batch.")

            for page in pages:
                label = page['title']  # Assuming the label is the title
                entities[label] = label  # Store the label as the key
                logging.debug(f"Entity found: Label: {label}")

            # Check if there's more data to retrieve (pagination)
            if 'continue' in data:
                params['apcontinue'] = data['continue']['apcontinue']
                logging.info(f"Continuing to next batch of entities with apcontinue token: {params['apcontinue']}")
            else:
                break  # No more pages to retrieve, exit the loop

        logging.info(f"Total entity labels retrieved: {len(entities)}")
        return entities

    except Exception as e:
        logging.error(f"Failed to retrieve entities: {e}")
        return {}

# Function to match entities (labels only) to JSON files by checking if the label matches the JSON filename
def map_entities_to_json(entities, json_directory):
    logging.info("Mapping entity labels to corresponding JSON files...")
    entity_to_json_map = {}

    try:
        # List all JSON files in the directory
        json_files = os.listdir(json_directory)
        logging.debug(f"Found {len(json_files)} JSON files in the directory.")

        # Loop through each JSON file in the directory
        for json_file in json_files:
            if json_file.endswith(".json"):
                json_path = os.path.join(json_directory, json_file)

                # Strip the .json extension to get the file name (assuming it's the label)
                file_label = json_file
                # Debugging: Log the current JSON file being processed
                logging.debug(f"Processing JSON file: {json_file}, extracted label: {file_label}")

                # Loop through each entity and check if the label matches the file name
                for label in entities.values():
                    entity_label = label  # Normalize label for comparison

                    # Debugging: Log the comparison between entity label and file label
                    logging.debug(f"Comparing entity label '{label}' with file label '{file_label}'")

                    if entity_label == file_label:
                        entity_to_json_map[label] = json_path
                        logging.info(f"Mapped entity label '{label}' to JSON file {json_file}")
                        break  # Stop looping through entities once a match is found
                else:
                    logging.debug(f"No match found for JSON file: {json_file}")
        
        logging.info(f"Total entity labels mapped: {len(entity_to_json_map)}")
        return entity_to_json_map
    except Exception as e:
        logging.error(f"Failed to map entity labels to JSON files: {e}")
        return {}

# Function to retrieve entity data (to get the claims)
def get_entity_data(session, entity_label):
    logging.info(f"Fetching data for entity with label {entity_label}...")
    try:
        params = {
            "action": "wbgetentities",
            "titles": entity_label,  # Retrieve entity by label, not QID
            "props": "claims",
            "languages": "en",
            "format": "json"
        }

        response = session.get(api_url, params=params, verify=False)
        entity_data = response.json().get('entities', {})
        
        logging.debug(f"Entity data for {entity_label}: {json.dumps(entity_data, indent=4)}")
        return entity_data
    except Exception as e:
        logging.error(f"Failed to retrieve data for entity with label {entity_label}: {e}")
        return {}

# Function to process entities and add qualifiers (continuation...)
def add_qualifier_to_entity(session, csrf_token, entity_label, person_data, property_to_related_field):
    logging.info(f"Processing entity with label {entity_label} for adding qualifiers...")
    entity_data = get_entity_data(session, entity_label)

    if not entity_data:
        logging.error(f"Failed to retrieve data for entity with label {entity_label}. Skipping...")
        return

    claims = entity_data.get('claims', {})

    # Loop through all mapped properties and related fields
    for prop_id, related_field in property_to_related_field.items():
        if prop_id in claims:
            # Get the GeoNames ID from the JSON for the related field
            qualifier_value = get_geoname_id_from_json(person_data, related_field)
            
            for claim in claims[prop_id]:
                claim_id = claim['id']
                qualifier_property = "P25"  # GeoNames ID property

                logging.debug(f"Checking if qualifier already exists for claim {claim_id}")
                
                if qualifier_value and not qualifier_exists(claim, qualifier_property, qualifier_value):
                    add_qualifier(session, csrf_token, claim_id, qualifier_property, qualifier_value)
                else:
                    logging.info(f"Qualifier already exists or GeoNames ID is unknown for claim {claim_id}, skipping.")
        else:
            logging.info(f"No claims found for property {prop_id} in entity {entity_label}, skipping.")

# Function to process multiple entities
def process_multiple_entities(entity_to_json_map):
    session = login_to_wikibase()
    if not session:
        logging.error("Session creation failed, cannot process entities.")
        return
    
    csrf_token = get_csrf_token(session)
    if not csrf_token:
        logging.error("Failed to retrieve CSRF token, cannot proceed with entity processing.")
        return

    for entity_label, json_file_path in entity_to_json_map.items():
        try:
            logging.info(f"Processing entity with label {entity_label} using JSON file {json_file_path}...")
                        # Read the JSON file for the specific entity
            with open(json_file_path, "r", encoding="utf-8") as file:
                person_data = json.load(file)
                
                # Add qualifiers to the entity based on the mapped properties
                add_qualifier_to_entity(session, csrf_token, entity_label, person_data, property_to_related_field)
        except Exception as e:
            logging.error(f"Error processing entity with label {entity_label}: {e}")

# Main function to automate the entire process
def automate_process():
    logging.info("Starting the automated process...")
    
    session = login_to_wikibase()
    if not session:
        logging.error("Failed to create a session, exiting...")
        return

    # Step 1: Retrieve all entities (labels) from Wikibase
    entities = get_all_entities(session)
    if not entities:
        logging.error("No entities retrieved, exiting...")
        return

    # Step 2: Map entities (labels) to their corresponding JSON files
    entity_to_json_map = map_entities_to_json(entities, json_directory)
    if not entity_to_json_map:
        logging.error("No entities were mapped to JSON files, exiting...")
        return

    # Step 3: Process each entity
    process_multiple_entities(entity_to_json_map)

# Call the automation process
automate_process()
            
            

2024-10-24 12:35:14,702 - INFO - Starting the automated process...
2024-10-24 12:35:14,702 - INFO - Attempting to log in to Wikibase...
2024-10-24 12:35:15,034 - INFO - Login successful!
2024-10-24 12:35:15,034 - INFO - Retrieving all entity labels from Wikibase...
2024-10-24 12:35:15,060 - INFO - Retrieved 379 entities in this batch.
2024-10-24 12:35:15,061 - INFO - Total entity labels retrieved: 379
2024-10-24 12:35:15,061 - INFO - Mapping entity labels to corresponding JSON files...
2024-10-24 12:35:15,107 - INFO - Total entity labels mapped: 0
2024-10-24 12:35:15,108 - ERROR - No entities were mapped to JSON files, exiting...


In [183]:
import os
import json
import requests
import logging

# Disable SSL warnings (only for testing)
requests.packages.urllib3.disable_warnings(requests.packages.urllib3.exceptions.InsecureRequestWarning)

# Setup logging
logging.basicConfig(level=logging.INFO, format='%(asctime)s - %(levelname)s - %(message)s')

# Define the API endpoint and credentials
api_url = "https://wikibase.example.com/w/api.php"
USERNAME = "admin"
PASSWORD = "change-this-password"

# Mapping properties to their related fields in JSON
property_to_related_field = {
    "P6": "birth_place",
    "P7": "death_place",
    "P8": "nationality",
    "P9": "birth_country",
    "P11": "death_place_alt",
    "P12": "death_country",
    "P15": "convoy_place",
    "P18": "exit_place_1940_1941",
    "P19": "exit_place_1941_1944"
}

# Function to log in to Wikibase
def login_to_wikibase():
    session = requests.Session()
    params = {
        "action": "query",
        "meta": "tokens",
        "type": "login",
        "format": "json"
    }

    response = session.get(api_url, params=params, verify=False)
    login_token = response.json()['query']['tokens']['logintoken']

    login_params = {
        "action": "clientlogin",
        "username": USERNAME,
        "password": PASSWORD,
        "logintoken": login_token,
        "loginreturnurl": api_url,
        "format": "json"
    }

    session.post(api_url, data=login_params, verify=False)
    return session

# Function to get the CSRF token
def get_csrf_token(session):
    params = {
        "action": "query",
        "meta": "tokens",
        "type": "csrf",
        "format": "json"
    }

    response = session.get(api_url, params=params, verify=False)
    return response.json()['query']['tokens']['csrftoken']

# Function to retrieve entity data (to get the claims)
def get_entity_data(session, entity_id):
    logging.info(f"Fetching data for entity {entity_id}...")
    params = {
        "action": "wbgetentities",
        "ids": entity_id,
        "props": "claims",
        "languages": "en",
        "format": "json"
    }

    response = session.get(api_url, params=params, verify=False)
    entity_data = response.json().get('entities', {}).get(entity_id, {})

    if not entity_data:
        logging.error(f"Failed to retrieve data for entity {entity_id}. Response: {response.json()}")

    return entity_data

# Function to check if a qualifier exists
def qualifier_exists(claim, qualifier_property, qualifier_value):
    qualifiers = claim.get('qualifiers', {}).get(qualifier_property, [])
    for qualifier in qualifiers:
        if qualifier.get('datavalue', {}).get('value') == qualifier_value:
            return True
    return False

# Function to add a qualifier to a specific claim
def add_qualifier(session, csrf_token, claim_id, qualifier_property, qualifier_value):
    qualifier_value = str(qualifier_value)
    params = {
        'action': 'wbsetqualifier',
        'claim': claim_id,
        'property': qualifier_property,
        'value': json.dumps(qualifier_value),
        'snaktype': 'value',
        'token': csrf_token,
        'format': 'json'
    }

    response = session.post(api_url, data=params, verify=False)
    response_data = response.json()

    if response.status_code == 200 and 'success' in response_data:
        logging.info(f"Qualifier added successfully to claim {claim_id}.")
    else:
        logging.error(f"Failed to add qualifier to claim {claim_id}. Response: {response_data}")

# Function to get the GeoNames ID from the JSON based on relatedField
def get_geoname_id_from_json(person_data, related_field):
    related_places = person_data.get('related-places', [])
    for place in related_places:
        if place['relatedField'] == related_field:
            geoname_id = place.get('geonameId')
            if geoname_id:
                return geoname_id
            else:
                return 0
    return 0

# Function to add qualifier to a specific entity and property
def add_qualifier_to_entity(session, csrf_token, entity_id, person_data, property_to_related_field):
    entity_data = get_entity_data(session, entity_id)

    if not entity_data:
        logging.error(f"Entity data missing for {entity_id}. Skipping.")
        return

    claims = entity_data.get('claims', {})

    for prop_id, related_field in property_to_related_field.items():
        if prop_id in claims:
            qualifier_value = get_geoname_id_from_json(person_data, related_field)
            for claim in claims[prop_id]:
                claim_id = claim['id']
                qualifier_property = "P25"

                if not qualifier_exists(claim, qualifier_property, qualifier_value):
                    add_qualifier(session, csrf_token, claim_id, qualifier_property, qualifier_value)
                else:
                    logging.info(f"Qualifier already exists for claim {claim_id}. Skipping.")
        else:
            logging.info(f"No claims found for property {prop_id} in entity {entity_id}. Skipping.")

# Main script to process all JSON files in the directory
def process_directory(directory_path):
    session = login_to_wikibase()
    csrf_token = get_csrf_token(session)

    for filename in os.listdir(directory_path):
        if filename.endswith(".json"):
            json_file_path = os.path.join(directory_path, filename)
            try:
                # Extract entity ID (assuming "name-Q181.json" format)
                entity_id = filename.split("-")[1].split(".")[0]
                logging.info(f"Processing file: {filename} for entity: {entity_id}")

                with open(json_file_path, "r", encoding="utf-8") as file:
                    person_data = json.load(file)
                    add_qualifier_to_entity(session, csrf_token, entity_id, person_data, property_to_related_field)
            except (IndexError, KeyError) as e:
                logging.error(f"Failed to extract entity ID from filename {filename}. Error: {e}")
            except json.JSONDecodeError as e:
                logging.error(f"Failed to parse JSON file {filename}. Error: {e}")

# Example usage: process the directory with JSON files
directory_path = "/Users/ismail.ahouari/Public/wikibase-release-pipeline/deploy/reecords"
process_directory(directory_path)

2024-10-24 10:32:13,772 - INFO - Processing file: dura-margarete.json for entity: margarete
2024-10-24 10:32:13,775 - INFO - Fetching data for entity margarete...
2024-10-24 10:32:13,888 - ERROR - Failed to retrieve data for entity margarete. Response: {'error': {'code': 'no-such-entity', 'info': 'Could not find an entity with the ID "margarete".', 'id': 'margarete', 'messages': [{'name': 'wikibase-api-no-such-entity', 'parameters': ['margarete'], 'html': {'*': 'Could not find an entity with the ID "margarete".'}}], '*': 'See https://wikibase.example.com/w/api.php for API usage. Subscribe to the mediawiki-api-announce mailing list at &lt;https://lists.wikimedia.org/postorius/lists/mediawiki-api-announce.lists.wikimedia.org/&gt; for notice of API deprecations and breaking changes.'}}
2024-10-24 10:32:13,889 - ERROR - Entity data missing for margarete. Skipping.
2024-10-24 10:32:13,890 - INFO - Processing file: rothschild-elisabeth.json for entity: elisabeth
2024-10-24 10:32:13,892 - INF

In [188]:
import requests
import time
import random
import logging
import urllib3

# Suppress the InsecureRequestWarning
urllib3.disable_warnings(urllib3.exceptions.InsecureRequestWarning)

# Initialize session
session = requests.Session()
api_url = "https://wikibase.example.com/w/api.php"  # Your Wikibase API URL

# Set up logging
logging.basicConfig(level=logging.INFO, format='%(asctime)s - %(levelname)s - %(message)s')

# Function to get CSRF token (if needed for write operations)
def get_csrf_token():
    try:
        response = session.get(api_url, params={
            "action": "query",
            "meta": "tokens",
            "type": "csrf",
            "format": "json"
        }, verify=False)  # Disable SSL verification
        response.raise_for_status()
        data = response.json()
        return data["query"]["tokens"]["csrftoken"]
    except requests.RequestException as e:
        logging.error(f"Error fetching CSRF token: {e}")
        return None

# Function to get all properties from Wikibase
def get_all_properties():
    properties = []
    apcontinue = None  # For pagination

    while True:
        params = {
            "action": "query",
            "list": "allpages",
            "apnamespace": 120,  # Namespace for properties
            "aplimit": 100,      # Adjust to a reasonable number, e.g., 100 per request
            "format": "json"
        }

        if apcontinue:
            params["apcontinue"] = apcontinue

        try:
            response = session.get(api_url, params=params, verify=False)  # Disable SSL verification
            response.raise_for_status()
            data = response.json()

            # Handle API errors and rate limits
            if "error" in data:
                logging.error(f"API error: {data['error']['info']}")
                break

            # Check if the request was successful
            if "query" in data:
                # Append current batch of properties to the list
                properties.extend(data["query"].get("allpages", []))
            else:
                logging.error(f"Error in response: {data}")
                break

            # Check if there's more data to fetch
            if "continue" in data:
                apcontinue = data["continue"].get("apcontinue")
            else:
                break

            # Adding a random delay to avoid hitting rate limits
            time.sleep(random.uniform(2, 5))  # Increase delay if hitting rate limits

        except requests.RequestException as e:
            logging.error(f"Request error: {e}")
            break

    return properties

def get_info_for_entity(qid):
    params = {
        "action": "wbgetentities",
        "ids": qid,
        "props": "labels|claims|descriptions|aliases",
        "languages": "en",
        "format": "json"
    }

    try:
        response = session.get(api_url, params=params, verify=False)  # Disable SSL verification
        response.raise_for_status()
        data = response.json()

        label = "No label found"
        description = "No description found"
        aliases = []
        claims = {}

        if "entities" in data and qid in data["entities"]:
            entity = data["entities"][qid]

            # Extract label
            if "labels" in entity and "en" in entity["labels"]:
                label = entity["labels"]["en"]["value"]

            # Extract description
            if "descriptions" in entity and "en" in entity["descriptions"]:
                description = entity["descriptions"]["en"]["value"]

            # Extract aliases
            if "aliases" in entity and "en" in entity["aliases"]:
                aliases = [alias["value"] for alias in entity["aliases"]["en"]]

            # Extract all claims
            if "claims" in entity:
                for prop_id, prop_claims in entity["claims"].items():
                    claims[prop_id] = []
                    for claim in prop_claims:
                        value = claim["mainsnak"].get("datavalue", {}).get("value")
                        claims[prop_id].append(value)

        return label, description, aliases, claims

    except requests.RequestException as e:
        logging.error(f"Error fetching entity data for QID {qid}: {e}")
        return "Error", "Error", [], {}

# Main logic
def main():
    # Get the CSRF token (if needed for write operations)
    # csrf_token = get_csrf_token()

    # Retrieve all properties
    properties = get_all_properties()

    # Extract QIDs from the titles
    qids = [prop['title'].replace("Item:", "") for prop in properties]
    # Print total number of entities
    logging.info(f"Total Entities: {len(qids)}")

    # Iterate through each QID and retrieve the label, description, aliases, and claims
    for qid in qids:
        label, description, aliases, claims = get_info_for_entity(qid)
        
        # Print information for each entity
        logging.info(f"QID: {qid}")
        logging.info(f"  Label: {label}")
        logging.info(f"  Description: {description}")
        logging.info(f"  Aliases: {', '.join(aliases)}")
        logging.info(f"  Claims: {claims}")
        logging.info("-" * 40)
        # Adding a delay between entity requests to avoid rate limits
        time.sleep(random.uniform(1, 3))

if __name__ == "__main__":
    main()





2024-10-24 10:46:24,221 - INFO - Total Entities: 379
2024-10-24 10:46:24,257 - INFO - QID: Q1
2024-10-24 10:46:24,257 - INFO -   Label: Rosenthal Ester(a)
2024-10-24 10:46:24,258 - INFO -   Description: Profile of Rosenthal Ester(a)
2024-10-24 10:46:24,258 - INFO -   Aliases: 
2024-10-24 10:46:24,259 - INFO -   Claims: {'P4': ['Unknown'], 'P5': [{'time': '+1927-05-26T00:00:00Z', 'timezone': 0, 'before': 0, 'after': 0, 'precision': 11, 'calendarmodel': 'http://www.wikidata.org/entity/Q1985727'}], 'P16': [{'time': '+1941-10-17T00:00:00Z', 'timezone': 0, 'before': 0, 'after': 0, 'precision': 11, 'calendarmodel': 'http://www.wikidata.org/entity/Q1985727'}], 'P17': [{'time': '+1929-06-16T00:00:00Z', 'timezone': 0, 'before': 0, 'after': 0, 'precision': 11, 'calendarmodel': 'http://www.wikidata.org/entity/Q1985727'}], 'P6': ['Lodz'], 'P9': ['Polen'], 'P10': ['00/09/1942'], 'P7': ['Chelmno'], 'P11': ['Unknown'], 'P12': ['Polen'], 'P13': ['Unknown'], 'P8': ['Polonaise'], 'P14': ['Da 3'], 'P15':

KeyboardInterrupt: 

# Testing SPARQL Querries

### SPARQL endpoint is linked to a Wikibase instance

In [76]:
import requests

sparql_endpoint = "https://wdqs-frontend.example.com/bigdata/namespace/wdq/sparql"
query = """
    SELECT ?property ?propertyLabel WHERE {
        ?property a wikibase:Property .
        SERVICE wikibase:label { bd:serviceParam wikibase:language "[AUTO_LANGUAGE],en". }
    }
    ORDER BY ?property
"""

headers = {
    "Accept": "application/sparql-results+json"
}

response = requests.get(sparql_endpoint, params={'query': query}, headers=headers, verify=False)

if response.status_code == 200:
    results = response.json()
    for result in results["results"]["bindings"]:
        print(f"Property: {result['property']['value']}, Label: {result['propertyLabel']['value']}")
else:
    print(f"Error: {response.status_code} - {response.text}")

Error: 404 - <html>
<head><title>404 Not Found</title></head>
<body>
<center><h1>404 Not Found</h1></center>
<hr><center>nginx/1.27.0</center>
</body>
</html>



In [ ]:
import requests

#sparql_endpoint = "https://wdqs-frontend.example.com/"

#sparql_endpoint = "https://wdqs-frontend.example.com/sparql"
sparql_endpoint = "https://wdqs-frontend.example.com/query"
query = """
    SELECT ?property ?propertyLabel WHERE {
        ?property a wikibase:Property .
        SERVICE wikibase:label { bd:serviceParam wikibase:language "[AUTO_LANGUAGE],en". }
    }
    ORDER BY ?property
"""

headers = {
    "Accept": "application/sparql-results+json"
}

response = requests.get(sparql_endpoint, params={'query': query}, headers=headers, verify=False)

print(response.text)  # Print the raw response to see what's being returned

if response.status_code == 200:
    try:
        results = response.json()
        for result in results["results"]["bindings"]:
            print(f"Property: {result['property']['value']}, Label: {result['propertyLabel']['value']}")
    except requests.exceptions.JSONDecodeError:
        print("Error: Received response is not in JSON format.")
else:
    print(f"Error: {response.status_code} - {response.text}")



<html>
<head><title>404 Not Found</title></head>
<body>
<center><h1>404 Not Found</h1></center>
<hr><center>nginx/1.27.0</center>
</body>
</html>

Error: 404 - <html>
<head><title>404 Not Found</title></head>
<body>
<center><h1>404 Not Found</h1></center>
<hr><center>nginx/1.27.0</center>
</body>
</html>

